In [1]:
import afqinsight.nn.tf_models as nn
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
from afqinsight.datasets import AFQDataset
from afqinsight.nn.tf_models import cnn_lenet, mlp4, cnn_vgg, lstm1v0, lstm1, lstm2, blstm1, blstm2, lstm_fcn, cnn_resnet
from sklearn.impute import SimpleImputer
import os.path
# Harmonization
from sklearn.model_selection import train_test_split
from neurocombat_sklearn import CombatModel
import pandas as pd

In [2]:
afq_dataset = AFQDataset.from_files(
    fn_nodes="../data/raw/combined_tract_profiles.csv",
    fn_subjects="../data/raw/participants_updated_id.csv",
    dwi_metrics=["dki_fa", "dki_md", "dki_mk"],
    index_col="subject_id",
    target_cols=["age", "dl_qc_score", "scan_site_id"],
    label_encode_cols=["scan_site_id"]
)

In [3]:
afq_dataset.drop_target_na()

In [4]:
print(len(afq_dataset.subjects))
print(afq_dataset.X.shape)
print(afq_dataset.y.shape)

1865
(1865, 7200)
(1865, 3)


In [5]:
full_dataset = list(afq_dataset.as_tensorflow_dataset().as_numpy_iterator())

2022-04-27 10:39:24.997007: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [6]:
X = np.concatenate([xx[0][None] for xx in full_dataset], 0)
y = np.array([yy[1][0] for yy in full_dataset])
qc = np.array([yy[1][1] for yy in full_dataset])
site = np.array([yy[1][2] for yy in full_dataset])

In [7]:
X = X[qc>0]
y = y[qc>0]
site = site[qc>0]

In [8]:
# # Split the data by sites
# X_0 = X[site==0]
# y_0 = y[site==0]
# X_3 = X[site==3]
# y_3 = y[site==3]
# X_4 = X[site==4]
# y_4 = y[site==4]

In [9]:
# # Split the data into train and test sets:
# X_0_train, X_0_test, y_0_train, y_0_test = train_test_split(X_0, y_0, test_size=0.2, random_state=42)
# X_3_train, X_3_test, y_3_train, y_3_test = train_test_split(X_3, y_3, test_size=0.2, random_state=42)
# X_4_train, X_4_test, y_4_train, y_4_test = train_test_split(X_4, y_4, test_size=0.2, random_state=42)

In [10]:
# imputer = SimpleImputer(strategy="median")

In [11]:
# # Impute train and test separately:
# X_0_train = np.concatenate([imputer.fit_transform(X_0_train[..., ii])[:, :, None] for ii in range(X_0_train.shape[-1])], -1)
# X_0_test = np.concatenate([imputer.fit_transform(X_0_test[..., ii])[:, :, None] for ii in range(X_0_test.shape[-1])], -1)
# X_3_train = np.concatenate([imputer.fit_transform(X_3_train[..., ii])[:, :, None] for ii in range(X_3_train.shape[-1])], -1)
# X_3_test = np.concatenate([imputer.fit_transform(X_3_test[..., ii])[:, :, None] for ii in range(X_3_test.shape[-1])], -1)
# X_4_train = np.concatenate([imputer.fit_transform(X_4_train[..., ii])[:, :, None] for ii in range(X_4_train.shape[-1])], -1)
# X_4_test = np.concatenate([imputer.fit_transform(X_4_test[..., ii])[:, :, None] for ii in range(X_4_test.shape[-1])], -1)

In [8]:
n_epochs = 1000

# EarlyStopping
early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor="val_loss",
    min_delta=0.001,
    mode="min",
    patience=100
)

# ReduceLROnPlateau
reduce_lr = tf.keras.callbacks.ReduceLROnPlateau(
    monitor="val_loss",
    factor=0.5,
    patience=20,
    verbose=1,
)

In [69]:
# Generate evaluation results and correlation coeffcients combined in a dataframe, and history
def single_cross_site(model_name, name_str, ckpt_filepath, lr,
                      site_1, site_2, site_3, X, y):
    # Split the data by sites
    X_1 = X[site==site_1]
    y_1 = y[site==site_1]
    X_2 = X[site==site_2]
    y_2 = y[site==site_2]
    X_3 = X[site==site_3]
    y_3 = y[site==site_3]
    # Split the data into train and test sets:
    X_train, X_test1, y_train, y_test1 = train_test_split(X_1, y_1, test_size=0.2)
    _, X_test2, _, y_test2 = train_test_split(X_2, y_2, test_size=0.2)
    _, X_test3, _, y_test3 = train_test_split(X_3, y_3, test_size=0.2)
    imputer = SimpleImputer(strategy="median")
    # Impute train and test separately:
    X_train = np.concatenate([imputer.fit_transform(X_train[..., ii])[:, :, None] for ii in range(X_train.shape[-1])], -1)
    X_test1 = np.concatenate([imputer.fit_transform(X_test1[..., ii])[:, :, None] for ii in range(X_test1.shape[-1])], -1)
    X_test2 = np.concatenate([imputer.fit_transform(X_test2[..., ii])[:, :, None] for ii in range(X_test2.shape[-1])], -1)
    X_test3 = np.concatenate([imputer.fit_transform(X_test3[..., ii])[:, :, None] for ii in range(X_test3.shape[-1])], -1)
    model = model_name(input_shape=(100, 72), n_classes=1, output_activation=None, verbose=True)
    model.compile(loss='mean_squared_error',
                  optimizer=tf.keras.optimizers.Adam(learning_rate=lr),
                  metrics=['mean_squared_error', 
                           tf.keras.metrics.RootMeanSquaredError(name='rmse'), 
                           'mean_absolute_error'])
    # ModelCheckpoint
    ckpt = tf.keras.callbacks.ModelCheckpoint(
    ckpt_filepath,
    monitor="val_loss",
    verbose=1,
    save_best_only=True,
    save_weights_only=True,
    mode="auto",
    )
    # CSVLogger
    log = tf.keras.callbacks.CSVLogger(filename=(name_str + '.csv'), append=True)
    callbacks = [early_stopping, ckpt, reduce_lr, log]
    history = model.fit(X_train, y_train, epochs=n_epochs, batch_size=128, validation_split=0.2,
                        callbacks=callbacks)
    model.load_weights(ckpt_filepath)
    y_predicted1 = model.predict(X_test1)
    y_predicted1 = y_predicted1.reshape(y_test1.shape)
    y_predicted2 = model.predict(X_test2)
    y_predicted2 = y_predicted2.reshape(y_test2.shape)
    y_predicted3 = model.predict(X_test3)
    y_predicted3 = y_predicted3.reshape(y_test3.shape)
    coef1 = np.corrcoef(y_test1, y_predicted1)[0,1] ** 2
    coef2 = np.corrcoef(y_test2, y_predicted2)[0,1] ** 2
    coef3 = np.corrcoef(y_test3, y_predicted3)[0,1] ** 2
    eval_1 = model.evaluate(X_test1, y_test1)
    eval_2 = model.evaluate(X_test2, y_test2)
    eval_3 = model.evaluate(X_test3, y_test3)
    result = {'Model': [name_str]*12,
              'Train_site': [site_1]*12,
              'Test_site': [site_1] * 4 + [site_2] * 4 + [site_3] * 4,
              'Metric': ['MSE', 'RMSE', 'MAE', 'coef'] * 3,
              'Value': [eval_1[1], eval_1[2], eval_1[3], coef1,
                        eval_2[1], eval_2[2], eval_2[3], coef2,
                        eval_3[1], eval_3[2], eval_3[3], coef3]}
    df = pd.DataFrame(result)
    return df, history

In [70]:
# Generate evaluation results and correlation coeffcients combined in a dataframe, and history
def double_cross_site(model_name, name_str, ckpt_filepath, lr,
                      site_1, site_2, site_3, X, y):
    # Split the data by sites
    X_1 = X[site==site_1]
    y_1 = y[site==site_1]
    X_2 = X[site==site_2]
    y_2 = y[site==site_2]
    X_3 = X[site==site_3]
    y_3 = y[site==site_3]
    # Split the data into train and test sets:
    X_1_train, X_1_test, y_1_train, y_1_test = train_test_split(X_1, y_1, test_size=0.2)
    X_2_train, X_2_test, y_2_train, y_2_test = train_test_split(X_2, y_2, test_size=0.2)
    X_3_train, X_3_test, y_3_train, y_3_test = train_test_split(X_3, y_3, test_size=0.2)
    imputer = SimpleImputer(strategy="median")
    # Impute train and test separately:
    X_1_train = np.concatenate([imputer.fit_transform(X_1_train[..., ii])[:, :, None] for ii in range(X_1_train.shape[-1])], -1)
    X_2_train = np.concatenate([imputer.fit_transform(X_2_train[..., ii])[:, :, None] for ii in range(X_2_train.shape[-1])], -1)
    X_1_test = np.concatenate([imputer.fit_transform(X_1_test[..., ii])[:, :, None] for ii in range(X_1_test.shape[-1])], -1)
    X_2_test = np.concatenate([imputer.fit_transform(X_2_test[..., ii])[:, :, None] for ii in range(X_2_test.shape[-1])], -1)
    X_3_test = np.concatenate([imputer.fit_transform(X_3_test[..., ii])[:, :, None] for ii in range(X_3_test.shape[-1])], -1)
    # Merging data from two sites
    from sklearn.utils import shuffle
    # training data
    X_train = np.concatenate((X_1_train, X_2_train), axis=0)
    y_train = np.concatenate((y_1_train, y_2_train), axis=0)
    # size down
    X_train, y_train = shuffle(X_train, y_train, n_samples=y_3_test.shape[0])
    model = model_name(input_shape=(100, 72), n_classes=1, output_activation=None, verbose=True)
    model.compile(loss='mean_squared_error',
                  optimizer=tf.keras.optimizers.Adam(learning_rate=lr),
                  metrics=['mean_squared_error', 
                           tf.keras.metrics.RootMeanSquaredError(name='rmse'), 
                           'mean_absolute_error'])
    # ModelCheckpoint
    ckpt = tf.keras.callbacks.ModelCheckpoint(
    ckpt_filepath,
    monitor="val_loss",
    verbose=1,
    save_best_only=True,
    save_weights_only=True,
    mode="auto",
    )
    # CSVLogger
    log = tf.keras.callbacks.CSVLogger(filename=(name_str + '.csv'), append=True)
    callbacks = [early_stopping, ckpt, reduce_lr, log]
    history = model.fit(X_train, y_train, epochs=n_epochs, batch_size=128, validation_split=0.2,
                        callbacks=callbacks)
    model.load_weights(ckpt_filepath)
    
    y_predicted1 = model.predict(X_1_test)
    y_predicted1 = y_predicted1.reshape(y_1_test.shape)
    y_predicted2 = model.predict(X_2_test)
    y_predicted2 = y_predicted2.reshape(y_2_test.shape)
    y_predicted3 = model.predict(X_3_test)
    y_predicted3 = y_predicted3.reshape(y_3_test.shape)
    coef1 = np.corrcoef(y_1_test, y_predicted1)[0,1] ** 2
    coef2 = np.corrcoef(y_2_test, y_predicted2)[0,1] ** 2
    coef3 = np.corrcoef(y_3_test, y_predicted3)[0,1] ** 2
    eval_1 = model.evaluate(X_1_test, y_1_test)
    eval_2 = model.evaluate(X_2_test, y_2_test)
    eval_3 = model.evaluate(X_3_test, y_3_test)
    result = {'Model': [name_str]*12,
              'Train_site': [f'{site_1}, {site_2}'] * 12,
              'Test_site': [site_1] * 4 + [site_2] * 4 + [site_3] * 4,
              'Metric': ['MSE', 'RMSE', 'MAE', 'coef'] * 3,
              'Value': [eval_1[1], eval_1[2], eval_1[3], coef1,
                        eval_2[1], eval_2[2], eval_2[3], coef2,
                        eval_3[1], eval_3[2], eval_3[3], coef3]}
    df = pd.DataFrame(result)
    return df, history

### Lenet

#### single-cross-site

In [11]:
df_lenet1, history_lenet1 = single_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.m5', 0.001, 0, 3, 4, X, y)

pooling layers: 4
Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 100, 72)]         0         
                                                                 
 conv1d (Conv1D)             (None, 100, 6)            1302      
                                                                 
 max_pooling1d (MaxPooling1D  (None, 50, 6)            0         
 )                                                               
                                                                 
 conv1d_1 (Conv1D)           (None, 50, 16)            304       
                                                                 
 max_pooling1d_1 (MaxPooling  (None, 25, 16)           0         
 1D)                                                             
                                                                 
 conv1d_2 (Conv1D)           (None, 25, 26)

Epoch 13/1000
1/4 [======>.......................] - ETA: 0s - loss: 17.8197 - mean_squared_error: 17.8197 - rmse: 4.2213 - mean_absolute_error: 3.2820
Epoch 00013: val_loss did not improve from 9.88464
4/4 [==============================] - 0s 22ms/step - loss: 17.1990 - mean_squared_error: 17.1990 - rmse: 4.1472 - mean_absolute_error: 3.2557 - val_loss: 10.3530 - val_mean_squared_error: 10.3530 - val_rmse: 3.2176 - val_mean_absolute_error: 2.4933 - lr: 0.0010
Epoch 14/1000
1/4 [======>.......................] - ETA: 0s - loss: 18.5029 - mean_squared_error: 18.5029 - rmse: 4.3015 - mean_absolute_error: 3.3933
Epoch 00014: val_loss did not improve from 9.88464
4/4 [==============================] - 0s 21ms/step - loss: 19.1063 - mean_squared_error: 19.1063 - rmse: 4.3711 - mean_absolute_error: 3.5215 - val_loss: 11.2137 - val_mean_squared_error: 11.2137 - val_rmse: 3.3487 - val_mean_absolute_error: 2.5381 - lr: 0.0010
Epoch 15/1000
1/4 [======>.......................] - ETA: 0s - loss:

1/4 [======>.......................] - ETA: 0s - loss: 19.7991 - mean_squared_error: 19.7991 - rmse: 4.4496 - mean_absolute_error: 3.5677
Epoch 00030: val_loss did not improve from 9.48943
4/4 [==============================] - 0s 21ms/step - loss: 17.8603 - mean_squared_error: 17.8603 - rmse: 4.2261 - mean_absolute_error: 3.3970 - val_loss: 10.5096 - val_mean_squared_error: 10.5096 - val_rmse: 3.2419 - val_mean_absolute_error: 2.4808 - lr: 5.0000e-04
Epoch 31/1000
1/4 [======>.......................] - ETA: 0s - loss: 15.5863 - mean_squared_error: 15.5863 - rmse: 3.9479 - mean_absolute_error: 3.0539
Epoch 00031: val_loss did not improve from 9.48943
4/4 [==============================] - 0s 21ms/step - loss: 16.0578 - mean_squared_error: 16.0578 - rmse: 4.0072 - mean_absolute_error: 3.1085 - val_loss: 10.2518 - val_mean_squared_error: 10.2518 - val_rmse: 3.2018 - val_mean_absolute_error: 2.4619 - lr: 5.0000e-04
Epoch 32/1000
1/4 [======>.......................] - ETA: 0s - loss: 17.53

1/4 [======>.......................] - ETA: 0s - loss: 14.0695 - mean_squared_error: 14.0695 - rmse: 3.7509 - mean_absolute_error: 3.0468
Epoch 00047: val_loss did not improve from 8.95443
4/4 [==============================] - 0s 22ms/step - loss: 15.3229 - mean_squared_error: 15.3229 - rmse: 3.9144 - mean_absolute_error: 3.1241 - val_loss: 9.6480 - val_mean_squared_error: 9.6480 - val_rmse: 3.1061 - val_mean_absolute_error: 2.3900 - lr: 5.0000e-04
Epoch 48/1000
1/4 [======>.......................] - ETA: 0s - loss: 17.9370 - mean_squared_error: 17.9370 - rmse: 4.2352 - mean_absolute_error: 3.3490
Epoch 00048: val_loss did not improve from 8.95443
4/4 [==============================] - 0s 22ms/step - loss: 14.9935 - mean_squared_error: 14.9935 - rmse: 3.8721 - mean_absolute_error: 3.0296 - val_loss: 9.2090 - val_mean_squared_error: 9.2090 - val_rmse: 3.0346 - val_mean_absolute_error: 2.3540 - lr: 5.0000e-04
Epoch 49/1000
1/4 [======>.......................] - ETA: 0s - loss: 16.9366 -

1/4 [======>.......................] - ETA: 0s - loss: 10.6627 - mean_squared_error: 10.6627 - rmse: 3.2654 - mean_absolute_error: 2.6948
Epoch 00064: val_loss did not improve from 8.10816
4/4 [==============================] - 0s 21ms/step - loss: 14.0701 - mean_squared_error: 14.0701 - rmse: 3.7510 - mean_absolute_error: 2.9581 - val_loss: 8.4476 - val_mean_squared_error: 8.4476 - val_rmse: 2.9065 - val_mean_absolute_error: 2.2384 - lr: 5.0000e-04
Epoch 65/1000
1/4 [======>.......................] - ETA: 0s - loss: 14.0893 - mean_squared_error: 14.0893 - rmse: 3.7536 - mean_absolute_error: 2.9494
Epoch 00065: val_loss improved from 8.10816 to 7.69858, saving model to /tmp/lenet.m5
4/4 [==============================] - 0s 26ms/step - loss: 13.4765 - mean_squared_error: 13.4765 - rmse: 3.6710 - mean_absolute_error: 2.8799 - val_loss: 7.6986 - val_mean_squared_error: 7.6986 - val_rmse: 2.7746 - val_mean_absolute_error: 2.1667 - lr: 5.0000e-04
Epoch 66/1000
1/4 [======>.................

...

Epoch 170/1000
1/4 [======>.......................] - ETA: 0s - loss: 9.8715 - mean_squared_error: 9.8715 - rmse: 3.1419 - mean_absolute_error: 2.4708
Epoch 00170: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 21ms/step - loss: 9.6866 - mean_squared_error: 9.6866 - rmse: 3.1123 - mean_absolute_error: 2.4157 - val_loss: 6.7694 - val_mean_squared_error: 6.7694 - val_rmse: 2.6018 - val_mean_absolute_error: 1.9620 - lr: 2.5000e-04
Epoch 171/1000
1/4 [======>.......................] - ETA: 0s - loss: 11.2011 - mean_squared_error: 11.2011 - rmse: 3.3468 - mean_absolute_error: 2.6147
Epoch 00171: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 22ms/step - loss: 8.9802 - mean_squared_error: 8.9802 - rmse: 2.9967 - mean_absolute_error: 2.3482 - val_loss: 7.1807 - val_mean_squared_error: 7.1807 - val_rmse: 2.6797 - val_mean_absolute_error: 2.0278 - lr: 2.5000e-04
Epoch 172/1000
1/4 [======>.......................] - ETA: 0s - loss

Epoch 188/1000
1/4 [======>.......................] - ETA: 0s - loss: 8.5035 - mean_squared_error: 8.5035 - rmse: 2.9161 - mean_absolute_error: 2.1834
Epoch 00188: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 22ms/step - loss: 8.8268 - mean_squared_error: 8.8268 - rmse: 2.9710 - mean_absolute_error: 2.3212 - val_loss: 6.6648 - val_mean_squared_error: 6.6648 - val_rmse: 2.5816 - val_mean_absolute_error: 1.9517 - lr: 1.2500e-04
Epoch 189/1000
1/4 [======>.......................] - ETA: 0s - loss: 8.5905 - mean_squared_error: 8.5905 - rmse: 2.9310 - mean_absolute_error: 2.2921
Epoch 00189: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 22ms/step - loss: 9.1095 - mean_squared_error: 9.1095 - rmse: 3.0182 - mean_absolute_error: 2.3540 - val_loss: 6.8575 - val_mean_squared_error: 6.8575 - val_rmse: 2.6187 - val_mean_absolute_error: 1.9737 - lr: 1.2500e-04
Epoch 190/1000
1/4 [======>.......................] - ETA: 0s - loss: 

Epoch 206/1000
1/4 [======>.......................] - ETA: 0s - loss: 8.2161 - mean_squared_error: 8.2161 - rmse: 2.8664 - mean_absolute_error: 2.2492
Epoch 00206: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 21ms/step - loss: 8.2286 - mean_squared_error: 8.2286 - rmse: 2.8686 - mean_absolute_error: 2.2586 - val_loss: 6.7998 - val_mean_squared_error: 6.7998 - val_rmse: 2.6076 - val_mean_absolute_error: 1.9580 - lr: 6.2500e-05
Epoch 207/1000
1/4 [======>.......................] - ETA: 0s - loss: 6.3010 - mean_squared_error: 6.3010 - rmse: 2.5102 - mean_absolute_error: 1.8869
Epoch 00207: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 22ms/step - loss: 9.2465 - mean_squared_error: 9.2465 - rmse: 3.0408 - mean_absolute_error: 2.2664 - val_loss: 6.8708 - val_mean_squared_error: 6.8708 - val_rmse: 2.6212 - val_mean_absolute_error: 1.9707 - lr: 6.2500e-05
Epoch 208/1000
1/4 [======>.......................] - ETA: 0s - loss: 

Epoch 224/1000
1/4 [======>.......................] - ETA: 0s - loss: 9.3830 - mean_squared_error: 9.3830 - rmse: 3.0632 - mean_absolute_error: 2.3291
Epoch 00224: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 21ms/step - loss: 9.1167 - mean_squared_error: 9.1167 - rmse: 3.0194 - mean_absolute_error: 2.3212 - val_loss: 6.8405 - val_mean_squared_error: 6.8405 - val_rmse: 2.6154 - val_mean_absolute_error: 1.9666 - lr: 3.1250e-05
Epoch 225/1000
1/4 [======>.......................] - ETA: 0s - loss: 7.7968 - mean_squared_error: 7.7968 - rmse: 2.7923 - mean_absolute_error: 2.1378
Epoch 00225: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 21ms/step - loss: 8.8628 - mean_squared_error: 8.8628 - rmse: 2.9771 - mean_absolute_error: 2.3248 - val_loss: 6.8185 - val_mean_squared_error: 6.8185 - val_rmse: 2.6112 - val_mean_absolute_error: 1.9636 - lr: 3.1250e-05
Epoch 226/1000
1/4 [======>.......................] - ETA: 0s - loss: 

Epoch 242/1000
1/4 [======>.......................] - ETA: 0s - loss: 9.4947 - mean_squared_error: 9.4947 - rmse: 3.0813 - mean_absolute_error: 2.4323
Epoch 00242: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 20ms/step - loss: 9.1317 - mean_squared_error: 9.1317 - rmse: 3.0219 - mean_absolute_error: 2.3469 - val_loss: 6.7549 - val_mean_squared_error: 6.7549 - val_rmse: 2.5990 - val_mean_absolute_error: 1.9582 - lr: 1.5625e-05
Epoch 243/1000
1/4 [======>.......................] - ETA: 0s - loss: 7.9867 - mean_squared_error: 7.9867 - rmse: 2.8261 - mean_absolute_error: 2.3514
Epoch 00243: val_loss did not improve from 6.36703
4/4 [==============================] - 0s 21ms/step - loss: 8.9463 - mean_squared_error: 8.9463 - rmse: 2.9910 - mean_absolute_error: 2.3652 - val_loss: 6.8271 - val_mean_squared_error: 6.8271 - val_rmse: 2.6129 - val_mean_absolute_error: 1.9676 - lr: 1.5625e-05
Epoch 244/1000
4/4 [==============================] - ETA: 0s - loss: 

In [12]:
df_lenet2, history_lenet2 = single_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.m5', 0.001, 3, 0, 4, X, y)

pooling layers: 4
Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 100, 72)]         0         
                                                                 
 conv1d_4 (Conv1D)           (None, 100, 6)            1302      
                                                                 
 max_pooling1d_4 (MaxPooling  (None, 50, 6)            0         
 1D)                                                             
                                                                 
 conv1d_5 (Conv1D)           (None, 50, 16)            304       
                                                                 
 max_pooling1d_5 (MaxPooling  (None, 25, 16)           0         
 1D)                                                             
                                                                 
 conv1d_6 (Conv1D)           (None, 25, 2

Epoch 13/1000
1/4 [======>.......................] - ETA: 0s - loss: 19.4496 - mean_squared_error: 19.4496 - rmse: 4.4102 - mean_absolute_error: 3.3832
Epoch 00013: val_loss did not improve from 10.92711
4/4 [==============================] - 0s 20ms/step - loss: 20.2685 - mean_squared_error: 20.2685 - rmse: 4.5021 - mean_absolute_error: 3.4835 - val_loss: 13.3739 - val_mean_squared_error: 13.3739 - val_rmse: 3.6570 - val_mean_absolute_error: 2.8317 - lr: 0.0010
Epoch 14/1000
1/4 [======>.......................] - ETA: 0s - loss: 17.7267 - mean_squared_error: 17.7267 - rmse: 4.2103 - mean_absolute_error: 3.0701
Epoch 00014: val_loss did not improve from 10.92711
4/4 [==============================] - 0s 20ms/step - loss: 16.0793 - mean_squared_error: 16.0793 - rmse: 4.0099 - mean_absolute_error: 3.0587 - val_loss: 12.0849 - val_mean_squared_error: 12.0849 - val_rmse: 3.4763 - val_mean_absolute_error: 2.7073 - lr: 0.0010
Epoch 15/1000
1/4 [======>.......................] - ETA: 0s - los

Epoch 31/1000
1/4 [======>.......................] - ETA: 0s - loss: 17.5711 - mean_squared_error: 17.5711 - rmse: 4.1918 - mean_absolute_error: 3.2905
Epoch 00031: val_loss did not improve from 10.92711
4/4 [==============================] - 0s 20ms/step - loss: 17.7508 - mean_squared_error: 17.7508 - rmse: 4.2132 - mean_absolute_error: 3.2306 - val_loss: 12.6450 - val_mean_squared_error: 12.6450 - val_rmse: 3.5560 - val_mean_absolute_error: 2.7608 - lr: 5.0000e-04
Epoch 32/1000
1/4 [======>.......................] - ETA: 0s - loss: 15.1172 - mean_squared_error: 15.1172 - rmse: 3.8881 - mean_absolute_error: 2.9743
Epoch 00032: val_loss did not improve from 10.92711
4/4 [==============================] - 0s 20ms/step - loss: 14.9244 - mean_squared_error: 14.9244 - rmse: 3.8632 - mean_absolute_error: 3.0126 - val_loss: 12.3545 - val_mean_squared_error: 12.3545 - val_rmse: 3.5149 - val_mean_absolute_error: 2.7341 - lr: 5.0000e-04
Epoch 33/1000
1/4 [======>.......................] - ETA: 

1/4 [======>.......................] - ETA: 0s - loss: 16.3624 - mean_squared_error: 16.3624 - rmse: 4.0450 - mean_absolute_error: 2.9726
Epoch 00048: val_loss did not improve from 10.50581
4/4 [==============================] - 0s 23ms/step - loss: 14.6191 - mean_squared_error: 14.6191 - rmse: 3.8235 - mean_absolute_error: 2.9007 - val_loss: 11.5037 - val_mean_squared_error: 11.5037 - val_rmse: 3.3917 - val_mean_absolute_error: 2.6359 - lr: 5.0000e-04
Epoch 49/1000
1/4 [======>.......................] - ETA: 0s - loss: 16.3284 - mean_squared_error: 16.3284 - rmse: 4.0408 - mean_absolute_error: 3.1277
Epoch 00049: val_loss did not improve from 10.50581
4/4 [==============================] - 0s 21ms/step - loss: 15.4907 - mean_squared_error: 15.4907 - rmse: 3.9358 - mean_absolute_error: 3.0557 - val_loss: 11.4928 - val_mean_squared_error: 11.4928 - val_rmse: 3.3901 - val_mean_absolute_error: 2.6375 - lr: 5.0000e-04
Epoch 50/1000
1/4 [======>.......................] - ETA: 0s - loss: 16.

1/4 [======>.......................] - ETA: 0s - loss: 15.5864 - mean_squared_error: 15.5864 - rmse: 3.9480 - mean_absolute_error: 3.0063
Epoch 00065: val_loss did not improve from 10.50581
4/4 [==============================] - 0s 24ms/step - loss: 13.4415 - mean_squared_error: 13.4415 - rmse: 3.6663 - mean_absolute_error: 2.8512 - val_loss: 11.6957 - val_mean_squared_error: 11.6957 - val_rmse: 3.4199 - val_mean_absolute_error: 2.6391 - lr: 2.5000e-04
Epoch 66/1000
1/4 [======>.......................] - ETA: 0s - loss: 12.3619 - mean_squared_error: 12.3619 - rmse: 3.5159 - mean_absolute_error: 2.6775
Epoch 00066: val_loss did not improve from 10.50581
4/4 [==============================] - 0s 21ms/step - loss: 14.3086 - mean_squared_error: 14.3086 - rmse: 3.7827 - mean_absolute_error: 2.9286 - val_loss: 11.1034 - val_mean_squared_error: 11.1034 - val_rmse: 3.3322 - val_mean_absolute_error: 2.5808 - lr: 2.5000e-04
Epoch 67/1000
1/4 [======>.......................] - ETA: 0s - loss: 12.

...

1/4 [======>.......................] - ETA: 0s - loss: 14.4019 - mean_squared_error: 14.4019 - rmse: 3.7950 - mean_absolute_error: 2.8966
Epoch 00187: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 20ms/step - loss: 12.0657 - mean_squared_error: 12.0657 - rmse: 3.4736 - mean_absolute_error: 2.6828 - val_loss: 10.0603 - val_mean_squared_error: 10.0603 - val_rmse: 3.1718 - val_mean_absolute_error: 2.4227 - lr: 6.2500e-05
Epoch 188/1000
4/4 [==============================] - ETA: 0s - loss: 11.6094 - mean_squared_error: 11.6094 - rmse: 3.4073 - mean_absolute_error: 2.6646
Epoch 00188: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 25ms/step - loss: 11.6094 - mean_squared_error: 11.6094 - rmse: 3.4073 - mean_absolute_error: 2.6646 - val_loss: 10.0403 - val_mean_squared_error: 10.0403 - val_rmse: 3.1686 - val_mean_absolute_error: 2.4205 - lr: 6.2500e-05
Epoch 189/1000
1/4 [======>.......................] - ETA: 0s - loss: 11.

1/4 [======>.......................] - ETA: 0s - loss: 14.1213 - mean_squared_error: 14.1213 - rmse: 3.7578 - mean_absolute_error: 2.8940
Epoch 00204: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 20ms/step - loss: 11.2991 - mean_squared_error: 11.2991 - rmse: 3.3614 - mean_absolute_error: 2.5713 - val_loss: 10.2261 - val_mean_squared_error: 10.2261 - val_rmse: 3.1978 - val_mean_absolute_error: 2.4312 - lr: 3.1250e-05
Epoch 205/1000
1/4 [======>.......................] - ETA: 0s - loss: 10.3806 - mean_squared_error: 10.3806 - rmse: 3.2219 - mean_absolute_error: 2.4778
Epoch 00205: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 22ms/step - loss: 11.6910 - mean_squared_error: 11.6910 - rmse: 3.4192 - mean_absolute_error: 2.6169 - val_loss: 10.0428 - val_mean_squared_error: 10.0428 - val_rmse: 3.1690 - val_mean_absolute_error: 2.4145 - lr: 3.1250e-05
Epoch 206/1000
1/4 [======>.......................] - ETA: 0s - loss: 11.

1/4 [======>.......................] - ETA: 0s - loss: 9.8967 - mean_squared_error: 9.8967 - rmse: 3.1459 - mean_absolute_error: 2.4460
Epoch 00221: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 20ms/step - loss: 11.2063 - mean_squared_error: 11.2063 - rmse: 3.3476 - mean_absolute_error: 2.5922 - val_loss: 9.8387 - val_mean_squared_error: 9.8387 - val_rmse: 3.1367 - val_mean_absolute_error: 2.3952 - lr: 1.5625e-05
Epoch 222/1000
1/4 [======>.......................] - ETA: 0s - loss: 11.6361 - mean_squared_error: 11.6361 - rmse: 3.4112 - mean_absolute_error: 2.6859
Epoch 00222: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 20ms/step - loss: 12.1246 - mean_squared_error: 12.1246 - rmse: 3.4820 - mean_absolute_error: 2.6830 - val_loss: 9.8688 - val_mean_squared_error: 9.8688 - val_rmse: 3.1415 - val_mean_absolute_error: 2.3975 - lr: 1.5625e-05
Epoch 223/1000
1/4 [======>.......................] - ETA: 0s - loss: 14.3998 -

Epoch 239/1000
1/4 [======>.......................] - ETA: 0s - loss: 10.7614 - mean_squared_error: 10.7614 - rmse: 3.2805 - mean_absolute_error: 2.5834
Epoch 00239: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 22ms/step - loss: 12.0231 - mean_squared_error: 12.0231 - rmse: 3.4674 - mean_absolute_error: 2.7000 - val_loss: 9.8259 - val_mean_squared_error: 9.8259 - val_rmse: 3.1346 - val_mean_absolute_error: 2.3919 - lr: 7.8125e-06
Epoch 240/1000
1/4 [======>.......................] - ETA: 0s - loss: 10.8458 - mean_squared_error: 10.8458 - rmse: 3.2933 - mean_absolute_error: 2.4399
Epoch 00240: val_loss did not improve from 9.36583
4/4 [==============================] - 0s 21ms/step - loss: 10.2810 - mean_squared_error: 10.2810 - rmse: 3.2064 - mean_absolute_error: 2.4867 - val_loss: 9.8002 - val_mean_squared_error: 9.8002 - val_rmse: 3.1305 - val_mean_absolute_error: 2.3900 - lr: 7.8125e-06
Epoch 241/1000
1/4 [======>.......................] - ETA: 0s 

Epoch 257/1000
1/4 [======>.......................] - ETA: 0s - loss: 13.0954 - mean_squared_error: 13.0954 - rmse: 3.6188 - mean_absolute_error: 2.8429
Epoch 00257: val_loss did not improve from 9.36583

Epoch 00257: ReduceLROnPlateau reducing learning rate to 3.906250185536919e-06.
2/2 [==============================] - 0s 3ms/step - loss: 10.0345 - mean_squared_error: 10.0345 - rmse: 3.1677 - mean_absolute_error: 2.6124


In [13]:
df_lenet3, history_lenet3 = single_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.m5', 0.001, 4, 0, 3, X, y)

pooling layers: 4
Model: "model_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_3 (InputLayer)        [(None, 100, 72)]         0         
                                                                 
 conv1d_8 (Conv1D)           (None, 100, 6)            1302      
                                                                 
 max_pooling1d_8 (MaxPooling  (None, 50, 6)            0         
 1D)                                                             
                                                                 
 conv1d_9 (Conv1D)           (None, 50, 16)            304       
                                                                 
 max_pooling1d_9 (MaxPooling  (None, 25, 16)           0         
 1D)                                                             
                                                                 
 conv1d_10 (Conv1D)          (None, 25, 2

Epoch 13/1000
1/2 [==============>...............] - ETA: 0s - loss: 23.2693 - mean_squared_error: 23.2693 - rmse: 4.8238 - mean_absolute_error: 4.0116
Epoch 00013: val_loss improved from 12.86259 to 11.25069, saving model to /tmp/lenet.m5
2/2 [==============================] - 0s 47ms/step - loss: 22.6206 - mean_squared_error: 22.6206 - rmse: 4.7561 - mean_absolute_error: 3.9394 - val_loss: 11.2507 - val_mean_squared_error: 11.2507 - val_rmse: 3.3542 - val_mean_absolute_error: 2.8029 - lr: 0.0010
Epoch 14/1000
1/2 [==============>...............] - ETA: 0s - loss: 20.0334 - mean_squared_error: 20.0334 - rmse: 4.4759 - mean_absolute_error: 3.6402
Epoch 00014: val_loss did not improve from 11.25069
2/2 [==============================] - 0s 25ms/step - loss: 21.4897 - mean_squared_error: 21.4897 - rmse: 4.6357 - mean_absolute_error: 3.7551 - val_loss: 12.1071 - val_mean_squared_error: 12.1071 - val_rmse: 3.4795 - val_mean_absolute_error: 2.9577 - lr: 0.0010
Epoch 15/1000
1/2 [===========

2/2 [==============================] - 0s 46ms/step - loss: 20.0944 - mean_squared_error: 20.0944 - rmse: 4.4827 - mean_absolute_error: 3.5620 - val_loss: 11.2278 - val_mean_squared_error: 11.2278 - val_rmse: 3.3508 - val_mean_absolute_error: 2.7258 - lr: 0.0010
Epoch 31/1000
1/2 [==============>...............] - ETA: 0s - loss: 25.5155 - mean_squared_error: 25.5155 - rmse: 5.0513 - mean_absolute_error: 4.1458
Epoch 00031: val_loss did not improve from 11.22784
2/2 [==============================] - 0s 28ms/step - loss: 26.4295 - mean_squared_error: 26.4295 - rmse: 5.1410 - mean_absolute_error: 4.2353 - val_loss: 11.4260 - val_mean_squared_error: 11.4260 - val_rmse: 3.3802 - val_mean_absolute_error: 2.7062 - lr: 0.0010
Epoch 32/1000
1/2 [==============>...............] - ETA: 0s - loss: 22.3704 - mean_squared_error: 22.3704 - rmse: 4.7297 - mean_absolute_error: 3.7393
Epoch 00032: val_loss did not improve from 11.22784
2/2 [==============================] - 0s 29ms/step - loss: 20.876

Epoch 48/1000
1/2 [==============>...............] - ETA: 0s - loss: 16.2833 - mean_squared_error: 16.2833 - rmse: 4.0353 - mean_absolute_error: 3.2692
Epoch 00048: val_loss improved from 11.00830 to 10.78526, saving model to /tmp/lenet.m5
2/2 [==============================] - 0s 40ms/step - loss: 19.5422 - mean_squared_error: 19.5422 - rmse: 4.4207 - mean_absolute_error: 3.5100 - val_loss: 10.7853 - val_mean_squared_error: 10.7853 - val_rmse: 3.2841 - val_mean_absolute_error: 2.6018 - lr: 0.0010
Epoch 49/1000
1/2 [==============>...............] - ETA: 0s - loss: 18.6183 - mean_squared_error: 18.6183 - rmse: 4.3149 - mean_absolute_error: 3.6308
Epoch 00049: val_loss improved from 10.78526 to 10.44408, saving model to /tmp/lenet.m5
2/2 [==============================] - 0s 53ms/step - loss: 19.0995 - mean_squared_error: 19.0995 - rmse: 4.3703 - mean_absolute_error: 3.6731 - val_loss: 10.4441 - val_mean_squared_error: 10.4441 - val_rmse: 3.2317 - val_mean_absolute_error: 2.6202 - lr: 0

1/2 [==============>...............] - ETA: 0s - loss: 17.7699 - mean_squared_error: 17.7699 - rmse: 4.2154 - mean_absolute_error: 3.4176
Epoch 00065: val_loss did not improve from 10.08949
2/2 [==============================] - 0s 25ms/step - loss: 16.7322 - mean_squared_error: 16.7322 - rmse: 4.0905 - mean_absolute_error: 3.3234 - val_loss: 10.6588 - val_mean_squared_error: 10.6588 - val_rmse: 3.2648 - val_mean_absolute_error: 2.5123 - lr: 0.0010
Epoch 66/1000
1/2 [==============>...............] - ETA: 0s - loss: 16.4334 - mean_squared_error: 16.4334 - rmse: 4.0538 - mean_absolute_error: 3.2410
Epoch 00066: val_loss did not improve from 10.08949
2/2 [==============================] - 0s 29ms/step - loss: 16.3289 - mean_squared_error: 16.3289 - rmse: 4.0409 - mean_absolute_error: 3.2344 - val_loss: 10.4796 - val_mean_squared_error: 10.4796 - val_rmse: 3.2372 - val_mean_absolute_error: 2.5019 - lr: 0.0010
Epoch 67/1000
1/2 [==============>...............] - ETA: 0s - loss: 15.3773 - m

...

Epoch 274/1000
1/2 [==============>...............] - ETA: 0s - loss: 11.9587 - mean_squared_error: 11.9587 - rmse: 3.4581 - mean_absolute_error: 2.7271
Epoch 00274: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 28ms/step - loss: 12.8585 - mean_squared_error: 12.8585 - rmse: 3.5859 - mean_absolute_error: 2.7766 - val_loss: 8.2709 - val_mean_squared_error: 8.2709 - val_rmse: 2.8759 - val_mean_absolute_error: 2.2284 - lr: 1.2500e-04
Epoch 275/1000
1/2 [==============>...............] - ETA: 0s - loss: 16.1591 - mean_squared_error: 16.1591 - rmse: 4.0198 - mean_absolute_error: 3.0990
Epoch 00275: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 25ms/step - loss: 15.6987 - mean_squared_error: 15.6987 - rmse: 3.9622 - mean_absolute_error: 3.0538 - val_loss: 8.4626 - val_mean_squared_error: 8.4626 - val_rmse: 2.9091 - val_mean_absolute_error: 2.2597 - lr: 1.2500e-04
Epoch 276/1000
1/2 [==============>...............] - ETA: 0s 

Epoch 292/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.9037 - mean_squared_error: 12.9037 - rmse: 3.5922 - mean_absolute_error: 2.8976
Epoch 00292: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 26ms/step - loss: 12.8370 - mean_squared_error: 12.8370 - rmse: 3.5829 - mean_absolute_error: 2.8393 - val_loss: 6.9294 - val_mean_squared_error: 6.9294 - val_rmse: 2.6324 - val_mean_absolute_error: 2.0185 - lr: 6.2500e-05
Epoch 293/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.8281 - mean_squared_error: 12.8281 - rmse: 3.5816 - mean_absolute_error: 2.8094
Epoch 00293: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 25ms/step - loss: 13.0678 - mean_squared_error: 13.0678 - rmse: 3.6149 - mean_absolute_error: 2.8734 - val_loss: 6.9611 - val_mean_squared_error: 6.9611 - val_rmse: 2.6384 - val_mean_absolute_error: 2.0218 - lr: 6.2500e-05
Epoch 294/1000
1/2 [==============>...............] - ETA: 0s 

Epoch 310/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.5255 - mean_squared_error: 12.5255 - rmse: 3.5391 - mean_absolute_error: 2.7741
Epoch 00310: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 27ms/step - loss: 12.6648 - mean_squared_error: 12.6648 - rmse: 3.5588 - mean_absolute_error: 2.7982 - val_loss: 6.9282 - val_mean_squared_error: 6.9282 - val_rmse: 2.6322 - val_mean_absolute_error: 2.0222 - lr: 6.2500e-05
Epoch 311/1000
1/2 [==============>...............] - ETA: 0s - loss: 11.8378 - mean_squared_error: 11.8378 - rmse: 3.4406 - mean_absolute_error: 2.7068
Epoch 00311: val_loss did not improve from 6.51974

Epoch 00311: ReduceLROnPlateau reducing learning rate to 3.125000148429535e-05.
2/2 [==============================] - 0s 28ms/step - loss: 11.5767 - mean_squared_error: 11.5767 - rmse: 3.4025 - mean_absolute_error: 2.7100 - val_loss: 6.7408 - val_mean_squared_error: 6.7408 - val_rmse: 2.5963 - val_mean_absolute_error: 1.999

1/2 [==============>...............] - ETA: 0s - loss: 13.9866 - mean_squared_error: 13.9866 - rmse: 3.7399 - mean_absolute_error: 2.8962
Epoch 00327: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 26ms/step - loss: 12.7590 - mean_squared_error: 12.7590 - rmse: 3.5720 - mean_absolute_error: 2.7910 - val_loss: 7.2284 - val_mean_squared_error: 7.2284 - val_rmse: 2.6886 - val_mean_absolute_error: 2.0587 - lr: 3.1250e-05
Epoch 328/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.5628 - mean_squared_error: 14.5628 - rmse: 3.8161 - mean_absolute_error: 2.9999
Epoch 00328: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 34ms/step - loss: 13.7651 - mean_squared_error: 13.7651 - rmse: 3.7101 - mean_absolute_error: 2.9113 - val_loss: 7.2424 - val_mean_squared_error: 7.2424 - val_rmse: 2.6912 - val_mean_absolute_error: 2.0609 - lr: 3.1250e-05
Epoch 329/1000
1/2 [==============>...............] - ETA: 0s - loss: 15.9851

Epoch 345/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.2823 - mean_squared_error: 13.2823 - rmse: 3.6445 - mean_absolute_error: 2.9143
Epoch 00345: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 27ms/step - loss: 13.1326 - mean_squared_error: 13.1326 - rmse: 3.6239 - mean_absolute_error: 2.9004 - val_loss: 6.8180 - val_mean_squared_error: 6.8180 - val_rmse: 2.6111 - val_mean_absolute_error: 2.0082 - lr: 1.5625e-05
Epoch 346/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.3527 - mean_squared_error: 12.3527 - rmse: 3.5146 - mean_absolute_error: 2.8120
Epoch 00346: val_loss did not improve from 6.51974
2/2 [==============================] - 0s 29ms/step - loss: 12.3077 - mean_squared_error: 12.3077 - rmse: 3.5082 - mean_absolute_error: 2.7942 - val_loss: 6.8315 - val_mean_squared_error: 6.8315 - val_rmse: 2.6137 - val_mean_absolute_error: 2.0099 - lr: 1.5625e-05
Epoch 347/1000
1/2 [==============>...............] - ETA: 0s 

In [28]:
df_lenet_1 = (df_lenet1.merge(df_lenet2, how='outer')).merge(df_lenet3, how='outer')

#### double-cross-site

In [31]:
df_lenet4, hisory_lenet4 = double_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.h5', 0.001, 0, 3, 4, X, y)

pooling layers: 4
Model: "model_8"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_9 (InputLayer)        [(None, 100, 72)]         0         
                                                                 
 conv1d_32 (Conv1D)          (None, 100, 6)            1302      
                                                                 
 max_pooling1d_32 (MaxPoolin  (None, 50, 6)            0         
 g1D)                                                            
                                                                 
 conv1d_33 (Conv1D)          (None, 50, 16)            304       
                                                                 
 max_pooling1d_33 (MaxPoolin  (None, 25, 16)           0         
 g1D)                                                            
                                                                 
 conv1d_34 (Conv1D)          (None, 25, 2

1/1 [==============================] - ETA: 0s - loss: 45.5173 - mean_squared_error: 45.5173 - rmse: 6.7467 - mean_absolute_error: 5.9030
Epoch 00012: val_loss did not improve from 17.10719
1/1 [==============================] - 0s 26ms/step - loss: 45.5173 - mean_squared_error: 45.5173 - rmse: 6.7467 - mean_absolute_error: 5.9030 - val_loss: 18.6993 - val_mean_squared_error: 18.6993 - val_rmse: 4.3243 - val_mean_absolute_error: 3.6566 - lr: 0.0010
Epoch 13/1000
1/1 [==============================] - ETA: 0s - loss: 37.7532 - mean_squared_error: 37.7532 - rmse: 6.1444 - mean_absolute_error: 4.3918
Epoch 00013: val_loss improved from 17.10719 to 16.55484, saving model to /tmp/lenet.h5
1/1 [==============================] - 0s 42ms/step - loss: 37.7532 - mean_squared_error: 37.7532 - rmse: 6.1444 - mean_absolute_error: 4.3918 - val_loss: 16.5548 - val_mean_squared_error: 16.5548 - val_rmse: 4.0688 - val_mean_absolute_error: 3.5872 - lr: 0.0010
Epoch 14/1000
1/1 [=========================

Epoch 30/1000
1/1 [==============================] - ETA: 0s - loss: 25.8541 - mean_squared_error: 25.8541 - rmse: 5.0847 - mean_absolute_error: 4.0397
Epoch 00030: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 26ms/step - loss: 25.8541 - mean_squared_error: 25.8541 - rmse: 5.0847 - mean_absolute_error: 4.0397 - val_loss: 17.5213 - val_mean_squared_error: 17.5213 - val_rmse: 4.1858 - val_mean_absolute_error: 3.8505 - lr: 0.0010
Epoch 31/1000
1/1 [==============================] - ETA: 0s - loss: 25.3980 - mean_squared_error: 25.3980 - rmse: 5.0396 - mean_absolute_error: 3.7888
Epoch 00031: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 28ms/step - loss: 25.3980 - mean_squared_error: 25.3980 - rmse: 5.0396 - mean_absolute_error: 3.7888 - val_loss: 16.6422 - val_mean_squared_error: 16.6422 - val_rmse: 4.0795 - val_mean_absolute_error: 3.7482 - lr: 0.0010
Epoch 32/1000
1/1 [==============================] - ETA: 0s - los

1/1 [==============================] - ETA: 0s - loss: 20.3973 - mean_squared_error: 20.3973 - rmse: 4.5163 - mean_absolute_error: 3.6941
Epoch 00047: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 28ms/step - loss: 20.3973 - mean_squared_error: 20.3973 - rmse: 4.5163 - mean_absolute_error: 3.6941 - val_loss: 27.8641 - val_mean_squared_error: 27.8641 - val_rmse: 5.2786 - val_mean_absolute_error: 4.4434 - lr: 5.0000e-04
Epoch 48/1000
1/1 [==============================] - ETA: 0s - loss: 18.8016 - mean_squared_error: 18.8016 - rmse: 4.3361 - mean_absolute_error: 3.2550
Epoch 00048: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 27ms/step - loss: 18.8016 - mean_squared_error: 18.8016 - rmse: 4.3361 - mean_absolute_error: 3.2550 - val_loss: 27.7232 - val_mean_squared_error: 27.7232 - val_rmse: 5.2653 - val_mean_absolute_error: 4.4374 - lr: 5.0000e-04
Epoch 49/1000
1/1 [==============================] - ETA: 0s - loss: 27.

1/1 [==============================] - ETA: 0s - loss: 20.9946 - mean_squared_error: 20.9946 - rmse: 4.5820 - mean_absolute_error: 3.7866
Epoch 00064: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 29ms/step - loss: 20.9946 - mean_squared_error: 20.9946 - rmse: 4.5820 - mean_absolute_error: 3.7866 - val_loss: 19.2547 - val_mean_squared_error: 19.2547 - val_rmse: 4.3880 - val_mean_absolute_error: 4.0007 - lr: 2.5000e-04
Epoch 65/1000
1/1 [==============================] - ETA: 0s - loss: 12.7812 - mean_squared_error: 12.7812 - rmse: 3.5751 - mean_absolute_error: 2.8546
Epoch 00065: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 33ms/step - loss: 12.7812 - mean_squared_error: 12.7812 - rmse: 3.5751 - mean_absolute_error: 2.8546 - val_loss: 19.2856 - val_mean_squared_error: 19.2856 - val_rmse: 4.3915 - val_mean_absolute_error: 4.0027 - lr: 2.5000e-04
Epoch 66/1000
1/1 [==============================] - ETA: 0s - loss: 19.

1/1 [==============================] - ETA: 0s - loss: 23.3481 - mean_squared_error: 23.3481 - rmse: 4.8320 - mean_absolute_error: 3.8182
Epoch 00081: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 27ms/step - loss: 23.3481 - mean_squared_error: 23.3481 - rmse: 4.8320 - mean_absolute_error: 3.8182 - val_loss: 21.7892 - val_mean_squared_error: 21.7892 - val_rmse: 4.6679 - val_mean_absolute_error: 4.1575 - lr: 1.2500e-04
Epoch 82/1000
1/1 [==============================] - ETA: 0s - loss: 24.7704 - mean_squared_error: 24.7704 - rmse: 4.9770 - mean_absolute_error: 4.0297
Epoch 00082: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 27ms/step - loss: 24.7704 - mean_squared_error: 24.7704 - rmse: 4.9770 - mean_absolute_error: 4.0297 - val_loss: 21.6583 - val_mean_squared_error: 21.6583 - val_rmse: 4.6539 - val_mean_absolute_error: 4.1499 - lr: 1.2500e-04
Epoch 83/1000
1/1 [==============================] - ETA: 0s - loss: 19.

1/1 [==============================] - ETA: 0s - loss: 23.8319 - mean_squared_error: 23.8319 - rmse: 4.8818 - mean_absolute_error: 3.9331
Epoch 00098: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 30ms/step - loss: 23.8319 - mean_squared_error: 23.8319 - rmse: 4.8818 - mean_absolute_error: 3.9331 - val_loss: 20.8308 - val_mean_squared_error: 20.8308 - val_rmse: 4.5641 - val_mean_absolute_error: 4.0994 - lr: 6.2500e-05
Epoch 99/1000
1/1 [==============================] - ETA: 0s - loss: 14.6284 - mean_squared_error: 14.6284 - rmse: 3.8247 - mean_absolute_error: 2.9530
Epoch 00099: val_loss did not improve from 15.95642
1/1 [==============================] - 0s 30ms/step - loss: 14.6284 - mean_squared_error: 14.6284 - rmse: 3.8247 - mean_absolute_error: 2.9530 - val_loss: 20.8554 - val_mean_squared_error: 20.8554 - val_rmse: 4.5668 - val_mean_absolute_error: 4.1009 - lr: 6.2500e-05
Epoch 100/1000
1/1 [==============================] - ETA: 0s - loss: 16

2/2 [==============================] - 0s 3ms/step - loss: 16.9177 - mean_squared_error: 16.9176 - rmse: 4.1131 - mean_absolute_error: 3.6413


In [32]:
df_lenet5, hisory_lenet5 = double_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.h5', 0.001, 0, 4, 3, X, y)

pooling layers: 4
Model: "model_9"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_10 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 conv1d_36 (Conv1D)          (None, 100, 6)            1302      
                                                                 
 max_pooling1d_36 (MaxPoolin  (None, 50, 6)            0         
 g1D)                                                            
                                                                 
 conv1d_37 (Conv1D)          (None, 50, 16)            304       
                                                                 
 max_pooling1d_37 (MaxPoolin  (None, 25, 16)           0         
 g1D)                                                            
                                                                 
 conv1d_38 (Conv1D)          (None, 25, 2

Epoch 12/1000
1/1 [==============================] - ETA: 0s - loss: 33.0930 - mean_squared_error: 33.0930 - rmse: 5.7526 - mean_absolute_error: 4.5218
Epoch 00012: val_loss improved from 8.58798 to 6.93875, saving model to /tmp/lenet.h5
1/1 [==============================] - 0s 55ms/step - loss: 33.0930 - mean_squared_error: 33.0930 - rmse: 5.7526 - mean_absolute_error: 4.5218 - val_loss: 6.9387 - val_mean_squared_error: 6.9387 - val_rmse: 2.6342 - val_mean_absolute_error: 2.0918 - lr: 0.0010
Epoch 13/1000
1/1 [==============================] - ETA: 0s - loss: 32.9906 - mean_squared_error: 32.9906 - rmse: 5.7437 - mean_absolute_error: 4.6076
Epoch 00013: val_loss did not improve from 6.93875
1/1 [==============================] - 0s 33ms/step - loss: 32.9906 - mean_squared_error: 32.9906 - rmse: 5.7437 - mean_absolute_error: 4.6076 - val_loss: 10.0628 - val_mean_squared_error: 10.0628 - val_rmse: 3.1722 - val_mean_absolute_error: 2.6987 - lr: 0.0010
Epoch 14/1000
1/1 [================

Epoch 30/1000
1/1 [==============================] - ETA: 0s - loss: 21.9111 - mean_squared_error: 21.9111 - rmse: 4.6809 - mean_absolute_error: 3.5481
Epoch 00030: val_loss did not improve from 6.91861
1/1 [==============================] - 0s 40ms/step - loss: 21.9111 - mean_squared_error: 21.9111 - rmse: 4.6809 - mean_absolute_error: 3.5481 - val_loss: 7.6060 - val_mean_squared_error: 7.6060 - val_rmse: 2.7579 - val_mean_absolute_error: 2.1718 - lr: 0.0010
Epoch 31/1000
1/1 [==============================] - ETA: 0s - loss: 23.6520 - mean_squared_error: 23.6520 - rmse: 4.8633 - mean_absolute_error: 3.8878
Epoch 00031: val_loss did not improve from 6.91861
1/1 [==============================] - 0s 54ms/step - loss: 23.6520 - mean_squared_error: 23.6520 - rmse: 4.8633 - mean_absolute_error: 3.8878 - val_loss: 7.0550 - val_mean_squared_error: 7.0550 - val_rmse: 2.6561 - val_mean_absolute_error: 2.1149 - lr: 0.0010
Epoch 32/1000
1/1 [==============================] - ETA: 0s - loss: 25.

Epoch 48/1000
1/1 [==============================] - ETA: 0s - loss: 24.7132 - mean_squared_error: 24.7132 - rmse: 4.9712 - mean_absolute_error: 3.8235
Epoch 00048: val_loss did not improve from 6.88245
1/1 [==============================] - 0s 37ms/step - loss: 24.7132 - mean_squared_error: 24.7132 - rmse: 4.9712 - mean_absolute_error: 3.8235 - val_loss: 7.4527 - val_mean_squared_error: 7.4527 - val_rmse: 2.7300 - val_mean_absolute_error: 2.1527 - lr: 0.0010
Epoch 49/1000
1/1 [==============================] - ETA: 0s - loss: 18.7482 - mean_squared_error: 18.7482 - rmse: 4.3299 - mean_absolute_error: 3.3264
Epoch 00049: val_loss did not improve from 6.88245
1/1 [==============================] - 0s 36ms/step - loss: 18.7482 - mean_squared_error: 18.7482 - rmse: 4.3299 - mean_absolute_error: 3.3264 - val_loss: 7.1249 - val_mean_squared_error: 7.1249 - val_rmse: 2.6692 - val_mean_absolute_error: 2.1098 - lr: 0.0010
Epoch 50/1000
1/1 [==============================] - ETA: 0s - loss: 20.

Epoch 66/1000
1/1 [==============================] - ETA: 0s - loss: 17.7181 - mean_squared_error: 17.7181 - rmse: 4.2093 - mean_absolute_error: 3.1790
Epoch 00066: val_loss did not improve from 6.88245
1/1 [==============================] - 0s 44ms/step - loss: 17.7181 - mean_squared_error: 17.7181 - rmse: 4.2093 - mean_absolute_error: 3.1790 - val_loss: 7.4196 - val_mean_squared_error: 7.4196 - val_rmse: 2.7239 - val_mean_absolute_error: 2.1438 - lr: 5.0000e-04
Epoch 67/1000
1/1 [==============================] - ETA: 0s - loss: 16.2641 - mean_squared_error: 16.2641 - rmse: 4.0329 - mean_absolute_error: 3.1176
Epoch 00067: val_loss did not improve from 6.88245
1/1 [==============================] - 0s 39ms/step - loss: 16.2641 - mean_squared_error: 16.2641 - rmse: 4.0329 - mean_absolute_error: 3.1176 - val_loss: 7.2717 - val_mean_squared_error: 7.2717 - val_rmse: 2.6966 - val_mean_absolute_error: 2.1212 - lr: 5.0000e-04
Epoch 68/1000
1/1 [==============================] - ETA: 0s - l

...

Epoch 119/1000
1/1 [==============================] - ETA: 0s - loss: 18.4128 - mean_squared_error: 18.4128 - rmse: 4.2910 - mean_absolute_error: 3.2633
Epoch 00119: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 34ms/step - loss: 18.4128 - mean_squared_error: 18.4128 - rmse: 4.2910 - mean_absolute_error: 3.2633 - val_loss: 7.9471 - val_mean_squared_error: 7.9471 - val_rmse: 2.8191 - val_mean_absolute_error: 2.2054 - lr: 6.2500e-05
Epoch 120/1000
1/1 [==============================] - ETA: 0s - loss: 16.2804 - mean_squared_error: 16.2804 - rmse: 4.0349 - mean_absolute_error: 3.0794
Epoch 00120: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 37ms/step - loss: 16.2804 - mean_squared_error: 16.2804 - rmse: 4.0349 - mean_absolute_error: 3.0794 - val_loss: 7.9151 - val_mean_squared_error: 7.9151 - val_rmse: 2.8134 - val_mean_absolute_error: 2.2021 - lr: 6.2500e-05
Epoch 121/1000
1/1 [==============================] - ETA: 0s 

Epoch 137/1000
1/1 [==============================] - ETA: 0s - loss: 19.1857 - mean_squared_error: 19.1857 - rmse: 4.3801 - mean_absolute_error: 3.4882
Epoch 00137: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 35ms/step - loss: 19.1857 - mean_squared_error: 19.1857 - rmse: 4.3801 - mean_absolute_error: 3.4882 - val_loss: 7.0428 - val_mean_squared_error: 7.0428 - val_rmse: 2.6538 - val_mean_absolute_error: 2.0931 - lr: 3.1250e-05
Epoch 138/1000
1/1 [==============================] - ETA: 0s - loss: 16.5334 - mean_squared_error: 16.5334 - rmse: 4.0661 - mean_absolute_error: 3.3417
Epoch 00138: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 34ms/step - loss: 16.5334 - mean_squared_error: 16.5334 - rmse: 4.0661 - mean_absolute_error: 3.3417 - val_loss: 7.0300 - val_mean_squared_error: 7.0300 - val_rmse: 2.6514 - val_mean_absolute_error: 2.0915 - lr: 3.1250e-05
Epoch 139/1000
1/1 [==============================] - ETA: 0s 

Epoch 155/1000
1/1 [==============================] - ETA: 0s - loss: 20.5569 - mean_squared_error: 20.5569 - rmse: 4.5340 - mean_absolute_error: 3.4778
Epoch 00155: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 37ms/step - loss: 20.5569 - mean_squared_error: 20.5569 - rmse: 4.5340 - mean_absolute_error: 3.4778 - val_loss: 7.1461 - val_mean_squared_error: 7.1461 - val_rmse: 2.6732 - val_mean_absolute_error: 2.1070 - lr: 3.1250e-05
Epoch 156/1000
1/1 [==============================] - ETA: 0s - loss: 15.8046 - mean_squared_error: 15.8046 - rmse: 3.9755 - mean_absolute_error: 3.1250
Epoch 00156: val_loss did not improve from 6.80596

Epoch 00156: ReduceLROnPlateau reducing learning rate to 1.5625000742147677e-05.
1/1 [==============================] - 0s 40ms/step - loss: 15.8046 - mean_squared_error: 15.8046 - rmse: 3.9755 - mean_absolute_error: 3.1250 - val_loss: 7.1620 - val_mean_squared_error: 7.1620 - val_rmse: 2.6762 - val_mean_absolute_error: 2.10

1/1 [==============================] - ETA: 0s - loss: 17.9781 - mean_squared_error: 17.9781 - rmse: 4.2401 - mean_absolute_error: 3.4333
Epoch 00172: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 51ms/step - loss: 17.9781 - mean_squared_error: 17.9781 - rmse: 4.2401 - mean_absolute_error: 3.4333 - val_loss: 7.3282 - val_mean_squared_error: 7.3282 - val_rmse: 2.7071 - val_mean_absolute_error: 2.1341 - lr: 1.5625e-05
Epoch 173/1000
1/1 [==============================] - ETA: 0s - loss: 15.6937 - mean_squared_error: 15.6937 - rmse: 3.9615 - mean_absolute_error: 3.0068
Epoch 00173: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 38ms/step - loss: 15.6937 - mean_squared_error: 15.6937 - rmse: 3.9615 - mean_absolute_error: 3.0068 - val_loss: 7.3343 - val_mean_squared_error: 7.3343 - val_rmse: 2.7082 - val_mean_absolute_error: 2.1350 - lr: 1.5625e-05
Epoch 174/1000
1/1 [==============================] - ETA: 0s - loss: 19.8449

Epoch 190/1000
1/1 [==============================] - ETA: 0s - loss: 16.1740 - mean_squared_error: 16.1740 - rmse: 4.0217 - mean_absolute_error: 3.1569
Epoch 00190: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 34ms/step - loss: 16.1740 - mean_squared_error: 16.1740 - rmse: 4.0217 - mean_absolute_error: 3.1569 - val_loss: 7.2993 - val_mean_squared_error: 7.2993 - val_rmse: 2.7017 - val_mean_absolute_error: 2.1303 - lr: 7.8125e-06
Epoch 191/1000
1/1 [==============================] - ETA: 0s - loss: 18.7145 - mean_squared_error: 18.7145 - rmse: 4.3260 - mean_absolute_error: 3.3402
Epoch 00191: val_loss did not improve from 6.80596
1/1 [==============================] - 0s 35ms/step - loss: 18.7145 - mean_squared_error: 18.7145 - rmse: 4.3260 - mean_absolute_error: 3.3402 - val_loss: 7.3016 - val_mean_squared_error: 7.3016 - val_rmse: 2.7021 - val_mean_absolute_error: 2.1307 - lr: 7.8125e-06
Epoch 192/1000
1/1 [==============================] - ETA: 0s 

In [33]:
df_lenet6, hisory_lenet6 = double_cross_site(cnn_lenet, 'cnn_lenet', '/tmp/lenet.h5', 0.001, 3, 4, 0, X, y)

pooling layers: 4
Model: "model_10"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_11 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 conv1d_40 (Conv1D)          (None, 100, 6)            1302      
                                                                 
 max_pooling1d_40 (MaxPoolin  (None, 50, 6)            0         
 g1D)                                                            
                                                                 
 conv1d_41 (Conv1D)          (None, 50, 16)            304       
                                                                 
 max_pooling1d_41 (MaxPoolin  (None, 25, 16)           0         
 g1D)                                                            
                                                                 
 conv1d_42 (Conv1D)          (None, 25, 

Epoch 12/1000
1/1 [==============================] - ETA: 0s - loss: 29.0010 - mean_squared_error: 29.0010 - rmse: 5.3853 - mean_absolute_error: 4.2981
Epoch 00012: val_loss improved from 34.49763 to 18.67783, saving model to /tmp/lenet.h5
1/1 [==============================] - 0s 53ms/step - loss: 29.0010 - mean_squared_error: 29.0010 - rmse: 5.3853 - mean_absolute_error: 4.2981 - val_loss: 18.6778 - val_mean_squared_error: 18.6778 - val_rmse: 4.3218 - val_mean_absolute_error: 3.1728 - lr: 0.0010
Epoch 13/1000
1/1 [==============================] - ETA: 0s - loss: 22.3344 - mean_squared_error: 22.3344 - rmse: 4.7259 - mean_absolute_error: 3.5956
Epoch 00013: val_loss improved from 18.67783 to 11.58398, saving model to /tmp/lenet.h5
1/1 [==============================] - 0s 58ms/step - loss: 22.3344 - mean_squared_error: 22.3344 - rmse: 4.7259 - mean_absolute_error: 3.5956 - val_loss: 11.5840 - val_mean_squared_error: 11.5840 - val_rmse: 3.4035 - val_mean_absolute_error: 2.9090 - lr: 0

Epoch 30/1000
1/1 [==============================] - ETA: 0s - loss: 19.9712 - mean_squared_error: 19.9712 - rmse: 4.4689 - mean_absolute_error: 3.6868
Epoch 00030: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 39ms/step - loss: 19.9712 - mean_squared_error: 19.9712 - rmse: 4.4689 - mean_absolute_error: 3.6868 - val_loss: 16.9847 - val_mean_squared_error: 16.9847 - val_rmse: 4.1212 - val_mean_absolute_error: 3.0635 - lr: 0.0010
Epoch 31/1000
1/1 [==============================] - ETA: 0s - loss: 16.4736 - mean_squared_error: 16.4736 - rmse: 4.0588 - mean_absolute_error: 3.1234
Epoch 00031: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 38ms/step - loss: 16.4736 - mean_squared_error: 16.4736 - rmse: 4.0588 - mean_absolute_error: 3.1234 - val_loss: 15.0520 - val_mean_squared_error: 15.0520 - val_rmse: 3.8797 - val_mean_absolute_error: 2.9649 - lr: 0.0010
Epoch 32/1000
1/1 [==============================] - ETA: 0s - los

1/1 [==============================] - ETA: 0s - loss: 18.5914 - mean_squared_error: 18.5914 - rmse: 4.3118 - mean_absolute_error: 3.2900
Epoch 00047: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 36ms/step - loss: 18.5914 - mean_squared_error: 18.5914 - rmse: 4.3118 - mean_absolute_error: 3.2900 - val_loss: 15.3117 - val_mean_squared_error: 15.3117 - val_rmse: 3.9130 - val_mean_absolute_error: 2.9747 - lr: 5.0000e-04
Epoch 48/1000
1/1 [==============================] - ETA: 0s - loss: 18.7963 - mean_squared_error: 18.7963 - rmse: 4.3355 - mean_absolute_error: 3.2678
Epoch 00048: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 39ms/step - loss: 18.7963 - mean_squared_error: 18.7963 - rmse: 4.3355 - mean_absolute_error: 3.2678 - val_loss: 15.7047 - val_mean_squared_error: 15.7047 - val_rmse: 3.9629 - val_mean_absolute_error: 2.9951 - lr: 5.0000e-04
Epoch 49/1000
1/1 [==============================] - ETA: 0s - loss: 18.

1/1 [==============================] - ETA: 0s - loss: 18.5157 - mean_squared_error: 18.5157 - rmse: 4.3030 - mean_absolute_error: 3.3151
Epoch 00064: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 38ms/step - loss: 18.5157 - mean_squared_error: 18.5157 - rmse: 4.3030 - mean_absolute_error: 3.3151 - val_loss: 13.9897 - val_mean_squared_error: 13.9897 - val_rmse: 3.7403 - val_mean_absolute_error: 2.8965 - lr: 2.5000e-04
Epoch 65/1000
1/1 [==============================] - ETA: 0s - loss: 22.1235 - mean_squared_error: 22.1235 - rmse: 4.7036 - mean_absolute_error: 3.7550
Epoch 00065: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 35ms/step - loss: 22.1235 - mean_squared_error: 22.1235 - rmse: 4.7036 - mean_absolute_error: 3.7550 - val_loss: 13.9158 - val_mean_squared_error: 13.9158 - val_rmse: 3.7304 - val_mean_absolute_error: 2.8917 - lr: 2.5000e-04
Epoch 66/1000
1/1 [==============================] - ETA: 0s - loss: 21.

1/1 [==============================] - ETA: 0s - loss: 18.8372 - mean_squared_error: 18.8372 - rmse: 4.3402 - mean_absolute_error: 3.4080
Epoch 00081: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 32ms/step - loss: 18.8372 - mean_squared_error: 18.8372 - rmse: 4.3402 - mean_absolute_error: 3.4080 - val_loss: 14.6509 - val_mean_squared_error: 14.6509 - val_rmse: 3.8277 - val_mean_absolute_error: 2.9357 - lr: 1.2500e-04
Epoch 82/1000
1/1 [==============================] - ETA: 0s - loss: 17.4905 - mean_squared_error: 17.4905 - rmse: 4.1822 - mean_absolute_error: 3.2596
Epoch 00082: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 49ms/step - loss: 17.4905 - mean_squared_error: 17.4905 - rmse: 4.1822 - mean_absolute_error: 3.2596 - val_loss: 14.6633 - val_mean_squared_error: 14.6633 - val_rmse: 3.8293 - val_mean_absolute_error: 2.9363 - lr: 1.2500e-04
Epoch 83/1000
1/1 [==============================] - ETA: 0s - loss: 17.

1/1 [==============================] - ETA: 0s - loss: 19.3119 - mean_squared_error: 19.3119 - rmse: 4.3945 - mean_absolute_error: 3.5021
Epoch 00098: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 36ms/step - loss: 19.3119 - mean_squared_error: 19.3119 - rmse: 4.3945 - mean_absolute_error: 3.5021 - val_loss: 14.6074 - val_mean_squared_error: 14.6074 - val_rmse: 3.8220 - val_mean_absolute_error: 2.9318 - lr: 6.2500e-05
Epoch 99/1000
1/1 [==============================] - ETA: 0s - loss: 17.1029 - mean_squared_error: 17.1029 - rmse: 4.1356 - mean_absolute_error: 3.2867
Epoch 00099: val_loss did not improve from 11.58398
1/1 [==============================] - 0s 38ms/step - loss: 17.1029 - mean_squared_error: 17.1029 - rmse: 4.1356 - mean_absolute_error: 3.2867 - val_loss: 14.6135 - val_mean_squared_error: 14.6135 - val_rmse: 3.8228 - val_mean_absolute_error: 2.9320 - lr: 6.2500e-05
Epoch 100/1000
1/1 [==============================] - ETA: 0s - loss: 17

In [34]:
df_lenet_2 = (df_lenet4.merge(df_lenet5, how='outer')).merge(df_lenet6, how='outer')

In [35]:
df_lenet_2

Model Train_site  Test_site Metric      Value
0   cnn_lenet       0, 3          0    MSE  14.499567
1   cnn_lenet       0, 3          0   RMSE   3.807830
2   cnn_lenet       0, 3          0    MAE   3.314900
3   cnn_lenet       0, 3          0   coef   0.221875
4   cnn_lenet       0, 3          3    MSE  13.346354
5   cnn_lenet       0, 3          3   RMSE   3.653266
6   cnn_lenet       0, 3          3    MAE   2.917012
7   cnn_lenet       0, 3          3   coef   0.052326
8   cnn_lenet       0, 3          4    MSE  16.917648
9   cnn_lenet       0, 3          4   RMSE   4.113107
10  cnn_lenet       0, 3          4    MAE   3.641336
11  cnn_lenet       0, 3          4   coef   0.189159
12  cnn_lenet       0, 4          0    MSE  11.730642
13  cnn_lenet       0, 4          0   RMSE   3.425003
14  cnn_lenet       0, 4          0    MAE   2.595923
15  cnn_lenet       0, 4          0   coef   0.252450
16  cnn_lenet       0, 4          4    MSE  10.804939
17  cnn_lenet       0, 4          4   RMSE   3.287087
18  cnn_lenet       0, 4          4    MAE   2.361628
19  cnn_lenet       0, 4          4   coef   0.313571
20  cnn_lenet       0, 4          3    MSE  14.794165
21  cnn_lenet       0, 4          3   RMSE   3.846318
22  cnn_lenet       0, 4          3    MAE   2.925367
23  cnn_lenet       0, 4          3   coef   0.102050
24  cnn_lenet       3, 4          3    MSE  10.552709
25  cnn_lenet       3, 4          3   RMSE   3.248493
26  cnn_lenet       3, 4          3    MAE   2.709475
27  cnn_lenet       3, 4          3   coef   0.417087
28  cnn_lenet       3, 4          4    MSE  14.053055
29  cnn_lenet       3, 4          4   RMSE   3.748740
30  cnn_lenet       3, 4          4    MAE   3.362711
31  cnn_lenet       3, 4          4   coef   0.256354
32  cnn_lenet       3, 4          0    MSE  13.831536
33  cnn_lenet       3, 4          0   RMSE   3.719077
34  cnn_lenet       3, 4          0    MAE   3.197613
35  cnn_lenet       3, 4          0   coef   0.224804

#### cost 0

In [47]:
cost0 = df_lenet_1[(df_lenet_1['Metric'] == 'MAE') & (df_lenet_1["Test_site"] == 0)]

Model  Train_site  Test_site Metric     Value
2   cnn_lenet           0          0    MAE  1.794308
18  cnn_lenet           3          0    MAE  2.747266
30  cnn_lenet           4          0    MAE  2.576798

In [125]:
cost0_3 = cost0[cost0['Train_site'] == 3]['Value'].values - cost0[cost0['Train_site'] == 0]['Value'].values
cost0_4 = cost0[cost0['Train_site'] == 4]['Value'].values - cost0[cost0['Train_site'] == 0]['Value'].values

In [143]:
cost0_3, cost0_4

(array([0.95295775]), array([0.78249013]))

In [144]:
cost0_mean = np.mean([cost0_3, cost0_4])

In [130]:
cost0_0 = df_lenet_2[(df_lenet_2['Metric'] == 'MAE') & (df_lenet_2["Test_site"] == 0)]

In [139]:
cost0_34 = cost0_0[cost0_0['Train_site'] == '3, 4']['Value'].values - cost0[cost0['Train_site'] == 0]['Value'].values

In [141]:
cost0_34

array([1.40330493])

#### cost 3

In [145]:
cost3 = df_lenet_1[(df_lenet_1['Metric'] == 'MAE') & (df_lenet_1["Test_site"] == 3)]

In [146]:
cost3

Model  Train_site  Test_site Metric     Value
6   cnn_lenet           0          3    MAE  2.835977
14  cnn_lenet           3          3    MAE  2.508021
34  cnn_lenet           4          3    MAE  2.893921

In [147]:
cost3_0 = cost3[cost3['Train_site'] == 0]['Value'].values - cost3[cost3['Train_site'] == 3]['Value'].values
cost3_4 = cost3[cost3['Train_site'] == 4]['Value'].values - cost3[cost3['Train_site'] == 3]['Value'].values

In [148]:
cost3_0, cost3_4

(array([0.32795596]), array([0.38590002]))

In [149]:
cost3_mean = np.mean([cost3_0, cost3_4])

In [150]:
cost3_mean

0.3569279909133911

In [151]:
cost3_3 = df_lenet_2[(df_lenet_2['Metric'] == 'MAE') & (df_lenet_2["Test_site"] == 3)]

In [154]:
cost3_3

Model Train_site  Test_site Metric     Value
6   cnn_lenet       0, 3          3    MAE  2.917012
22  cnn_lenet       0, 4          3    MAE  2.925367
26  cnn_lenet       3, 4          3    MAE  2.709475

In [152]:
cost3_04 = cost3_3[cost3_3['Train_site'] == '0, 4']['Value'].values - cost3[cost3['Train_site'] == 3]['Value'].values

In [153]:
cost3_04

array([0.417346])

#### cost 4

In [155]:
cost4 = df_lenet_1[(df_lenet_1['Metric'] == 'MAE') & (df_lenet_1["Test_site"] == 4)]

In [156]:
cost4

Model  Train_site  Test_site Metric     Value
10  cnn_lenet           0          4    MAE  3.189179
22  cnn_lenet           3          4    MAE  2.612432
26  cnn_lenet           4          4    MAE  2.199979

In [157]:
cost4_0 = cost4[cost4['Train_site'] == 0]['Value'].values - cost4[cost4['Train_site'] == 4]['Value'].values
cost4_3 = cost4[cost4['Train_site'] == 3]['Value'].values - cost4[cost4['Train_site'] == 4]['Value'].values

In [158]:
cost4_mean = np.mean([cost4_0, cost4_3])

In [163]:
cost4_mean

0.7008271217346191

In [159]:
cost4_4 = df_lenet_2[(df_lenet_2['Metric'] == 'MAE') & (df_lenet_2["Test_site"] == 4)]

In [160]:
cost4_4

Model Train_site  Test_site Metric     Value
10  cnn_lenet       0, 3          4    MAE  3.641336
18  cnn_lenet       0, 4          4    MAE  2.361628
30  cnn_lenet       3, 4          4    MAE  3.362711

In [161]:
cost4_03 = cost4_4[cost4_4['Train_site'] == '0, 3']['Value'].values - cost4[cost4['Train_site'] == 4]['Value'].values

In [162]:
cost4_03

array([1.44135761])

### mlp4

#### single-cross-site

In [65]:
df_mlp41, history_mlp41 = single_cross_site(mlp4, 'mlp4', '/tmp/mlp4.m5', 0.001, 0, 3, 4, X, y)
df_mlp42, history_mlp42 = single_cross_site(mlp4, 'mlp4', '/tmp/mlp4.m5', 0.001, 3, 0, 4, X, y)
df_mlp43, history_mlp43 = single_cross_site(mlp4, 'mlp4', '/tmp/mlp4.m5', 0.001, 4, 0, 3, X, y)

Model: "model_11"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_12 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 flatten_11 (Flatten)        (None, 7200)              0         
                                                                 
 dropout_22 (Dropout)        (None, 7200)              0         
                                                                 
 dense_33 (Dense)            (None, 500)               3600500   
                                                                 
 dropout_23 (Dropout)        (None, 500)               0         
                                                                 
 dense_34 (Dense)            (None, 500)               250500    
                                                                 
 dropout_24 (Dropout)        (None, 500)               0  

Epoch 15/1000
4/4 [==============================] - ETA: 0s - loss: 12.3087 - mean_squared_error: 12.3087 - rmse: 3.5084 - mean_absolute_error: 2.8514
Epoch 00015: val_loss did not improve from 8.64317
4/4 [==============================] - 0s 31ms/step - loss: 12.3087 - mean_squared_error: 12.3087 - rmse: 3.5084 - mean_absolute_error: 2.8514 - val_loss: 12.0291 - val_mean_squared_error: 12.0291 - val_rmse: 3.4683 - val_mean_absolute_error: 2.5307 - lr: 0.0010
Epoch 16/1000
4/4 [==============================] - ETA: 0s - loss: 11.7966 - mean_squared_error: 11.7966 - rmse: 3.4346 - mean_absolute_error: 2.7939
Epoch 00016: val_loss did not improve from 8.64317
4/4 [==============================] - 0s 27ms/step - loss: 11.7966 - mean_squared_error: 11.7966 - rmse: 3.4346 - mean_absolute_error: 2.7939 - val_loss: 9.7820 - val_mean_squared_error: 9.7820 - val_rmse: 3.1276 - val_mean_absolute_error: 2.3287 - lr: 0.0010
Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 1

Epoch 33/1000
4/4 [==============================] - ETA: 0s - loss: 11.2328 - mean_squared_error: 11.2328 - rmse: 3.3515 - mean_absolute_error: 2.7315
Epoch 00033: val_loss did not improve from 8.53091
4/4 [==============================] - 0s 26ms/step - loss: 11.2328 - mean_squared_error: 11.2328 - rmse: 3.3515 - mean_absolute_error: 2.7315 - val_loss: 14.8707 - val_mean_squared_error: 14.8707 - val_rmse: 3.8563 - val_mean_absolute_error: 2.8642 - lr: 0.0010
Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 11.8330 - mean_squared_error: 11.8330 - rmse: 3.4399 - mean_absolute_error: 2.7618
Epoch 00034: val_loss did not improve from 8.53091
4/4 [==============================] - 0s 24ms/step - loss: 11.8330 - mean_squared_error: 11.8330 - rmse: 3.4399 - mean_absolute_error: 2.7618 - val_loss: 8.8613 - val_mean_squared_error: 8.8613 - val_rmse: 2.9768 - val_mean_absolute_error: 2.2191 - lr: 0.0010
Epoch 35/1000
4/4 [==============================] - ETA: 0s - loss: 1

Epoch 51/1000
4/4 [==============================] - ETA: 0s - loss: 10.5899 - mean_squared_error: 10.5899 - rmse: 3.2542 - mean_absolute_error: 2.6560
Epoch 00051: val_loss did not improve from 6.88219
4/4 [==============================] - 0s 26ms/step - loss: 10.5899 - mean_squared_error: 10.5899 - rmse: 3.2542 - mean_absolute_error: 2.6560 - val_loss: 13.5316 - val_mean_squared_error: 13.5316 - val_rmse: 3.6785 - val_mean_absolute_error: 2.7729 - lr: 0.0010
Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 10.6033 - mean_squared_error: 10.6033 - rmse: 3.2563 - mean_absolute_error: 2.5870
Epoch 00052: val_loss did not improve from 6.88219
4/4 [==============================] - 0s 26ms/step - loss: 10.6033 - mean_squared_error: 10.6033 - rmse: 3.2563 - mean_absolute_error: 2.5870 - val_loss: 8.1355 - val_mean_squared_error: 8.1355 - val_rmse: 2.8523 - val_mean_absolute_error: 2.1222 - lr: 0.0010
Epoch 53/1000
4/4 [==============================] - ETA: 0s - loss: 1

Epoch 69/1000
4/4 [==============================] - ETA: 0s - loss: 8.0314 - mean_squared_error: 8.0314 - rmse: 2.8340 - mean_absolute_error: 2.2225
Epoch 00069: val_loss did not improve from 4.94310
4/4 [==============================] - 0s 25ms/step - loss: 8.0314 - mean_squared_error: 8.0314 - rmse: 2.8340 - mean_absolute_error: 2.2225 - val_loss: 7.8044 - val_mean_squared_error: 7.8044 - val_rmse: 2.7936 - val_mean_absolute_error: 2.1114 - lr: 0.0010
Epoch 70/1000
4/4 [==============================] - ETA: 0s - loss: 7.8266 - mean_squared_error: 7.8266 - rmse: 2.7976 - mean_absolute_error: 2.1823
Epoch 00070: val_loss did not improve from 4.94310
4/4 [==============================] - 0s 24ms/step - loss: 7.8266 - mean_squared_error: 7.8266 - rmse: 2.7976 - mean_absolute_error: 2.1823 - val_loss: 8.4967 - val_mean_squared_error: 8.4967 - val_rmse: 2.9149 - val_mean_absolute_error: 2.2190 - lr: 0.0010
Epoch 71/1000
4/4 [==============================] - ETA: 0s - loss: 8.2528 - me

...

Epoch 30/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.4273 - mean_squared_error: 13.4273 - rmse: 3.6643 - mean_absolute_error: 3.1701
Epoch 00030: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 41ms/step - loss: 13.4537 - mean_squared_error: 13.4537 - rmse: 3.6679 - mean_absolute_error: 3.1509 - val_loss: 13.5604 - val_mean_squared_error: 13.5604 - val_rmse: 3.6824 - val_mean_absolute_error: 2.8291 - lr: 5.0000e-04
Epoch 31/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.6557 - mean_squared_error: 14.6557 - rmse: 3.8283 - mean_absolute_error: 3.1227
Epoch 00031: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 40ms/step - loss: 15.7408 - mean_squared_error: 15.7408 - rmse: 3.9675 - mean_absolute_error: 3.2510 - val_loss: 13.8867 - val_mean_squared_error: 13.8867 - val_rmse: 3.7265 - val_mean_absolute_error: 2.8544 - lr: 5.0000e-04
Epoch 32/1000
1/2 [==============>...............] - ETA: 

1/2 [==============>...............] - ETA: 0s - loss: 13.5158 - mean_squared_error: 13.5158 - rmse: 3.6764 - mean_absolute_error: 3.0340
Epoch 00047: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 42ms/step - loss: 14.1212 - mean_squared_error: 14.1212 - rmse: 3.7578 - mean_absolute_error: 3.0832 - val_loss: 19.0208 - val_mean_squared_error: 19.0208 - val_rmse: 4.3613 - val_mean_absolute_error: 3.2724 - lr: 2.5000e-04
Epoch 48/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.5997 - mean_squared_error: 13.5997 - rmse: 3.6878 - mean_absolute_error: 2.9965
Epoch 00048: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 46ms/step - loss: 14.3098 - mean_squared_error: 14.3098 - rmse: 3.7828 - mean_absolute_error: 3.0729 - val_loss: 20.6933 - val_mean_squared_error: 20.6933 - val_rmse: 4.5490 - val_mean_absolute_error: 3.4254 - lr: 2.5000e-04
Epoch 49/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.

Epoch 65/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.4070 - mean_squared_error: 13.4070 - rmse: 3.6616 - mean_absolute_error: 2.9439
Epoch 00065: val_loss did not improve from 11.83063

Epoch 00065: ReduceLROnPlateau reducing learning rate to 0.0001250000059371814.
2/2 [==============================] - 0s 41ms/step - loss: 13.3436 - mean_squared_error: 13.3436 - rmse: 3.6529 - mean_absolute_error: 2.9878 - val_loss: 13.9132 - val_mean_squared_error: 13.9132 - val_rmse: 3.7300 - val_mean_absolute_error: 2.8291 - lr: 2.5000e-04
Epoch 66/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.6148 - mean_squared_error: 13.6148 - rmse: 3.6898 - mean_absolute_error: 3.0873
Epoch 00066: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 44ms/step - loss: 13.4007 - mean_squared_error: 13.4007 - rmse: 3.6607 - mean_absolute_error: 3.0463 - val_loss: 13.6041 - val_mean_squared_error: 13.6041 - val_rmse: 3.6884 - val_mean_absolute_error: 2

1/2 [==============>...............] - ETA: 0s - loss: 12.1789 - mean_squared_error: 12.1789 - rmse: 3.4898 - mean_absolute_error: 2.8820
Epoch 00082: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 44ms/step - loss: 13.1513 - mean_squared_error: 13.1513 - rmse: 3.6265 - mean_absolute_error: 2.9759 - val_loss: 16.2414 - val_mean_squared_error: 16.2414 - val_rmse: 4.0301 - val_mean_absolute_error: 3.0290 - lr: 1.2500e-04
Epoch 83/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.9400 - mean_squared_error: 12.9400 - rmse: 3.5972 - mean_absolute_error: 2.8378
Epoch 00083: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 42ms/step - loss: 12.5843 - mean_squared_error: 12.5843 - rmse: 3.5474 - mean_absolute_error: 2.8173 - val_loss: 16.3787 - val_mean_squared_error: 16.3787 - val_rmse: 4.0471 - val_mean_absolute_error: 3.0407 - lr: 1.2500e-04
Epoch 84/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.

1/2 [==============>...............] - ETA: 0s - loss: 12.7307 - mean_squared_error: 12.7307 - rmse: 3.5680 - mean_absolute_error: 2.9134
Epoch 00099: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 40ms/step - loss: 13.0730 - mean_squared_error: 13.0730 - rmse: 3.6157 - mean_absolute_error: 2.9187 - val_loss: 16.8116 - val_mean_squared_error: 16.8116 - val_rmse: 4.1002 - val_mean_absolute_error: 3.0708 - lr: 6.2500e-05
Epoch 100/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.0052 - mean_squared_error: 12.0052 - rmse: 3.4649 - mean_absolute_error: 2.8194
Epoch 00100: val_loss did not improve from 11.83063
2/2 [==============================] - 0s 42ms/step - loss: 11.9599 - mean_squared_error: 11.9599 - rmse: 3.4583 - mean_absolute_error: 2.8076 - val_loss: 16.7339 - val_mean_squared_error: 16.7339 - val_rmse: 4.0907 - val_mean_absolute_error: 3.0646 - lr: 6.2500e-05
Epoch 101/1000
1/2 [==============>...............] - ETA: 0s - loss: 1

In [66]:
df_mlp4_1 = (df_mlp41.merge(df_mlp42, how='outer')).merge(df_mlp43, how='outer')

#### double-cross-site

In [67]:
df_mlp44, hisory_mlp44 = double_cross_site(mlp4, 'mlp4', '/tmp/mlp4.h5', 0.001, 0, 3, 4, X, y)
df_mlp45, hisory_mlp45 = double_cross_site(mlp4, 'mlp4', '/tmp/mlp4.h5', 0.001, 0, 4, 3, X, y)
df_mlp46, hisory_mlp46 = double_cross_site(mlp4, 'mlp4', '/tmp/mlp4.h5', 0.001, 3, 4, 0, X, y)

Model: "model_14"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_15 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 flatten_14 (Flatten)        (None, 7200)              0         
                                                                 
 dropout_34 (Dropout)        (None, 7200)              0         
                                                                 
 dense_45 (Dense)            (None, 500)               3600500   
                                                                 
 dropout_35 (Dropout)        (None, 500)               0         
                                                                 
 dense_46 (Dense)            (None, 500)               250500    
                                                                 
 dropout_36 (Dropout)        (None, 500)               0  

Epoch 15/1000
1/1 [==============================] - ETA: 0s - loss: 6.0507 - mean_squared_error: 6.0507 - rmse: 2.4598 - mean_absolute_error: 2.0384
Epoch 00015: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 59ms/step - loss: 6.0507 - mean_squared_error: 6.0507 - rmse: 2.4598 - mean_absolute_error: 2.0384 - val_loss: 44.8950 - val_mean_squared_error: 44.8950 - val_rmse: 6.7004 - val_mean_absolute_error: 5.7161 - lr: 0.0010
Epoch 16/1000
1/1 [==============================] - ETA: 0s - loss: 14.0854 - mean_squared_error: 14.0854 - rmse: 3.7531 - mean_absolute_error: 2.8546
Epoch 00016: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 40ms/step - loss: 14.0854 - mean_squared_error: 14.0854 - rmse: 3.7531 - mean_absolute_error: 2.8546 - val_loss: 45.5770 - val_mean_squared_error: 45.5770 - val_rmse: 6.7511 - val_mean_absolute_error: 5.7634 - lr: 0.0010
Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 1

Epoch 33/1000
1/1 [==============================] - ETA: 0s - loss: 6.2000 - mean_squared_error: 6.2000 - rmse: 2.4900 - mean_absolute_error: 1.9748
Epoch 00033: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 41ms/step - loss: 6.2000 - mean_squared_error: 6.2000 - rmse: 2.4900 - mean_absolute_error: 1.9748 - val_loss: 32.9345 - val_mean_squared_error: 32.9345 - val_rmse: 5.7389 - val_mean_absolute_error: 4.8952 - lr: 5.0000e-04
Epoch 34/1000
1/1 [==============================] - ETA: 0s - loss: 9.3111 - mean_squared_error: 9.3111 - rmse: 3.0514 - mean_absolute_error: 2.5200
Epoch 00034: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 37ms/step - loss: 9.3111 - mean_squared_error: 9.3111 - rmse: 3.0514 - mean_absolute_error: 2.5200 - val_loss: 34.8387 - val_mean_squared_error: 34.8387 - val_rmse: 5.9024 - val_mean_absolute_error: 5.0267 - lr: 5.0000e-04
Epoch 35/1000
1/1 [==============================] - ETA: 0s - los

Epoch 51/1000
1/1 [==============================] - ETA: 0s - loss: 7.4069 - mean_squared_error: 7.4069 - rmse: 2.7216 - mean_absolute_error: 2.1536
Epoch 00051: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 38ms/step - loss: 7.4069 - mean_squared_error: 7.4069 - rmse: 2.7216 - mean_absolute_error: 2.1536 - val_loss: 37.6995 - val_mean_squared_error: 37.6995 - val_rmse: 6.1400 - val_mean_absolute_error: 5.2085 - lr: 2.5000e-04
Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 6.8562 - mean_squared_error: 6.8562 - rmse: 2.6184 - mean_absolute_error: 2.0950
Epoch 00052: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 41ms/step - loss: 6.8562 - mean_squared_error: 6.8562 - rmse: 2.6184 - mean_absolute_error: 2.0950 - val_loss: 37.6239 - val_mean_squared_error: 37.6239 - val_rmse: 6.1338 - val_mean_absolute_error: 5.2038 - lr: 2.5000e-04
Epoch 53/1000
1/1 [==============================] - ETA: 0s - los

Epoch 69/1000
1/1 [==============================] - ETA: 0s - loss: 7.1102 - mean_squared_error: 7.1102 - rmse: 2.6665 - mean_absolute_error: 2.1233
Epoch 00069: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 43ms/step - loss: 7.1102 - mean_squared_error: 7.1102 - rmse: 2.6665 - mean_absolute_error: 2.1233 - val_loss: 37.7628 - val_mean_squared_error: 37.7628 - val_rmse: 6.1451 - val_mean_absolute_error: 5.2067 - lr: 1.2500e-04
Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 5.8646 - mean_squared_error: 5.8646 - rmse: 2.4217 - mean_absolute_error: 1.8866
Epoch 00070: val_loss did not improve from 12.27122
1/1 [==============================] - 0s 43ms/step - loss: 5.8646 - mean_squared_error: 5.8646 - rmse: 2.4217 - mean_absolute_error: 1.8866 - val_loss: 37.6470 - val_mean_squared_error: 37.6470 - val_rmse: 6.1357 - val_mean_absolute_error: 5.1983 - lr: 1.2500e-04
Epoch 71/1000
1/1 [==============================] - ETA: 0s - los

...

Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 14.1890 - mean_squared_error: 14.1890 - rmse: 3.7668 - mean_absolute_error: 2.9721
Epoch 00036: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 46ms/step - loss: 14.1890 - mean_squared_error: 14.1890 - rmse: 3.7668 - mean_absolute_error: 2.9721 - val_loss: 14.8168 - val_mean_squared_error: 14.8168 - val_rmse: 3.8493 - val_mean_absolute_error: 2.6983 - lr: 5.0000e-04
Epoch 37/1000
1/1 [==============================] - ETA: 0s - loss: 16.1530 - mean_squared_error: 16.1530 - rmse: 4.0191 - mean_absolute_error: 3.1824
Epoch 00037: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 48ms/step - loss: 16.1530 - mean_squared_error: 16.1530 - rmse: 4.0191 - mean_absolute_error: 3.1824 - val_loss: 14.2281 - val_mean_squared_error: 14.2281 - val_rmse: 3.7720 - val_mean_absolute_error: 2.6471 - lr: 5.0000e-04
Epoch 38/1000
1/1 [==============================] - ETA: 

1/1 [==============================] - ETA: 0s - loss: 14.6433 - mean_squared_error: 14.6433 - rmse: 3.8267 - mean_absolute_error: 3.0157
Epoch 00053: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 47ms/step - loss: 14.6433 - mean_squared_error: 14.6433 - rmse: 3.8267 - mean_absolute_error: 3.0157 - val_loss: 12.6090 - val_mean_squared_error: 12.6090 - val_rmse: 3.5509 - val_mean_absolute_error: 2.5274 - lr: 2.5000e-04
Epoch 54/1000
1/1 [==============================] - ETA: 0s - loss: 15.0558 - mean_squared_error: 15.0558 - rmse: 3.8802 - mean_absolute_error: 3.2026
Epoch 00054: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 49ms/step - loss: 15.0558 - mean_squared_error: 15.0558 - rmse: 3.8802 - mean_absolute_error: 3.2026 - val_loss: 12.7095 - val_mean_squared_error: 12.7095 - val_rmse: 3.5650 - val_mean_absolute_error: 2.5348 - lr: 2.5000e-04
Epoch 55/1000
1/1 [==============================] - ETA: 0s - loss: 13.

Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 13.9969 - mean_squared_error: 13.9969 - rmse: 3.7412 - mean_absolute_error: 2.9620
Epoch 00071: val_loss did not improve from 10.04005

Epoch 00071: ReduceLROnPlateau reducing learning rate to 0.0001250000059371814.
1/1 [==============================] - 0s 48ms/step - loss: 13.9969 - mean_squared_error: 13.9969 - rmse: 3.7412 - mean_absolute_error: 2.9620 - val_loss: 14.1879 - val_mean_squared_error: 14.1879 - val_rmse: 3.7667 - val_mean_absolute_error: 2.6499 - lr: 2.5000e-04
Epoch 72/1000
1/1 [==============================] - ETA: 0s - loss: 13.6497 - mean_squared_error: 13.6497 - rmse: 3.6946 - mean_absolute_error: 2.9618
Epoch 00072: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 44ms/step - loss: 13.6497 - mean_squared_error: 13.6497 - rmse: 3.6946 - mean_absolute_error: 2.9618 - val_loss: 14.3804 - val_mean_squared_error: 14.3804 - val_rmse: 3.7922 - val_mean_absolute_error: 2

1/1 [==============================] - ETA: 0s - loss: 14.2321 - mean_squared_error: 14.2321 - rmse: 3.7725 - mean_absolute_error: 2.9915
Epoch 00088: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 41ms/step - loss: 14.2321 - mean_squared_error: 14.2321 - rmse: 3.7725 - mean_absolute_error: 2.9915 - val_loss: 14.9429 - val_mean_squared_error: 14.9429 - val_rmse: 3.8656 - val_mean_absolute_error: 2.7034 - lr: 1.2500e-04
Epoch 89/1000
1/1 [==============================] - ETA: 0s - loss: 14.6707 - mean_squared_error: 14.6707 - rmse: 3.8302 - mean_absolute_error: 3.0763
Epoch 00089: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 47ms/step - loss: 14.6707 - mean_squared_error: 14.6707 - rmse: 3.8302 - mean_absolute_error: 3.0763 - val_loss: 14.9703 - val_mean_squared_error: 14.9703 - val_rmse: 3.8691 - val_mean_absolute_error: 2.7060 - lr: 1.2500e-04
Epoch 90/1000
1/1 [==============================] - ETA: 0s - loss: 16.

1/1 [==============================] - ETA: 0s - loss: 14.8796 - mean_squared_error: 14.8796 - rmse: 3.8574 - mean_absolute_error: 3.0783
Epoch 00105: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 49ms/step - loss: 14.8796 - mean_squared_error: 14.8796 - rmse: 3.8574 - mean_absolute_error: 3.0783 - val_loss: 15.3821 - val_mean_squared_error: 15.3821 - val_rmse: 3.9220 - val_mean_absolute_error: 2.7487 - lr: 6.2500e-05
Epoch 106/1000
1/1 [==============================] - ETA: 0s - loss: 13.1087 - mean_squared_error: 13.1087 - rmse: 3.6206 - mean_absolute_error: 2.8707
Epoch 00106: val_loss did not improve from 10.04005
1/1 [==============================] - 0s 41ms/step - loss: 13.1087 - mean_squared_error: 13.1087 - rmse: 3.6206 - mean_absolute_error: 2.8707 - val_loss: 15.2895 - val_mean_squared_error: 15.2895 - val_rmse: 3.9102 - val_mean_absolute_error: 2.7385 - lr: 6.2500e-05
Epoch 107/1000
1/1 [==============================] - ETA: 0s - loss: 1

In [68]:
df_mlp4_2 = (df_mlp44.merge(df_mlp45, how='outer')).merge(df_mlp46, how='outer')

### cnn_vgg

#### single-cross-site

In [71]:
df_vgg1, history_vgg1 = single_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.m5', 0.001, 0, 3, 4, X, y)
df_vgg2, history_vgg2 = single_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.m5', 0.001, 3, 0, 4, X, y)
df_vgg3, history_vgg3 = single_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.m5', 0.001, 4, 0, 3, X, y)

pooling layers: 4
Model: "model_17"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_18 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 conv1d_44 (Conv1D)          (None, 100, 64)           13888     
                                                                 
 conv1d_45 (Conv1D)          (None, 100, 64)           12352     
                                                                 
 max_pooling1d_44 (MaxPoolin  (None, 50, 64)           0         
 g1D)                                                            
                                                                 
 conv1d_46 (Conv1D)          (None, 50, 128)           24704     
                                                                 
 conv1d_47 (Conv1D)          (None, 50, 128)           49280     
                                        

Epoch 11/1000
4/4 [==============================] - ETA: 0s - loss: 11.9354 - mean_squared_error: 11.9354 - rmse: 3.4548 - mean_absolute_error: 2.8034
Epoch 00011: val_loss did not improve from 7.92551
4/4 [==============================] - 2s 470ms/step - loss: 11.9354 - mean_squared_error: 11.9354 - rmse: 3.4548 - mean_absolute_error: 2.8034 - val_loss: 8.9917 - val_mean_squared_error: 8.9917 - val_rmse: 2.9986 - val_mean_absolute_error: 2.3569 - lr: 0.0010
Epoch 12/1000
4/4 [==============================] - ETA: 0s - loss: 11.5299 - mean_squared_error: 11.5299 - rmse: 3.3956 - mean_absolute_error: 2.6752
Epoch 00012: val_loss did not improve from 7.92551
4/4 [==============================] - 2s 470ms/step - loss: 11.5299 - mean_squared_error: 11.5299 - rmse: 3.3956 - mean_absolute_error: 2.6752 - val_loss: 8.0440 - val_mean_squared_error: 8.0440 - val_rmse: 2.8362 - val_mean_absolute_error: 2.3716 - lr: 0.0010
Epoch 13/1000
4/4 [==============================] - ETA: 0s - loss: 1

4/4 [==============================] - ETA: 0s - loss: 7.1041 - mean_squared_error: 7.1041 - rmse: 2.6654 - mean_absolute_error: 2.1261
Epoch 00028: val_loss did not improve from 5.64359
4/4 [==============================] - 2s 503ms/step - loss: 7.1041 - mean_squared_error: 7.1041 - rmse: 2.6654 - mean_absolute_error: 2.1261 - val_loss: 6.5009 - val_mean_squared_error: 6.5009 - val_rmse: 2.5497 - val_mean_absolute_error: 2.0454 - lr: 0.0010
Epoch 29/1000
4/4 [==============================] - ETA: 0s - loss: 7.3931 - mean_squared_error: 7.3931 - rmse: 2.7190 - mean_absolute_error: 2.1480
Epoch 00029: val_loss did not improve from 5.64359
4/4 [==============================] - 2s 500ms/step - loss: 7.3931 - mean_squared_error: 7.3931 - rmse: 2.7190 - mean_absolute_error: 2.1480 - val_loss: 9.0930 - val_mean_squared_error: 9.0930 - val_rmse: 3.0155 - val_mean_absolute_error: 2.4576 - lr: 0.0010
Epoch 30/1000
4/4 [==============================] - ETA: 0s - loss: 9.2319 - mean_squared_e

Epoch 46/1000
4/4 [==============================] - ETA: 0s - loss: 4.3767 - mean_squared_error: 4.3767 - rmse: 2.0920 - mean_absolute_error: 1.6246
Epoch 00046: val_loss did not improve from 4.74323
4/4 [==============================] - 2s 523ms/step - loss: 4.3767 - mean_squared_error: 4.3767 - rmse: 2.0920 - mean_absolute_error: 1.6246 - val_loss: 6.2752 - val_mean_squared_error: 6.2752 - val_rmse: 2.5050 - val_mean_absolute_error: 1.9982 - lr: 0.0010
Epoch 47/1000
4/4 [==============================] - ETA: 0s - loss: 5.5112 - mean_squared_error: 5.5112 - rmse: 2.3476 - mean_absolute_error: 1.8019
Epoch 00047: val_loss did not improve from 4.74323
4/4 [==============================] - 2s 526ms/step - loss: 5.5112 - mean_squared_error: 5.5112 - rmse: 2.3476 - mean_absolute_error: 1.8019 - val_loss: 5.8711 - val_mean_squared_error: 5.8711 - val_rmse: 2.4230 - val_mean_absolute_error: 1.9327 - lr: 0.0010
Epoch 48/1000
4/4 [==============================] - ETA: 0s - loss: 4.8760 - 

Epoch 64/1000
4/4 [==============================] - ETA: 0s - loss: 2.2626 - mean_squared_error: 2.2626 - rmse: 1.5042 - mean_absolute_error: 1.1503
Epoch 00064: val_loss did not improve from 4.36785
4/4 [==============================] - 2s 508ms/step - loss: 2.2626 - mean_squared_error: 2.2626 - rmse: 1.5042 - mean_absolute_error: 1.1503 - val_loss: 4.5870 - val_mean_squared_error: 4.5870 - val_rmse: 2.1417 - val_mean_absolute_error: 1.6602 - lr: 0.0010
Epoch 65/1000
4/4 [==============================] - ETA: 0s - loss: 1.9987 - mean_squared_error: 1.9987 - rmse: 1.4138 - mean_absolute_error: 1.0834
Epoch 00065: val_loss did not improve from 4.36785
4/4 [==============================] - 2s 489ms/step - loss: 1.9987 - mean_squared_error: 1.9987 - rmse: 1.4138 - mean_absolute_error: 1.0834 - val_loss: 5.1183 - val_mean_squared_error: 5.1183 - val_rmse: 2.2624 - val_mean_absolute_error: 1.7435 - lr: 0.0010
Epoch 66/1000
4/4 [==============================] - ETA: 0s - loss: 2.0846 - 

...

Epoch 159/1000
2/2 [==============================] - ETA: 0s - loss: 1.5856 - mean_squared_error: 1.5856 - rmse: 1.2592 - mean_absolute_error: 0.9652
Epoch 00159: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 263ms/step - loss: 1.5856 - mean_squared_error: 1.5856 - rmse: 1.2592 - mean_absolute_error: 0.9652 - val_loss: 9.2664 - val_mean_squared_error: 9.2664 - val_rmse: 3.0441 - val_mean_absolute_error: 2.5023 - lr: 5.0000e-04
Epoch 160/1000
2/2 [==============================] - ETA: 0s - loss: 1.5232 - mean_squared_error: 1.5232 - rmse: 1.2342 - mean_absolute_error: 0.9776
Epoch 00160: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 271ms/step - loss: 1.5232 - mean_squared_error: 1.5232 - rmse: 1.2342 - mean_absolute_error: 0.9776 - val_loss: 8.2249 - val_mean_squared_error: 8.2249 - val_rmse: 2.8679 - val_mean_absolute_error: 2.4056 - lr: 5.0000e-04
Epoch 161/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 177/1000
2/2 [==============================] - ETA: 0s - loss: 1.1547 - mean_squared_error: 1.1547 - rmse: 1.0746 - mean_absolute_error: 0.8599
Epoch 00177: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 282ms/step - loss: 1.1547 - mean_squared_error: 1.1547 - rmse: 1.0746 - mean_absolute_error: 0.8599 - val_loss: 8.7925 - val_mean_squared_error: 8.7925 - val_rmse: 2.9652 - val_mean_absolute_error: 2.4013 - lr: 5.0000e-04
Epoch 178/1000
2/2 [==============================] - ETA: 0s - loss: 1.2775 - mean_squared_error: 1.2775 - rmse: 1.1303 - mean_absolute_error: 0.8780
Epoch 00178: val_loss did not improve from 7.15999

Epoch 00178: ReduceLROnPlateau reducing learning rate to 0.0002500000118743628.
2/2 [==============================] - 1s 288ms/step - loss: 1.2775 - mean_squared_error: 1.2775 - rmse: 1.1303 - mean_absolute_error: 0.8780 - val_loss: 8.0600 - val_mean_squared_error: 8.0600 - val_rmse: 2.8390 - val_mean_absolute_error: 2.4007 - lr

Epoch 195/1000
2/2 [==============================] - ETA: 0s - loss: 0.8075 - mean_squared_error: 0.8075 - rmse: 0.8986 - mean_absolute_error: 0.7065
Epoch 00195: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 282ms/step - loss: 0.8075 - mean_squared_error: 0.8075 - rmse: 0.8986 - mean_absolute_error: 0.7065 - val_loss: 8.0826 - val_mean_squared_error: 8.0826 - val_rmse: 2.8430 - val_mean_absolute_error: 2.2976 - lr: 2.5000e-04
Epoch 196/1000
2/2 [==============================] - ETA: 0s - loss: 1.0007 - mean_squared_error: 1.0007 - rmse: 1.0004 - mean_absolute_error: 0.7858
Epoch 00196: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 294ms/step - loss: 1.0007 - mean_squared_error: 1.0007 - rmse: 1.0004 - mean_absolute_error: 0.7858 - val_loss: 7.7301 - val_mean_squared_error: 7.7301 - val_rmse: 2.7803 - val_mean_absolute_error: 2.2722 - lr: 2.5000e-04
Epoch 197/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 213/1000
2/2 [==============================] - ETA: 0s - loss: 0.7824 - mean_squared_error: 0.7824 - rmse: 0.8845 - mean_absolute_error: 0.6914
Epoch 00213: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 297ms/step - loss: 0.7824 - mean_squared_error: 0.7824 - rmse: 0.8845 - mean_absolute_error: 0.6914 - val_loss: 7.1783 - val_mean_squared_error: 7.1783 - val_rmse: 2.6792 - val_mean_absolute_error: 2.2603 - lr: 1.2500e-04
Epoch 214/1000
2/2 [==============================] - ETA: 0s - loss: 0.8456 - mean_squared_error: 0.8456 - rmse: 0.9196 - mean_absolute_error: 0.7307
Epoch 00214: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 301ms/step - loss: 0.8456 - mean_squared_error: 0.8456 - rmse: 0.9196 - mean_absolute_error: 0.7307 - val_loss: 7.1726 - val_mean_squared_error: 7.1726 - val_rmse: 2.6782 - val_mean_absolute_error: 2.2588 - lr: 1.2500e-04
Epoch 215/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 231/1000
2/2 [==============================] - ETA: 0s - loss: 0.7486 - mean_squared_error: 0.7486 - rmse: 0.8652 - mean_absolute_error: 0.6888
Epoch 00231: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 290ms/step - loss: 0.7486 - mean_squared_error: 0.7486 - rmse: 0.8652 - mean_absolute_error: 0.6888 - val_loss: 7.5889 - val_mean_squared_error: 7.5889 - val_rmse: 2.7548 - val_mean_absolute_error: 2.2879 - lr: 6.2500e-05
Epoch 232/1000
2/2 [==============================] - ETA: 0s - loss: 0.8133 - mean_squared_error: 0.8133 - rmse: 0.9018 - mean_absolute_error: 0.6837
Epoch 00232: val_loss did not improve from 7.15999
2/2 [==============================] - 1s 287ms/step - loss: 0.8133 - mean_squared_error: 0.8133 - rmse: 0.9018 - mean_absolute_error: 0.6837 - val_loss: 7.5926 - val_mean_squared_error: 7.5926 - val_rmse: 2.7555 - val_mean_absolute_error: 2.2878 - lr: 6.2500e-05
Epoch 233/1000
2/2 [==============================] - ETA: 0s - loss

In [73]:
df_vgg_1 = (df_vgg1.merge(df_vgg2, how='outer')).merge(df_vgg3, how='outer')

#### double-cross-site

In [76]:
df_vgg4, hisory_vgg4 = double_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.h5', 0.001, 0, 3, 4, X, y)
df_vgg5, hisory_vgg5 = double_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.h5', 0.001, 0, 4, 3, X, y)
df_vgg6, hisory_vgg6 = double_cross_site(cnn_vgg, 'cnn_vgg', '/tmp/vgg.h5', 0.001, 3, 4, 0, X, y)

pooling layers: 4
Model: "model_20"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_21 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 conv1d_74 (Conv1D)          (None, 100, 64)           13888     
                                                                 
 conv1d_75 (Conv1D)          (None, 100, 64)           12352     
                                                                 
 max_pooling1d_56 (MaxPoolin  (None, 50, 64)           0         
 g1D)                                                            
                                                                 
 conv1d_76 (Conv1D)          (None, 50, 128)           24704     
                                                                 
 conv1d_77 (Conv1D)          (None, 50, 128)           49280     
                                        

Epoch 11/1000
1/1 [==============================] - ETA: 0s - loss: 13.4484 - mean_squared_error: 13.4484 - rmse: 3.6672 - mean_absolute_error: 2.8061
Epoch 00011: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 299ms/step - loss: 13.4484 - mean_squared_error: 13.4484 - rmse: 3.6672 - mean_absolute_error: 2.8061 - val_loss: 48.4502 - val_mean_squared_error: 48.4502 - val_rmse: 6.9606 - val_mean_absolute_error: 5.8413 - lr: 0.0010
Epoch 12/1000
1/1 [==============================] - ETA: 0s - loss: 33.0493 - mean_squared_error: 33.0493 - rmse: 5.7488 - mean_absolute_error: 4.8934
Epoch 00012: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 285ms/step - loss: 33.0493 - mean_squared_error: 33.0493 - rmse: 5.7488 - mean_absolute_error: 4.8934 - val_loss: 47.9808 - val_mean_squared_error: 47.9808 - val_rmse: 6.9268 - val_mean_absolute_error: 5.7970 - lr: 0.0010
Epoch 13/1000
1/1 [==============================] - ETA: 0s - l

Epoch 29/1000
1/1 [==============================] - ETA: 0s - loss: 8.9037 - mean_squared_error: 8.9037 - rmse: 2.9839 - mean_absolute_error: 2.3776
Epoch 00029: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 288ms/step - loss: 8.9037 - mean_squared_error: 8.9037 - rmse: 2.9839 - mean_absolute_error: 2.3776 - val_loss: 15.9296 - val_mean_squared_error: 15.9296 - val_rmse: 3.9912 - val_mean_absolute_error: 3.3681 - lr: 5.0000e-04
Epoch 30/1000
1/1 [==============================] - ETA: 0s - loss: 9.1757 - mean_squared_error: 9.1757 - rmse: 3.0291 - mean_absolute_error: 2.3681
Epoch 00030: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 279ms/step - loss: 9.1757 - mean_squared_error: 9.1757 - rmse: 3.0291 - mean_absolute_error: 2.3681 - val_loss: 17.1021 - val_mean_squared_error: 17.1021 - val_rmse: 4.1355 - val_mean_absolute_error: 3.4487 - lr: 5.0000e-04
Epoch 31/1000
1/1 [==============================] - ETA: 0s - l

Epoch 47/1000
1/1 [==============================] - ETA: 0s - loss: 8.7573 - mean_squared_error: 8.7573 - rmse: 2.9593 - mean_absolute_error: 2.3501
Epoch 00047: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 267ms/step - loss: 8.7573 - mean_squared_error: 8.7573 - rmse: 2.9593 - mean_absolute_error: 2.3501 - val_loss: 15.8516 - val_mean_squared_error: 15.8516 - val_rmse: 3.9814 - val_mean_absolute_error: 3.3210 - lr: 2.5000e-04
Epoch 48/1000
1/1 [==============================] - ETA: 0s - loss: 8.4394 - mean_squared_error: 8.4394 - rmse: 2.9051 - mean_absolute_error: 2.2924
Epoch 00048: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 263ms/step - loss: 8.4394 - mean_squared_error: 8.4394 - rmse: 2.9051 - mean_absolute_error: 2.2924 - val_loss: 15.8469 - val_mean_squared_error: 15.8469 - val_rmse: 3.9808 - val_mean_absolute_error: 3.3168 - lr: 2.5000e-04
Epoch 49/1000
1/1 [==============================] - ETA: 0s - l

Epoch 65/1000
1/1 [==============================] - ETA: 0s - loss: 8.3318 - mean_squared_error: 8.3318 - rmse: 2.8865 - mean_absolute_error: 2.3342
Epoch 00065: val_loss did not improve from 15.37174

Epoch 00065: ReduceLROnPlateau reducing learning rate to 0.0001250000059371814.
1/1 [==============================] - 0s 265ms/step - loss: 8.3318 - mean_squared_error: 8.3318 - rmse: 2.8865 - mean_absolute_error: 2.3342 - val_loss: 15.8078 - val_mean_squared_error: 15.8078 - val_rmse: 3.9759 - val_mean_absolute_error: 3.3193 - lr: 2.5000e-04
Epoch 66/1000
1/1 [==============================] - ETA: 0s - loss: 7.1796 - mean_squared_error: 7.1796 - rmse: 2.6795 - mean_absolute_error: 2.0932
Epoch 00066: val_loss did not improve from 15.37174
1/1 [==============================] - 0s 265ms/step - loss: 7.1796 - mean_squared_error: 7.1796 - rmse: 2.6795 - mean_absolute_error: 2.0932 - val_loss: 15.8939 - val_mean_squared_error: 15.8939 - val_rmse: 3.9867 - val_mean_absolute_error: 3.3294 

...

Epoch 61/1000
1/1 [==============================] - ETA: 0s - loss: 9.5267 - mean_squared_error: 9.5267 - rmse: 3.0865 - mean_absolute_error: 2.2931
Epoch 00061: val_loss did not improve from 5.81093
1/1 [==============================] - 1s 511ms/step - loss: 9.5267 - mean_squared_error: 9.5267 - rmse: 3.0865 - mean_absolute_error: 2.2931 - val_loss: 6.1154 - val_mean_squared_error: 6.1154 - val_rmse: 2.4729 - val_mean_absolute_error: 1.9569 - lr: 5.0000e-04
Epoch 62/1000
1/1 [==============================] - ETA: 0s - loss: 9.6737 - mean_squared_error: 9.6737 - rmse: 3.1103 - mean_absolute_error: 2.4011
Epoch 00062: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 499ms/step - loss: 9.6737 - mean_squared_error: 9.6737 - rmse: 3.1103 - mean_absolute_error: 2.4011 - val_loss: 6.5246 - val_mean_squared_error: 6.5246 - val_rmse: 2.5543 - val_mean_absolute_error: 1.9996 - lr: 5.0000e-04
Epoch 63/1000
1/1 [==============================] - ETA: 0s - loss: 9

Epoch 79/1000
1/1 [==============================] - ETA: 0s - loss: 8.1774 - mean_squared_error: 8.1774 - rmse: 2.8596 - mean_absolute_error: 2.3028
Epoch 00079: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 499ms/step - loss: 8.1774 - mean_squared_error: 8.1774 - rmse: 2.8596 - mean_absolute_error: 2.3028 - val_loss: 6.8697 - val_mean_squared_error: 6.8697 - val_rmse: 2.6210 - val_mean_absolute_error: 2.0963 - lr: 5.0000e-04
Epoch 80/1000
1/1 [==============================] - ETA: 0s - loss: 7.4412 - mean_squared_error: 7.4412 - rmse: 2.7278 - mean_absolute_error: 2.0731
Epoch 00080: val_loss did not improve from 5.81093

Epoch 00080: ReduceLROnPlateau reducing learning rate to 0.0002500000118743628.
1/1 [==============================] - 0s 482ms/step - loss: 7.4412 - mean_squared_error: 7.4412 - rmse: 2.7278 - mean_absolute_error: 2.0731 - val_loss: 6.9594 - val_mean_squared_error: 6.9594 - val_rmse: 2.6381 - val_mean_absolute_error: 2.0994 - lr: 

Epoch 97/1000
1/1 [==============================] - ETA: 0s - loss: 7.3405 - mean_squared_error: 7.3405 - rmse: 2.7093 - mean_absolute_error: 2.0778
Epoch 00097: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 492ms/step - loss: 7.3405 - mean_squared_error: 7.3405 - rmse: 2.7093 - mean_absolute_error: 2.0778 - val_loss: 7.6267 - val_mean_squared_error: 7.6267 - val_rmse: 2.7616 - val_mean_absolute_error: 2.1884 - lr: 2.5000e-04
Epoch 98/1000
1/1 [==============================] - ETA: 0s - loss: 7.5265 - mean_squared_error: 7.5265 - rmse: 2.7435 - mean_absolute_error: 2.1504
Epoch 00098: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 488ms/step - loss: 7.5265 - mean_squared_error: 7.5265 - rmse: 2.7435 - mean_absolute_error: 2.1504 - val_loss: 7.4976 - val_mean_squared_error: 7.4976 - val_rmse: 2.7382 - val_mean_absolute_error: 2.1720 - lr: 2.5000e-04
Epoch 99/1000
1/1 [==============================] - ETA: 0s - loss: 7

Epoch 115/1000
1/1 [==============================] - ETA: 0s - loss: 6.5809 - mean_squared_error: 6.5809 - rmse: 2.5653 - mean_absolute_error: 1.9442
Epoch 00115: val_loss did not improve from 5.81093
1/1 [==============================] - 1s 514ms/step - loss: 6.5809 - mean_squared_error: 6.5809 - rmse: 2.5653 - mean_absolute_error: 1.9442 - val_loss: 7.8428 - val_mean_squared_error: 7.8428 - val_rmse: 2.8005 - val_mean_absolute_error: 2.2130 - lr: 1.2500e-04
Epoch 116/1000
1/1 [==============================] - ETA: 0s - loss: 6.9161 - mean_squared_error: 6.9161 - rmse: 2.6299 - mean_absolute_error: 2.0420
Epoch 00116: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 463ms/step - loss: 6.9161 - mean_squared_error: 6.9161 - rmse: 2.6299 - mean_absolute_error: 2.0420 - val_loss: 7.8839 - val_mean_squared_error: 7.8839 - val_rmse: 2.8078 - val_mean_absolute_error: 2.2182 - lr: 1.2500e-04
Epoch 117/1000
1/1 [==============================] - ETA: 0s - loss

Epoch 133/1000
1/1 [==============================] - ETA: 0s - loss: 6.0809 - mean_squared_error: 6.0809 - rmse: 2.4659 - mean_absolute_error: 1.9276
Epoch 00133: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 482ms/step - loss: 6.0809 - mean_squared_error: 6.0809 - rmse: 2.4659 - mean_absolute_error: 1.9276 - val_loss: 7.8249 - val_mean_squared_error: 7.8249 - val_rmse: 2.7973 - val_mean_absolute_error: 2.2047 - lr: 6.2500e-05
Epoch 134/1000
1/1 [==============================] - ETA: 0s - loss: 6.7198 - mean_squared_error: 6.7198 - rmse: 2.5923 - mean_absolute_error: 1.9724
Epoch 00134: val_loss did not improve from 5.81093
1/1 [==============================] - 0s 483ms/step - loss: 6.7198 - mean_squared_error: 6.7198 - rmse: 2.5923 - mean_absolute_error: 1.9724 - val_loss: 7.7625 - val_mean_squared_error: 7.7625 - val_rmse: 2.7861 - val_mean_absolute_error: 2.1902 - lr: 6.2500e-05
Epoch 135/1000
1/1 [==============================] - ETA: 0s - loss

In [77]:
df_vgg_2 = (df_vgg4.merge(df_vgg5, how='outer')).merge(df_vgg6, how='outer')

### cnn_resnet

#### single-cross-site

In [78]:
df_resnet1, history_resnet1 = single_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.m5', 0.01, 0, 3, 4, X, y)
df_resnet2, history_resnet2 = single_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.m5', 0.01, 3, 0, 4, X, y)
df_resnet3, history_resnet3 = single_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.m5', 0.01, 4, 0, 3, X, y)

Model: "model_23"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_24 (InputLayer)          [(None, 100, 72)]    0           []                               
                                                                                                  
 conv1d_104 (Conv1D)            (None, 100, 64)      36928       ['input_24[0][0]']               
                                                                                                  
 batch_normalization (BatchNorm  (None, 100, 64)     256         ['conv1d_104[0][0]']             
 alization)                                                                                       
                                                                                                  
 activation (Activation)        (None, 100, 64)      0           ['batch_normalization[0][0

4/4 [==============================] - ETA: 0s - loss: 66.7085 - mean_squared_error: 66.7085 - rmse: 8.1675 - mean_absolute_error: 7.3260  
Epoch 00001: val_loss improved from inf to 54636304.00000, saving model to /tmp/resnet.m5
4/4 [==============================] - 4s 479ms/step - loss: 66.7085 - mean_squared_error: 66.7085 - rmse: 8.1675 - mean_absolute_error: 7.3260 - val_loss: 54636304.0000 - val_mean_squared_error: 54636304.0000 - val_rmse: 7391.6372 - val_mean_absolute_error: 7375.8066 - lr: 0.0100
Epoch 2/1000
4/4 [==============================] - ETA: 0s - loss: 12.4071 - mean_squared_error: 12.4071 - rmse: 3.5224 - mean_absolute_error: 2.6843
Epoch 00002: val_loss did not improve from 54636304.00000
4/4 [==============================] - 1s 338ms/step - loss: 12.4071 - mean_squared_error: 12.4071 - rmse: 3.5224 - mean_absolute_error: 2.6843 - val_loss: 4587397632.0000 - val_mean_squared_error: 4587397632.0000 - val_rmse: 67730.3281 - val_mean_absolute_error: 67591.3750 - lr

4/4 [==============================] - ETA: 0s - loss: 1.5670 - mean_squared_error: 1.5670 - rmse: 1.2518 - mean_absolute_error: 0.9827
Epoch 00017: val_loss improved from 9989.11914 to 6471.95850, saving model to /tmp/resnet.m5
4/4 [==============================] - 1s 365ms/step - loss: 1.5670 - mean_squared_error: 1.5670 - rmse: 1.2518 - mean_absolute_error: 0.9827 - val_loss: 6471.9585 - val_mean_squared_error: 6471.9585 - val_rmse: 80.4485 - val_mean_absolute_error: 79.6361 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 1.8141 - mean_squared_error: 1.8141 - rmse: 1.3469 - mean_absolute_error: 1.0451
Epoch 00018: val_loss improved from 6471.95850 to 3163.48975, saving model to /tmp/resnet.m5
4/4 [==============================] - 1s 365ms/step - loss: 1.8141 - mean_squared_error: 1.8141 - rmse: 1.3469 - mean_absolute_error: 1.0451 - val_loss: 3163.4897 - val_mean_squared_error: 3163.4897 - val_rmse: 56.2449 - val_mean_absolute_error: 55.5537 - lr:

4/4 [==============================] - ETA: 0s - loss: 0.6996 - mean_squared_error: 0.6996 - rmse: 0.8364 - mean_absolute_error: 0.6554
Epoch 00034: val_loss did not improve from 7.59214
4/4 [==============================] - 1s 363ms/step - loss: 0.6996 - mean_squared_error: 0.6996 - rmse: 0.8364 - mean_absolute_error: 0.6554 - val_loss: 48.8095 - val_mean_squared_error: 48.8095 - val_rmse: 6.9864 - val_mean_absolute_error: 5.9399 - lr: 0.0100
Epoch 35/1000
4/4 [==============================] - ETA: 0s - loss: 0.7984 - mean_squared_error: 0.7984 - rmse: 0.8935 - mean_absolute_error: 0.6497
Epoch 00035: val_loss did not improve from 7.59214
4/4 [==============================] - 1s 337ms/step - loss: 0.7984 - mean_squared_error: 0.7984 - rmse: 0.8935 - mean_absolute_error: 0.6497 - val_loss: 49.1277 - val_mean_squared_error: 49.1277 - val_rmse: 7.0091 - val_mean_absolute_error: 5.8362 - lr: 0.0100
Epoch 36/1000
4/4 [==============================] - ETA: 0s - loss: 0.5605 - mean_squar

Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 0.1631 - mean_squared_error: 0.1631 - rmse: 0.4038 - mean_absolute_error: 0.3083
Epoch 00052: val_loss did not improve from 7.59214
4/4 [==============================] - 1s 360ms/step - loss: 0.1631 - mean_squared_error: 0.1631 - rmse: 0.4038 - mean_absolute_error: 0.3083 - val_loss: 10.6275 - val_mean_squared_error: 10.6275 - val_rmse: 3.2600 - val_mean_absolute_error: 2.6578 - lr: 0.0050
Epoch 53/1000
4/4 [==============================] - ETA: 0s - loss: 0.1547 - mean_squared_error: 0.1547 - rmse: 0.3933 - mean_absolute_error: 0.3012
Epoch 00053: val_loss did not improve from 7.59214
4/4 [==============================] - 1s 352ms/step - loss: 0.1547 - mean_squared_error: 0.1547 - rmse: 0.3933 - mean_absolute_error: 0.3012 - val_loss: 11.8951 - val_mean_squared_error: 11.8951 - val_rmse: 3.4489 - val_mean_absolute_error: 2.8493 - lr: 0.0050
Epoch 54/1000
4/4 [==============================] - ETA: 0s - loss: 0.138

...

Epoch 318/1000
2/2 [==============================] - ETA: 0s - loss: 0.0405 - mean_squared_error: 0.0405 - rmse: 0.2013 - mean_absolute_error: 0.1262
Epoch 00318: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 146ms/step - loss: 0.0405 - mean_squared_error: 0.0405 - rmse: 0.2013 - mean_absolute_error: 0.1262 - val_loss: 6.2126 - val_mean_squared_error: 6.2126 - val_rmse: 2.4925 - val_mean_absolute_error: 1.8578 - lr: 7.8125e-05
Epoch 319/1000
2/2 [==============================] - ETA: 0s - loss: 0.0662 - mean_squared_error: 0.0662 - rmse: 0.2573 - mean_absolute_error: 0.1830
Epoch 00319: val_loss did not improve from 6.02912

Epoch 00319: ReduceLROnPlateau reducing learning rate to 3.9062499126885086e-05.
2/2 [==============================] - 0s 168ms/step - loss: 0.0662 - mean_squared_error: 0.0662 - rmse: 0.2573 - mean_absolute_error: 0.1830 - val_loss: 6.2986 - val_mean_squared_error: 6.2986 - val_rmse: 2.5097 - val_mean_absolute_error: 1.8463 - l

Epoch 336/1000
2/2 [==============================] - ETA: 0s - loss: 0.3434 - mean_squared_error: 0.3434 - rmse: 0.5860 - mean_absolute_error: 0.4183
Epoch 00336: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 157ms/step - loss: 0.3434 - mean_squared_error: 0.3434 - rmse: 0.5860 - mean_absolute_error: 0.4183 - val_loss: 6.1650 - val_mean_squared_error: 6.1650 - val_rmse: 2.4829 - val_mean_absolute_error: 1.8981 - lr: 3.9062e-05
Epoch 337/1000
2/2 [==============================] - ETA: 0s - loss: 0.1019 - mean_squared_error: 0.1019 - rmse: 0.3193 - mean_absolute_error: 0.2317
Epoch 00337: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 161ms/step - loss: 0.1019 - mean_squared_error: 0.1019 - rmse: 0.3193 - mean_absolute_error: 0.2317 - val_loss: 6.1473 - val_mean_squared_error: 6.1473 - val_rmse: 2.4794 - val_mean_absolute_error: 1.8978 - lr: 3.9062e-05
Epoch 338/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 354/1000
2/2 [==============================] - ETA: 0s - loss: 0.2762 - mean_squared_error: 0.2762 - rmse: 0.5255 - mean_absolute_error: 0.3957
Epoch 00354: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 160ms/step - loss: 0.2762 - mean_squared_error: 0.2762 - rmse: 0.5255 - mean_absolute_error: 0.3957 - val_loss: 6.1273 - val_mean_squared_error: 6.1273 - val_rmse: 2.4753 - val_mean_absolute_error: 1.8728 - lr: 1.9531e-05
Epoch 355/1000
2/2 [==============================] - ETA: 0s - loss: 0.1523 - mean_squared_error: 0.1523 - rmse: 0.3902 - mean_absolute_error: 0.2787
Epoch 00355: val_loss did not improve from 6.02912
2/2 [==============================] - 1s 202ms/step - loss: 0.1523 - mean_squared_error: 0.1523 - rmse: 0.3902 - mean_absolute_error: 0.2787 - val_loss: 6.1310 - val_mean_squared_error: 6.1310 - val_rmse: 2.4761 - val_mean_absolute_error: 1.8755 - lr: 1.9531e-05
Epoch 356/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 372/1000
2/2 [==============================] - ETA: 0s - loss: 0.0157 - mean_squared_error: 0.0157 - rmse: 0.1255 - mean_absolute_error: 0.0815
Epoch 00372: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 153ms/step - loss: 0.0157 - mean_squared_error: 0.0157 - rmse: 0.1255 - mean_absolute_error: 0.0815 - val_loss: 6.1677 - val_mean_squared_error: 6.1677 - val_rmse: 2.4835 - val_mean_absolute_error: 1.9079 - lr: 9.7656e-06
Epoch 373/1000
2/2 [==============================] - ETA: 0s - loss: 0.0277 - mean_squared_error: 0.0277 - rmse: 0.1664 - mean_absolute_error: 0.1183
Epoch 00373: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 153ms/step - loss: 0.0277 - mean_squared_error: 0.0277 - rmse: 0.1664 - mean_absolute_error: 0.1183 - val_loss: 6.1697 - val_mean_squared_error: 6.1697 - val_rmse: 2.4839 - val_mean_absolute_error: 1.9099 - lr: 9.7656e-06
Epoch 374/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 390/1000
2/2 [==============================] - ETA: 0s - loss: 0.0524 - mean_squared_error: 0.0524 - rmse: 0.2288 - mean_absolute_error: 0.1316
Epoch 00390: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 154ms/step - loss: 0.0524 - mean_squared_error: 0.0524 - rmse: 0.2288 - mean_absolute_error: 0.1316 - val_loss: 6.1326 - val_mean_squared_error: 6.1326 - val_rmse: 2.4764 - val_mean_absolute_error: 1.9297 - lr: 4.8828e-06
Epoch 391/1000
2/2 [==============================] - ETA: 0s - loss: 0.0406 - mean_squared_error: 0.0406 - rmse: 0.2016 - mean_absolute_error: 0.1208
Epoch 00391: val_loss did not improve from 6.02912
2/2 [==============================] - 0s 156ms/step - loss: 0.0406 - mean_squared_error: 0.0406 - rmse: 0.2016 - mean_absolute_error: 0.1208 - val_loss: 6.1352 - val_mean_squared_error: 6.1352 - val_rmse: 2.4769 - val_mean_absolute_error: 1.9311 - lr: 4.8828e-06
Epoch 392/1000
2/2 [==============================] - ETA: 0s - loss

In [79]:
df_resnet_1 = (df_resnet1.merge(df_resnet2, how='outer')).merge(df_resnet3, how='outer')

#### double-cross-site

In [81]:
df_resnet4, hisory_resnet4 = double_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.h5', 0.01, 0, 3, 4, X, y)
df_resnet5, hisory_resnet5 = double_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.h5', 0.01, 0, 4, 3, X, y)
df_resnet6, hisory_resnet6 = double_cross_site(cnn_resnet, 'cnn_resnet', '/tmp/resnet.h5', 0.01, 3, 4, 0, X, y)

Model: "model_28"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_29 (InputLayer)          [(None, 100, 72)]    0           []                               
                                                                                                  
 conv1d_159 (Conv1D)            (None, 100, 64)      36928       ['input_29[0][0]']               
                                                                                                  
 batch_normalization_60 (BatchN  (None, 100, 64)     256         ['conv1d_159[0][0]']             
 ormalization)                                                                                    
                                                                                                  
 activation_60 (Activation)     (None, 100, 64)      0           ['batch_normalization_60[0

1/1 [==============================] - ETA: 0s - loss: 106.8213 - mean_squared_error: 106.8213 - rmse: 10.3354 - mean_absolute_error: 9.6814
Epoch 00001: val_loss improved from inf to 1273.64111, saving model to /tmp/resnet.h5
1/1 [==============================] - 3s 3s/step - loss: 106.8213 - mean_squared_error: 106.8213 - rmse: 10.3354 - mean_absolute_error: 9.6814 - val_loss: 1273.6411 - val_mean_squared_error: 1273.6411 - val_rmse: 35.6881 - val_mean_absolute_error: 35.2566 - lr: 0.0100
Epoch 2/1000
1/1 [==============================] - ETA: 0s - loss: 79.3188 - mean_squared_error: 79.3188 - rmse: 8.9061 - mean_absolute_error: 7.8969
Epoch 00002: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 152ms/step - loss: 79.3188 - mean_squared_error: 79.3188 - rmse: 8.9061 - mean_absolute_error: 7.8969 - val_loss: 729182.5625 - val_mean_squared_error: 729182.5625 - val_rmse: 853.9219 - val_mean_absolute_error: 840.1892 - lr: 0.0100
Epoch 3/1000
1/1 [====

Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 0.9363 - mean_squared_error: 0.9363 - rmse: 0.9676 - mean_absolute_error: 0.7038
Epoch 00018: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 155ms/step - loss: 0.9363 - mean_squared_error: 0.9363 - rmse: 0.9676 - mean_absolute_error: 0.7038 - val_loss: 10113495040.0000 - val_mean_squared_error: 10113495040.0000 - val_rmse: 100565.8750 - val_mean_absolute_error: 98385.7500 - lr: 0.0100
Epoch 19/1000
1/1 [==============================] - ETA: 0s - loss: 0.7473 - mean_squared_error: 0.7473 - rmse: 0.8645 - mean_absolute_error: 0.6807
Epoch 00019: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 148ms/step - loss: 0.7473 - mean_squared_error: 0.7473 - rmse: 0.8645 - mean_absolute_error: 0.6807 - val_loss: 8031344640.0000 - val_mean_squared_error: 8031344640.0000 - val_rmse: 89617.7734 - val_mean_absolute_error: 87656.8828 - lr: 0.0100
Epoch 20/1000
1/1

Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 0.1584 - mean_squared_error: 0.1584 - rmse: 0.3980 - mean_absolute_error: 0.3085
Epoch 00035: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 157ms/step - loss: 0.1584 - mean_squared_error: 0.1584 - rmse: 0.3980 - mean_absolute_error: 0.3085 - val_loss: 45480856.0000 - val_mean_squared_error: 45480856.0000 - val_rmse: 6743.9497 - val_mean_absolute_error: 6561.9956 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 0.1437 - mean_squared_error: 0.1437 - rmse: 0.3791 - mean_absolute_error: 0.2933
Epoch 00036: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 151ms/step - loss: 0.1437 - mean_squared_error: 0.1437 - rmse: 0.3791 - mean_absolute_error: 0.2933 - val_loss: 36210744.0000 - val_mean_squared_error: 36210744.0000 - val_rmse: 6017.5361 - val_mean_absolute_error: 5852.9614 - lr: 0.0050
Epoch 37/1000
1/1 [=============

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 0.0301 - mean_squared_error: 0.0301 - rmse: 0.1736 - mean_absolute_error: 0.1341
Epoch 00052: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 157ms/step - loss: 0.0301 - mean_squared_error: 0.0301 - rmse: 0.1736 - mean_absolute_error: 0.1341 - val_loss: 1702554.3750 - val_mean_squared_error: 1702554.3750 - val_rmse: 1304.8197 - val_mean_absolute_error: 1255.1909 - lr: 0.0025
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 0.0283 - mean_squared_error: 0.0283 - rmse: 0.1683 - mean_absolute_error: 0.1305
Epoch 00053: val_loss did not improve from 1273.64111
1/1 [==============================] - 0s 153ms/step - loss: 0.0283 - mean_squared_error: 0.0283 - rmse: 0.1683 - mean_absolute_error: 0.1305 - val_loss: 1449872.8750 - val_mean_squared_error: 1449872.8750 - val_rmse: 1204.1067 - val_mean_absolute_error: 1157.2218 - lr: 0.0025
Epoch 54/1000
1/1 [=================

...

Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 3.8654 - mean_squared_error: 3.8654 - rmse: 1.9661 - mean_absolute_error: 1.5701
Epoch 00018: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 347ms/step - loss: 3.8654 - mean_squared_error: 3.8654 - rmse: 1.9661 - mean_absolute_error: 1.5701 - val_loss: 348441760.0000 - val_mean_squared_error: 348441760.0000 - val_rmse: 18666.5957 - val_mean_absolute_error: 18463.6309 - lr: 0.0100
Epoch 19/1000
1/1 [==============================] - ETA: 0s - loss: 2.9872 - mean_squared_error: 2.9872 - rmse: 1.7284 - mean_absolute_error: 1.3630
Epoch 00019: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 359ms/step - loss: 2.9872 - mean_squared_error: 2.9872 - rmse: 1.7284 - mean_absolute_error: 1.3630 - val_loss: 296904640.0000 - val_mean_squared_error: 296904640.0000 - val_rmse: 17230.9219 - val_mean_absolute_error: 17039.8750 - lr: 0.0100
Epoch 20/1000
1/1 [=========

Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 0.6107 - mean_squared_error: 0.6107 - rmse: 0.7815 - mean_absolute_error: 0.6150
Epoch 00035: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 352ms/step - loss: 0.6107 - mean_squared_error: 0.6107 - rmse: 0.7815 - mean_absolute_error: 0.6150 - val_loss: 1255863.2500 - val_mean_squared_error: 1255863.2500 - val_rmse: 1120.6531 - val_mean_absolute_error: 1110.1332 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 0.5496 - mean_squared_error: 0.5496 - rmse: 0.7413 - mean_absolute_error: 0.5803
Epoch 00036: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 350ms/step - loss: 0.5496 - mean_squared_error: 0.5496 - rmse: 0.7413 - mean_absolute_error: 0.5803 - val_loss: 954669.4375 - val_mean_squared_error: 954669.4375 - val_rmse: 977.0719 - val_mean_absolute_error: 967.7816 - lr: 0.0050
Epoch 37/1000
1/1 [=========================

1/1 [==============================] - ETA: 0s - loss: 0.1805 - mean_squared_error: 0.1805 - rmse: 0.4249 - mean_absolute_error: 0.3084
Epoch 00052: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 346ms/step - loss: 0.1805 - mean_squared_error: 0.1805 - rmse: 0.4249 - mean_absolute_error: 0.3084 - val_loss: 38151.5742 - val_mean_squared_error: 38151.5742 - val_rmse: 195.3243 - val_mean_absolute_error: 193.1421 - lr: 0.0025
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 0.1711 - mean_squared_error: 0.1711 - rmse: 0.4136 - mean_absolute_error: 0.3003
Epoch 00053: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 352ms/step - loss: 0.1711 - mean_squared_error: 0.1711 - rmse: 0.4136 - mean_absolute_error: 0.3003 - val_loss: 32950.5781 - val_mean_squared_error: 32950.5781 - val_rmse: 181.5229 - val_mean_absolute_error: 179.4572 - lr: 0.0025
Epoch 54/1000
1/1 [==============================] - ETA: 0s - los

1/1 [==============================] - ETA: 0s - loss: 0.0843 - mean_squared_error: 0.0843 - rmse: 0.2904 - mean_absolute_error: 0.1916
Epoch 00069: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 354ms/step - loss: 0.0843 - mean_squared_error: 0.0843 - rmse: 0.2904 - mean_absolute_error: 0.1916 - val_loss: 3756.3926 - val_mean_squared_error: 3756.3926 - val_rmse: 61.2894 - val_mean_absolute_error: 60.1889 - lr: 0.0012
Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 0.0815 - mean_squared_error: 0.0815 - rmse: 0.2855 - mean_absolute_error: 0.1868
Epoch 00070: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 339ms/step - loss: 0.0815 - mean_squared_error: 0.0815 - rmse: 0.2855 - mean_absolute_error: 0.1868 - val_loss: 3299.7363 - val_mean_squared_error: 3299.7363 - val_rmse: 57.4433 - val_mean_absolute_error: 56.3761 - lr: 0.0012
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 0.078

1/1 [==============================] - ETA: 0s - loss: 0.0539 - mean_squared_error: 0.0539 - rmse: 0.2321 - mean_absolute_error: 0.1384
Epoch 00086: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 362ms/step - loss: 0.0539 - mean_squared_error: 0.0539 - rmse: 0.2321 - mean_absolute_error: 0.1384 - val_loss: 676.2050 - val_mean_squared_error: 676.2050 - val_rmse: 26.0039 - val_mean_absolute_error: 25.1241 - lr: 6.2500e-04
Epoch 87/1000
1/1 [==============================] - ETA: 0s - loss: 0.0531 - mean_squared_error: 0.0531 - rmse: 0.2304 - mean_absolute_error: 0.1375
Epoch 00087: val_loss did not improve from 64.22162
1/1 [==============================] - 0s 354ms/step - loss: 0.0531 - mean_squared_error: 0.0531 - rmse: 0.2304 - mean_absolute_error: 0.1375 - val_loss: 628.8538 - val_mean_squared_error: 628.8538 - val_rmse: 25.0770 - val_mean_absolute_error: 24.1956 - lr: 6.2500e-04
Epoch 88/1000
1/1 [==============================] - ETA: 0s - loss: 0

In [82]:
df_resnet_2 = (df_resnet4.merge(df_resnet5, how='outer')).merge(df_resnet6, how='outer')

### lstm1v0

#### single-cross-site

In [83]:
df_lstm1v01, history_lstm1v01 = single_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 0, 3, 4, X, y)
df_lstm1v02, history_lstm1v02 = single_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 3, 0, 4, X, y)
df_lstm1v03, history_lstm1v03 = single_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 4, 0, 3, X, y)

Model: "model_31"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_32 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm (LSTM)                 (None, 100)               69200     
                                                                 
 dense_83 (Dense)            (None, 1)                 101       
                                                                 
Total params: 69,301
Trainable params: 69,301
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
4/4 [==============================] - ETA: 0s - loss: 60.7524 - mean_squared_error: 60.7524 - rmse: 7.7944 - mean_absolute_error: 6.4211  
Epoch 00001: val_loss improved from inf to 11.55742, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 2s 250ms/step - loss: 60.7524 - mean_squa

4/4 [==============================] - ETA: 0s - loss: 12.2475 - mean_squared_error: 12.2475 - rmse: 3.4996 - mean_absolute_error: 2.8355
Epoch 00016: val_loss did not improve from 11.00079
4/4 [==============================] - 0s 119ms/step - loss: 12.2475 - mean_squared_error: 12.2475 - rmse: 3.4996 - mean_absolute_error: 2.8355 - val_loss: 11.0072 - val_mean_squared_error: 11.0072 - val_rmse: 3.3177 - val_mean_absolute_error: 2.7916 - lr: 0.0100
Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 12.2480 - mean_squared_error: 12.2480 - rmse: 3.4997 - mean_absolute_error: 2.8301
Epoch 00017: val_loss did not improve from 11.00079
4/4 [==============================] - 0s 118ms/step - loss: 12.2480 - mean_squared_error: 12.2480 - rmse: 3.4997 - mean_absolute_error: 2.8301 - val_loss: 11.0022 - val_mean_squared_error: 11.0022 - val_rmse: 3.3170 - val_mean_absolute_error: 2.7890 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 12.2475 -

4/4 [==============================] - ETA: 0s - loss: 12.1243 - mean_squared_error: 12.1243 - rmse: 3.4820 - mean_absolute_error: 2.8219
Epoch 00033: val_loss improved from 10.91874 to 10.89175, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 1s 128ms/step - loss: 12.1243 - mean_squared_error: 12.1243 - rmse: 3.4820 - mean_absolute_error: 2.8219 - val_loss: 10.8918 - val_mean_squared_error: 10.8918 - val_rmse: 3.3003 - val_mean_absolute_error: 2.7704 - lr: 0.0100
Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 12.0907 - mean_squared_error: 12.0907 - rmse: 3.4772 - mean_absolute_error: 2.8072
Epoch 00034: val_loss improved from 10.89175 to 10.87407, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 1s 135ms/step - loss: 12.0907 - mean_squared_error: 12.0907 - rmse: 3.4772 - mean_absolute_error: 2.8072 - val_loss: 10.8741 - val_mean_squared_error: 10.8741 - val_rmse: 3.2976 - val_mean_absolute_error: 2.7686 - lr: 0.0100
Ep

Epoch 50/1000
4/4 [==============================] - ETA: 0s - loss: 10.7928 - mean_squared_error: 10.7928 - rmse: 3.2852 - mean_absolute_error: 2.6484
Epoch 00050: val_loss improved from 10.32726 to 9.58555, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 1s 133ms/step - loss: 10.7928 - mean_squared_error: 10.7928 - rmse: 3.2852 - mean_absolute_error: 2.6484 - val_loss: 9.5856 - val_mean_squared_error: 9.5856 - val_rmse: 3.0961 - val_mean_absolute_error: 2.5961 - lr: 0.0100
Epoch 51/1000
4/4 [==============================] - ETA: 0s - loss: 10.2541 - mean_squared_error: 10.2541 - rmse: 3.2022 - mean_absolute_error: 2.5930
Epoch 00051: val_loss improved from 9.58555 to 9.38521, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 0s 124ms/step - loss: 10.2541 - mean_squared_error: 10.2541 - rmse: 3.2022 - mean_absolute_error: 2.5930 - val_loss: 9.3852 - val_mean_squared_error: 9.3852 - val_rmse: 3.0635 - val_mean_absolute_error: 2.5835 - lr: 0.

4/4 [==============================] - ETA: 0s - loss: 8.3198 - mean_squared_error: 8.3198 - rmse: 2.8844 - mean_absolute_error: 2.3350
Epoch 00067: val_loss did not improve from 7.93907
4/4 [==============================] - 0s 119ms/step - loss: 8.3198 - mean_squared_error: 8.3198 - rmse: 2.8844 - mean_absolute_error: 2.3350 - val_loss: 8.0767 - val_mean_squared_error: 8.0767 - val_rmse: 2.8420 - val_mean_absolute_error: 2.3204 - lr: 0.0100
Epoch 68/1000
4/4 [==============================] - ETA: 0s - loss: 7.3407 - mean_squared_error: 7.3407 - rmse: 2.7094 - mean_absolute_error: 2.2152
Epoch 00068: val_loss improved from 7.93907 to 7.40229, saving model to /tmp/lstm1v0.m5
4/4 [==============================] - 0s 123ms/step - loss: 7.3407 - mean_squared_error: 7.3407 - rmse: 2.7094 - mean_absolute_error: 2.2152 - val_loss: 7.4023 - val_mean_squared_error: 7.4023 - val_rmse: 2.7207 - val_mean_absolute_error: 2.2414 - lr: 0.0100
Epoch 69/1000
4/4 [==============================] - ET

...

Epoch 248/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.9461 - mean_squared_error: 14.9461 - rmse: 3.8660 - mean_absolute_error: 3.1333
Epoch 00248: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 68ms/step - loss: 13.9021 - mean_squared_error: 13.9021 - rmse: 3.7285 - mean_absolute_error: 3.0201 - val_loss: 15.5575 - val_mean_squared_error: 15.5575 - val_rmse: 3.9443 - val_mean_absolute_error: 3.4360 - lr: 0.0050
Epoch 249/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.8989 - mean_squared_error: 14.8989 - rmse: 3.8599 - mean_absolute_error: 3.1065
Epoch 00249: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 66ms/step - loss: 13.9153 - mean_squared_error: 13.9153 - rmse: 3.7303 - mean_absolute_error: 3.0193 - val_loss: 15.5315 - val_mean_squared_error: 15.5315 - val_rmse: 3.9410 - val_mean_absolute_error: 3.4352 - lr: 0.0050
Epoch 250/1000
1/2 [==============>...............] - ETA: 0s - lo

Epoch 266/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.6176 - mean_squared_error: 13.6176 - rmse: 3.6902 - mean_absolute_error: 3.0220
Epoch 00266: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 68ms/step - loss: 13.6221 - mean_squared_error: 13.6221 - rmse: 3.6908 - mean_absolute_error: 3.0334 - val_loss: 15.2479 - val_mean_squared_error: 15.2479 - val_rmse: 3.9049 - val_mean_absolute_error: 3.4224 - lr: 0.0025
Epoch 267/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.2517 - mean_squared_error: 14.2517 - rmse: 3.7751 - mean_absolute_error: 3.1294
Epoch 00267: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 67ms/step - loss: 13.5998 - mean_squared_error: 13.5998 - rmse: 3.6878 - mean_absolute_error: 3.0410 - val_loss: 15.2490 - val_mean_squared_error: 15.2490 - val_rmse: 3.9050 - val_mean_absolute_error: 3.4240 - lr: 0.0025
Epoch 268/1000
1/2 [==============>...............] - ETA: 0s - lo

Epoch 284/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.1495 - mean_squared_error: 14.1495 - rmse: 3.7616 - mean_absolute_error: 3.1242
Epoch 00284: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 67ms/step - loss: 13.4816 - mean_squared_error: 13.4816 - rmse: 3.6717 - mean_absolute_error: 3.0352 - val_loss: 15.0157 - val_mean_squared_error: 15.0157 - val_rmse: 3.8750 - val_mean_absolute_error: 3.3935 - lr: 0.0012
Epoch 285/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.6104 - mean_squared_error: 12.6104 - rmse: 3.5511 - mean_absolute_error: 2.9151
Epoch 00285: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 70ms/step - loss: 13.4669 - mean_squared_error: 13.4669 - rmse: 3.6697 - mean_absolute_error: 3.0335 - val_loss: 14.9951 - val_mean_squared_error: 14.9951 - val_rmse: 3.8724 - val_mean_absolute_error: 3.3896 - lr: 0.0012
Epoch 286/1000
1/2 [==============>...............] - ETA: 0s - lo

Epoch 302/1000
1/2 [==============>...............] - ETA: 0s - loss: 14.1127 - mean_squared_error: 14.1127 - rmse: 3.7567 - mean_absolute_error: 3.1121
Epoch 00302: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 68ms/step - loss: 13.3995 - mean_squared_error: 13.3995 - rmse: 3.6605 - mean_absolute_error: 3.0307 - val_loss: 14.8724 - val_mean_squared_error: 14.8724 - val_rmse: 3.8565 - val_mean_absolute_error: 3.3733 - lr: 0.0012
Epoch 303/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.5339 - mean_squared_error: 12.5339 - rmse: 3.5403 - mean_absolute_error: 2.8646
Epoch 00303: val_loss did not improve from 8.19048

Epoch 00303: ReduceLROnPlateau reducing learning rate to 0.0006249999860301614.
2/2 [==============================] - 0s 69ms/step - loss: 13.3902 - mean_squared_error: 13.3902 - rmse: 3.6593 - mean_absolute_error: 3.0207 - val_loss: 14.8578 - val_mean_squared_error: 14.8578 - val_rmse: 3.8546 - val_mean_absolute_error: 3.369

1/2 [==============>...............] - ETA: 0s - loss: 13.1475 - mean_squared_error: 13.1475 - rmse: 3.6260 - mean_absolute_error: 3.0512
Epoch 00319: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 75ms/step - loss: 13.3486 - mean_squared_error: 13.3486 - rmse: 3.6536 - mean_absolute_error: 3.0216 - val_loss: 14.8113 - val_mean_squared_error: 14.8113 - val_rmse: 3.8485 - val_mean_absolute_error: 3.3662 - lr: 6.2500e-04
Epoch 320/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.1605 - mean_squared_error: 13.1605 - rmse: 3.6277 - mean_absolute_error: 3.0155
Epoch 00320: val_loss did not improve from 8.19048
2/2 [==============================] - 0s 66ms/step - loss: 13.3533 - mean_squared_error: 13.3533 - rmse: 3.6542 - mean_absolute_error: 3.0254 - val_loss: 14.8135 - val_mean_squared_error: 14.8135 - val_rmse: 3.8488 - val_mean_absolute_error: 3.3667 - lr: 6.2500e-04
Epoch 321/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.

In [84]:
df_lstm1v0_1 = (df_lstm1v01.merge(df_lstm1v02, how='outer')).merge(df_lstm1v03, how='outer')

#### double-cross-site

In [85]:
df_lstm1v04, history_lstm1v04 = double_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 0, 3, 4, X, y)
df_lstm1v05, history_lstm1v05 = double_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 0, 4, 3, X, y)
df_lstm1v06, history_lstm1v06 = double_cross_site(lstm1v0, 'lstm1v0', '/tmp/lstm1v0.m5', 0.01, 3, 4, 0, X, y)

Model: "model_34"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_35 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm_3 (LSTM)               (None, 100)               69200     
                                                                 
 dense_86 (Dense)            (None, 1)                 101       
                                                                 
Total params: 69,301
Trainable params: 69,301
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
1/1 [==============================] - ETA: 0s - loss: 113.6045 - mean_squared_error: 113.6045 - rmse: 10.6585 - mean_absolute_error: 10.0144
Epoch 00001: val_loss improved from inf to 49.03585, saving model to /tmp/lstm1v0.m5
1/1 [==============================] - 2s 2s/step - loss: 113.6045 - mean_squa

Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 13.6248 - mean_squared_error: 13.6248 - rmse: 3.6912 - mean_absolute_error: 2.8198
Epoch 00017: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 65ms/step - loss: 13.6248 - mean_squared_error: 13.6248 - rmse: 3.6912 - mean_absolute_error: 2.8198 - val_loss: 11.1498 - val_mean_squared_error: 11.1498 - val_rmse: 3.3391 - val_mean_absolute_error: 2.2439 - lr: 0.0100
Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 13.7136 - mean_squared_error: 13.7136 - rmse: 3.7032 - mean_absolute_error: 2.8086
Epoch 00018: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 61ms/step - loss: 13.7136 - mean_squared_error: 13.7136 - rmse: 3.7032 - mean_absolute_error: 2.8086 - val_loss: 11.1778 - val_mean_squared_error: 11.1778 - val_rmse: 3.3433 - val_mean_absolute_error: 2.2416 - lr: 0.0100
Epoch 19/1000
1/1 [==============================] - ETA: 0s - los

1/1 [==============================] - 0s 68ms/step - loss: 13.3838 - mean_squared_error: 13.3838 - rmse: 3.6584 - mean_absolute_error: 2.9943 - val_loss: 11.0031 - val_mean_squared_error: 11.0031 - val_rmse: 3.3171 - val_mean_absolute_error: 2.4280 - lr: 0.0050
Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 13.3684 - mean_squared_error: 13.3684 - rmse: 3.6563 - mean_absolute_error: 2.9856
Epoch 00035: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 62ms/step - loss: 13.3684 - mean_squared_error: 13.3684 - rmse: 3.6563 - mean_absolute_error: 2.9856 - val_loss: 10.9791 - val_mean_squared_error: 10.9791 - val_rmse: 3.3135 - val_mean_absolute_error: 2.4185 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 13.3520 - mean_squared_error: 13.3520 - rmse: 3.6540 - mean_absolute_error: 2.9751
Epoch 00036: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 60ms/step - loss: 13.352

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 13.3149 - mean_squared_error: 13.3149 - rmse: 3.6490 - mean_absolute_error: 2.8898
Epoch 00052: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 64ms/step - loss: 13.3149 - mean_squared_error: 13.3149 - rmse: 3.6490 - mean_absolute_error: 2.8898 - val_loss: 10.8733 - val_mean_squared_error: 10.8733 - val_rmse: 3.2975 - val_mean_absolute_error: 2.3370 - lr: 0.0050
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 13.3116 - mean_squared_error: 13.3116 - rmse: 3.6485 - mean_absolute_error: 2.8934
Epoch 00053: val_loss did not improve from 10.87076

Epoch 00053: ReduceLROnPlateau reducing learning rate to 0.0024999999441206455.
1/1 [==============================] - 0s 60ms/step - loss: 13.3116 - mean_squared_error: 13.3116 - rmse: 3.6485 - mean_absolute_error: 2.8934 - val_loss: 10.8747 - val_mean_squared_error: 10.8747 - val_rmse: 3.2977 - val_mean_absolute_error: 2.342

Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 13.3055 - mean_squared_error: 13.3055 - rmse: 3.6477 - mean_absolute_error: 2.9207
Epoch 00070: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 61ms/step - loss: 13.3055 - mean_squared_error: 13.3055 - rmse: 3.6477 - mean_absolute_error: 2.9207 - val_loss: 10.8929 - val_mean_squared_error: 10.8929 - val_rmse: 3.3004 - val_mean_absolute_error: 2.3688 - lr: 0.0025
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 13.3053 - mean_squared_error: 13.3053 - rmse: 3.6476 - mean_absolute_error: 2.9203
Epoch 00071: val_loss did not improve from 10.87076
1/1 [==============================] - 0s 62ms/step - loss: 13.3053 - mean_squared_error: 13.3053 - rmse: 3.6476 - mean_absolute_error: 2.9203 - val_loss: 10.8923 - val_mean_squared_error: 10.8923 - val_rmse: 3.3003 - val_mean_absolute_error: 2.3683 - lr: 0.0025
Epoch 72/1000
1/1 [==============================] - ETA: 0s - los

...

Epoch 23/1000
1/1 [==============================] - ETA: 0s - loss: 12.7303 - mean_squared_error: 12.7303 - rmse: 3.5680 - mean_absolute_error: 2.8744
Epoch 00023: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 130ms/step - loss: 12.7303 - mean_squared_error: 12.7303 - rmse: 3.5680 - mean_absolute_error: 2.8744 - val_loss: 14.6589 - val_mean_squared_error: 14.6589 - val_rmse: 3.8287 - val_mean_absolute_error: 2.9884 - lr: 0.0100
Epoch 24/1000
1/1 [==============================] - ETA: 0s - loss: 12.5875 - mean_squared_error: 12.5875 - rmse: 3.5479 - mean_absolute_error: 2.8856
Epoch 00024: val_loss did not improve from 14.18027

Epoch 00024: ReduceLROnPlateau reducing learning rate to 0.004999999888241291.
1/1 [==============================] - 0s 130ms/step - loss: 12.5875 - mean_squared_error: 12.5875 - rmse: 3.5479 - mean_absolute_error: 2.8856 - val_loss: 14.4542 - val_mean_squared_error: 14.4542 - val_rmse: 3.8019 - val_mean_absolute_error: 3.00

Epoch 41/1000
1/1 [==============================] - ETA: 0s - loss: 12.4838 - mean_squared_error: 12.4838 - rmse: 3.5332 - mean_absolute_error: 2.9376
Epoch 00041: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 129ms/step - loss: 12.4838 - mean_squared_error: 12.4838 - rmse: 3.5332 - mean_absolute_error: 2.9376 - val_loss: 14.2772 - val_mean_squared_error: 14.2772 - val_rmse: 3.7785 - val_mean_absolute_error: 3.0273 - lr: 0.0050
Epoch 42/1000
1/1 [==============================] - ETA: 0s - loss: 12.4766 - mean_squared_error: 12.4766 - rmse: 3.5322 - mean_absolute_error: 2.9309
Epoch 00042: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 140ms/step - loss: 12.4766 - mean_squared_error: 12.4766 - rmse: 3.5322 - mean_absolute_error: 2.9309 - val_loss: 14.2997 - val_mean_squared_error: 14.2997 - val_rmse: 3.7815 - val_mean_absolute_error: 3.0234 - lr: 0.0050
Epoch 43/1000
1/1 [==============================] - ETA: 0s - l

Epoch 59/1000
1/1 [==============================] - ETA: 0s - loss: 12.4701 - mean_squared_error: 12.4701 - rmse: 3.5313 - mean_absolute_error: 2.9148
Epoch 00059: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 155ms/step - loss: 12.4701 - mean_squared_error: 12.4701 - rmse: 3.5313 - mean_absolute_error: 2.9148 - val_loss: 14.3421 - val_mean_squared_error: 14.3421 - val_rmse: 3.7871 - val_mean_absolute_error: 3.0166 - lr: 0.0025
Epoch 60/1000
1/1 [==============================] - ETA: 0s - loss: 12.4689 - mean_squared_error: 12.4689 - rmse: 3.5311 - mean_absolute_error: 2.9158
Epoch 00060: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 131ms/step - loss: 12.4689 - mean_squared_error: 12.4689 - rmse: 3.5311 - mean_absolute_error: 2.9158 - val_loss: 14.3349 - val_mean_squared_error: 14.3349 - val_rmse: 3.7861 - val_mean_absolute_error: 3.0174 - lr: 0.0025
Epoch 61/1000
1/1 [==============================] - ETA: 0s - l

Epoch 77/1000
1/1 [==============================] - ETA: 0s - loss: 12.4629 - mean_squared_error: 12.4629 - rmse: 3.5303 - mean_absolute_error: 2.9232
Epoch 00077: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 139ms/step - loss: 12.4629 - mean_squared_error: 12.4629 - rmse: 3.5303 - mean_absolute_error: 2.9232 - val_loss: 14.2966 - val_mean_squared_error: 14.2966 - val_rmse: 3.7811 - val_mean_absolute_error: 3.0220 - lr: 0.0012
Epoch 78/1000
1/1 [==============================] - ETA: 0s - loss: 12.4627 - mean_squared_error: 12.4627 - rmse: 3.5302 - mean_absolute_error: 2.9231
Epoch 00078: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 128ms/step - loss: 12.4627 - mean_squared_error: 12.4627 - rmse: 3.5302 - mean_absolute_error: 2.9231 - val_loss: 14.2968 - val_mean_squared_error: 14.2968 - val_rmse: 3.7811 - val_mean_absolute_error: 3.0219 - lr: 0.0012
Epoch 79/1000
1/1 [==============================] - ETA: 0s - l

1/1 [==============================] - ETA: 0s - loss: 12.4590 - mean_squared_error: 12.4590 - rmse: 3.5297 - mean_absolute_error: 2.9207
Epoch 00094: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 140ms/step - loss: 12.4590 - mean_squared_error: 12.4590 - rmse: 3.5297 - mean_absolute_error: 2.9207 - val_loss: 14.3035 - val_mean_squared_error: 14.3035 - val_rmse: 3.7820 - val_mean_absolute_error: 3.0203 - lr: 6.2500e-04
Epoch 95/1000
1/1 [==============================] - ETA: 0s - loss: 12.4588 - mean_squared_error: 12.4588 - rmse: 3.5297 - mean_absolute_error: 2.9206
Epoch 00095: val_loss did not improve from 14.18027
1/1 [==============================] - 0s 132ms/step - loss: 12.4588 - mean_squared_error: 12.4588 - rmse: 3.5297 - mean_absolute_error: 2.9206 - val_loss: 14.3038 - val_mean_squared_error: 14.3038 - val_rmse: 3.7820 - val_mean_absolute_error: 3.0202 - lr: 6.2500e-04
Epoch 96/1000
1/1 [==============================] - ETA: 0s - loss: 1

In [86]:
df_lstm1v0_2 = (df_lstm1v04.merge(df_lstm1v05, how='outer')).merge(df_lstm1v06, how='outer')

### lstm1

#### single-cross-site

In [87]:
df_lstm11, history_lstm11 = single_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 0, 3, 4, X, y)
df_lstm12, history_lstm12 = single_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 3, 0, 4, X, y)
df_lstm13, history_lstm13 = single_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 4, 0, 3, X, y)

Model: "model_37"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_38 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm_6 (LSTM)               (None, 100)               69200     
                                                                 
 dense_89 (Dense)            (None, 1)                 101       
                                                                 
Total params: 69,301
Trainable params: 69,301
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
4/4 [==============================] - ETA: 0s - loss: 57.3572 - mean_squared_error: 57.3572 - rmse: 7.5735 - mean_absolute_error: 6.2358  
Epoch 00001: val_loss improved from inf to 13.19039, saving model to /tmp/lstm1.m5
4/4 [==============================] - 2s 241ms/step - loss: 57.3572 - mean_square

Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 11.6043 - mean_squared_error: 11.6043 - rmse: 3.4065 - mean_absolute_error: 2.7957
Epoch 00017: val_loss did not improve from 12.63062
4/4 [==============================] - 0s 120ms/step - loss: 11.6043 - mean_squared_error: 11.6043 - rmse: 3.4065 - mean_absolute_error: 2.7957 - val_loss: 12.7115 - val_mean_squared_error: 12.7115 - val_rmse: 3.5653 - val_mean_absolute_error: 2.9233 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 11.5026 - mean_squared_error: 11.5026 - rmse: 3.3915 - mean_absolute_error: 2.7658
Epoch 00018: val_loss improved from 12.63062 to 12.61639, saving model to /tmp/lstm1.m5
4/4 [==============================] - 0s 123ms/step - loss: 11.5026 - mean_squared_error: 11.5026 - rmse: 3.3915 - mean_absolute_error: 2.7658 - val_loss: 12.6164 - val_mean_squared_error: 12.6164 - val_rmse: 3.5520 - val_mean_absolute_error: 2.9178 - lr: 0.0100
Epoch 19/1000
4/4 [=========

Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 11.2190 - mean_squared_error: 11.2190 - rmse: 3.3495 - mean_absolute_error: 2.7136
Epoch 00034: val_loss improved from 12.33764 to 12.29351, saving model to /tmp/lstm1.m5
4/4 [==============================] - 0s 124ms/step - loss: 11.2190 - mean_squared_error: 11.2190 - rmse: 3.3495 - mean_absolute_error: 2.7136 - val_loss: 12.2935 - val_mean_squared_error: 12.2935 - val_rmse: 3.5062 - val_mean_absolute_error: 2.8793 - lr: 0.0100
Epoch 35/1000
4/4 [==============================] - ETA: 0s - loss: 11.1554 - mean_squared_error: 11.1554 - rmse: 3.3400 - mean_absolute_error: 2.6847
Epoch 00035: val_loss improved from 12.29351 to 12.22313, saving model to /tmp/lstm1.m5
4/4 [==============================] - 0s 128ms/step - loss: 11.1554 - mean_squared_error: 11.1554 - rmse: 3.3400 - mean_absolute_error: 2.6847 - val_loss: 12.2231 - val_mean_squared_error: 12.2231 - val_rmse: 3.4962 - val_mean_absolute_error: 2.8686 - lr:

Epoch 51/1000
4/4 [==============================] - ETA: 0s - loss: 9.0234 - mean_squared_error: 9.0234 - rmse: 3.0039 - mean_absolute_error: 2.4368
Epoch 00051: val_loss did not improve from 9.87836
4/4 [==============================] - 0s 121ms/step - loss: 9.0234 - mean_squared_error: 9.0234 - rmse: 3.0039 - mean_absolute_error: 2.4368 - val_loss: 12.2159 - val_mean_squared_error: 12.2159 - val_rmse: 3.4951 - val_mean_absolute_error: 2.8156 - lr: 0.0100
Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 11.3103 - mean_squared_error: 11.3103 - rmse: 3.3631 - mean_absolute_error: 2.7228
Epoch 00052: val_loss improved from 9.87836 to 8.95575, saving model to /tmp/lstm1.m5
4/4 [==============================] - 0s 127ms/step - loss: 11.3103 - mean_squared_error: 11.3103 - rmse: 3.3631 - mean_absolute_error: 2.7228 - val_loss: 8.9557 - val_mean_squared_error: 8.9557 - val_rmse: 2.9926 - val_mean_absolute_error: 2.4258 - lr: 0.0100
Epoch 53/1000
4/4 [==================

Epoch 69/1000
4/4 [==============================] - ETA: 0s - loss: 7.0312 - mean_squared_error: 7.0312 - rmse: 2.6516 - mean_absolute_error: 2.0801
Epoch 00069: val_loss did not improve from 7.64099
4/4 [==============================] - 0s 119ms/step - loss: 7.0312 - mean_squared_error: 7.0312 - rmse: 2.6516 - mean_absolute_error: 2.0801 - val_loss: 8.6698 - val_mean_squared_error: 8.6698 - val_rmse: 2.9445 - val_mean_absolute_error: 2.3966 - lr: 0.0100
Epoch 70/1000
4/4 [==============================] - ETA: 0s - loss: 7.4029 - mean_squared_error: 7.4029 - rmse: 2.7208 - mean_absolute_error: 2.1560
Epoch 00070: val_loss improved from 7.64099 to 7.47932, saving model to /tmp/lstm1.m5
4/4 [==============================] - 0s 125ms/step - loss: 7.4029 - mean_squared_error: 7.4029 - rmse: 2.7208 - mean_absolute_error: 2.1560 - val_loss: 7.4793 - val_mean_squared_error: 7.4793 - val_rmse: 2.7348 - val_mean_absolute_error: 2.2015 - lr: 0.0100
Epoch 71/1000
4/4 [========================

...

Epoch 116/1000
1/2 [==============>...............] - ETA: 0s - loss: 11.9449 - mean_squared_error: 11.9449 - rmse: 3.4561 - mean_absolute_error: 2.9321
Epoch 00116: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 70ms/step - loss: 12.8445 - mean_squared_error: 12.8445 - rmse: 3.5839 - mean_absolute_error: 3.0478 - val_loss: 16.1323 - val_mean_squared_error: 16.1323 - val_rmse: 4.0165 - val_mean_absolute_error: 3.5353 - lr: 0.0050
Epoch 117/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.9983 - mean_squared_error: 12.9983 - rmse: 3.6053 - mean_absolute_error: 3.0390
Epoch 00117: val_loss did not improve from 15.48493

Epoch 00117: ReduceLROnPlateau reducing learning rate to 0.0024999999441206455.
2/2 [==============================] - 0s 74ms/step - loss: 12.8412 - mean_squared_error: 12.8412 - rmse: 3.5835 - mean_absolute_error: 3.0481 - val_loss: 16.0989 - val_mean_squared_error: 16.0989 - val_rmse: 4.0123 - val_mean_absolute_error: 3.5

Epoch 134/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.6500 - mean_squared_error: 13.6500 - rmse: 3.6946 - mean_absolute_error: 3.0831
Epoch 00134: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 72ms/step - loss: 12.7394 - mean_squared_error: 12.7394 - rmse: 3.5692 - mean_absolute_error: 2.9875 - val_loss: 16.0071 - val_mean_squared_error: 16.0071 - val_rmse: 4.0009 - val_mean_absolute_error: 3.4541 - lr: 0.0025
Epoch 135/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.1035 - mean_squared_error: 13.1035 - rmse: 3.6199 - mean_absolute_error: 2.9952
Epoch 00135: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 71ms/step - loss: 12.7092 - mean_squared_error: 12.7092 - rmse: 3.5650 - mean_absolute_error: 2.9914 - val_loss: 16.0248 - val_mean_squared_error: 16.0248 - val_rmse: 4.0031 - val_mean_absolute_error: 3.4564 - lr: 0.0025
Epoch 136/1000
1/2 [==============>...............] - ETA: 0s - 

Epoch 152/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.3791 - mean_squared_error: 12.3791 - rmse: 3.5184 - mean_absolute_error: 2.9812
Epoch 00152: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 68ms/step - loss: 12.6640 - mean_squared_error: 12.6640 - rmse: 3.5587 - mean_absolute_error: 3.0091 - val_loss: 15.9087 - val_mean_squared_error: 15.9087 - val_rmse: 3.9886 - val_mean_absolute_error: 3.4694 - lr: 0.0012
Epoch 153/1000
1/2 [==============>...............] - ETA: 0s - loss: 13.1025 - mean_squared_error: 13.1025 - rmse: 3.6197 - mean_absolute_error: 3.0481
Epoch 00153: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 70ms/step - loss: 12.6478 - mean_squared_error: 12.6478 - rmse: 3.5564 - mean_absolute_error: 3.0008 - val_loss: 15.9030 - val_mean_squared_error: 15.9030 - val_rmse: 3.9879 - val_mean_absolute_error: 3.4572 - lr: 0.0012
Epoch 154/1000
1/2 [==============>...............] - ETA: 0s - 

1/2 [==============>...............] - ETA: 0s - loss: 13.2772 - mean_squared_error: 13.2772 - rmse: 3.6438 - mean_absolute_error: 3.0659
Epoch 00169: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 75ms/step - loss: 12.6104 - mean_squared_error: 12.6104 - rmse: 3.5511 - mean_absolute_error: 2.9983 - val_loss: 15.8486 - val_mean_squared_error: 15.8486 - val_rmse: 3.9810 - val_mean_absolute_error: 3.4608 - lr: 6.2500e-04
Epoch 170/1000
1/2 [==============>...............] - ETA: 0s - loss: 11.9086 - mean_squared_error: 11.9086 - rmse: 3.4509 - mean_absolute_error: 2.9259
Epoch 00170: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 72ms/step - loss: 12.6115 - mean_squared_error: 12.6115 - rmse: 3.5513 - mean_absolute_error: 2.9951 - val_loss: 15.8514 - val_mean_squared_error: 15.8514 - val_rmse: 3.9814 - val_mean_absolute_error: 3.4580 - lr: 6.2500e-04
Epoch 171/1000
1/2 [==============>...............] - ETA: 0s - loss: 1

1/2 [==============>...............] - ETA: 0s - loss: 12.1649 - mean_squared_error: 12.1649 - rmse: 3.4878 - mean_absolute_error: 2.9401
Epoch 00186: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 73ms/step - loss: 12.5907 - mean_squared_error: 12.5907 - rmse: 3.5483 - mean_absolute_error: 2.9877 - val_loss: 15.8397 - val_mean_squared_error: 15.8397 - val_rmse: 3.9799 - val_mean_absolute_error: 3.4506 - lr: 3.1250e-04
Epoch 187/1000
1/2 [==============>...............] - ETA: 0s - loss: 12.3068 - mean_squared_error: 12.3068 - rmse: 3.5081 - mean_absolute_error: 2.9478
Epoch 00187: val_loss did not improve from 15.48493
2/2 [==============================] - 0s 72ms/step - loss: 12.5917 - mean_squared_error: 12.5917 - rmse: 3.5485 - mean_absolute_error: 2.9862 - val_loss: 15.8392 - val_mean_squared_error: 15.8392 - val_rmse: 3.9798 - val_mean_absolute_error: 3.4496 - lr: 3.1250e-04
Epoch 188/1000
1/2 [==============>...............] - ETA: 0s - loss: 1

In [88]:
df_lstm1_1 = (df_lstm11.merge(df_lstm12, how='outer')).merge(df_lstm13, how='outer')

#### double-cross-site

In [89]:
df_lstm14, history_lstm14 = double_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 0, 3, 4, X, y)
df_lstm15, history_lstm15 = double_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 0, 4, 3, X, y)
df_lstm16, history_lstm16 = double_cross_site(lstm1, 'lstm1', '/tmp/lstm1.m5', 0.01, 3, 4, 0, X, y)

Model: "model_40"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_41 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm_9 (LSTM)               (None, 100)               69200     
                                                                 
 dense_92 (Dense)            (None, 1)                 101       
                                                                 
Total params: 69,301
Trainable params: 69,301
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
1/1 [==============================] - ETA: 0s - loss: 130.0111 - mean_squared_error: 130.0111 - rmse: 11.4022 - mean_absolute_error: 10.8814
Epoch 00001: val_loss improved from inf to 68.33839, saving model to /tmp/lstm1.m5
1/1 [==============================] - 2s 2s/step - loss: 130.0111 - mean_square

1/1 [==============================] - ETA: 0s - loss: 11.6932 - mean_squared_error: 11.6932 - rmse: 3.4195 - mean_absolute_error: 2.6836
Epoch 00016: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 102ms/step - loss: 11.6932 - mean_squared_error: 11.6932 - rmse: 3.4195 - mean_absolute_error: 2.6836 - val_loss: 12.0931 - val_mean_squared_error: 12.0931 - val_rmse: 3.4775 - val_mean_absolute_error: 2.8702 - lr: 0.0100
Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 11.9118 - mean_squared_error: 11.9118 - rmse: 3.4514 - mean_absolute_error: 2.6698
Epoch 00017: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 97ms/step - loss: 11.9118 - mean_squared_error: 11.9118 - rmse: 3.4514 - mean_absolute_error: 2.6698 - val_loss: 12.5142 - val_mean_squared_error: 12.5142 - val_rmse: 3.5375 - val_mean_absolute_error: 2.8837 - lr: 0.0100
Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 12.1166 - 

Epoch 34/1000
1/1 [==============================] - ETA: 0s - loss: 11.7028 - mean_squared_error: 11.7028 - rmse: 3.4209 - mean_absolute_error: 2.8313
Epoch 00034: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 78ms/step - loss: 11.7028 - mean_squared_error: 11.7028 - rmse: 3.4209 - mean_absolute_error: 2.8313 - val_loss: 10.4175 - val_mean_squared_error: 10.4175 - val_rmse: 3.2276 - val_mean_absolute_error: 2.7786 - lr: 0.0050
Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 11.6807 - mean_squared_error: 11.6807 - rmse: 3.4177 - mean_absolute_error: 2.8234
Epoch 00035: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 76ms/step - loss: 11.6807 - mean_squared_error: 11.6807 - rmse: 3.4177 - mean_absolute_error: 2.8234 - val_loss: 10.4425 - val_mean_squared_error: 10.4425 - val_rmse: 3.2315 - val_mean_absolute_error: 2.7820 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - los

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 11.5387 - mean_squared_error: 11.5387 - rmse: 3.3969 - mean_absolute_error: 2.7026
Epoch 00052: val_loss did not improve from 10.33462

Epoch 00052: ReduceLROnPlateau reducing learning rate to 0.0024999999441206455.
1/1 [==============================] - 0s 77ms/step - loss: 11.5387 - mean_squared_error: 11.5387 - rmse: 3.3969 - mean_absolute_error: 2.7026 - val_loss: 11.0837 - val_mean_squared_error: 11.0837 - val_rmse: 3.3292 - val_mean_absolute_error: 2.8301 - lr: 0.0050
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 11.5317 - mean_squared_error: 11.5317 - rmse: 3.3958 - mean_absolute_error: 2.7047
Epoch 00053: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 75ms/step - loss: 11.5317 - mean_squared_error: 11.5317 - rmse: 3.3958 - mean_absolute_error: 2.7047 - val_loss: 11.0653 - val_mean_squared_error: 11.0653 - val_rmse: 3.3265 - val_mean_absolute_error: 2.829

Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 11.4269 - mean_squared_error: 11.4269 - rmse: 3.3804 - mean_absolute_error: 2.7390
Epoch 00070: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 75ms/step - loss: 11.4269 - mean_squared_error: 11.4269 - rmse: 3.3804 - mean_absolute_error: 2.7390 - val_loss: 10.7718 - val_mean_squared_error: 10.7718 - val_rmse: 3.2820 - val_mean_absolute_error: 2.8194 - lr: 0.0025
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 11.3893 - mean_squared_error: 11.3893 - rmse: 3.3748 - mean_absolute_error: 2.7316
Epoch 00071: val_loss did not improve from 10.33462
1/1 [==============================] - 0s 71ms/step - loss: 11.3893 - mean_squared_error: 11.3893 - rmse: 3.3748 - mean_absolute_error: 2.7316 - val_loss: 10.7344 - val_mean_squared_error: 10.7344 - val_rmse: 3.2763 - val_mean_absolute_error: 2.8090 - lr: 0.0025
Epoch 72/1000
1/1 [==============================] - ETA: 0s - los

...

Epoch 44/1000
1/1 [==============================] - ETA: 0s - loss: 13.7652 - mean_squared_error: 13.7652 - rmse: 3.7101 - mean_absolute_error: 2.9216
Epoch 00044: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 156ms/step - loss: 13.7652 - mean_squared_error: 13.7652 - rmse: 3.7101 - mean_absolute_error: 2.9216 - val_loss: 10.0900 - val_mean_squared_error: 10.0900 - val_rmse: 3.1765 - val_mean_absolute_error: 2.8002 - lr: 0.0050
Epoch 45/1000
1/1 [==============================] - ETA: 0s - loss: 13.7655 - mean_squared_error: 13.7655 - rmse: 3.7102 - mean_absolute_error: 2.9212
Epoch 00045: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 135ms/step - loss: 13.7655 - mean_squared_error: 13.7655 - rmse: 3.7102 - mean_absolute_error: 2.9212 - val_loss: 10.0938 - val_mean_squared_error: 10.0938 - val_rmse: 3.1771 - val_mean_absolute_error: 2.8011 - lr: 0.0050
Epoch 46/1000
1/1 [==============================] - ETA: 0s - los

Epoch 62/1000
1/1 [==============================] - ETA: 0s - loss: 13.7002 - mean_squared_error: 13.7002 - rmse: 3.7014 - mean_absolute_error: 2.9581
Epoch 00062: val_loss did not improve from 9.96635

Epoch 00062: ReduceLROnPlateau reducing learning rate to 0.0024999999441206455.
1/1 [==============================] - 0s 145ms/step - loss: 13.7002 - mean_squared_error: 13.7002 - rmse: 3.7014 - mean_absolute_error: 2.9581 - val_loss: 10.4126 - val_mean_squared_error: 10.4126 - val_rmse: 3.2269 - val_mean_absolute_error: 2.8513 - lr: 0.0050
Epoch 63/1000
1/1 [==============================] - ETA: 0s - loss: 13.6970 - mean_squared_error: 13.6970 - rmse: 3.7009 - mean_absolute_error: 2.9569
Epoch 00063: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 161ms/step - loss: 13.6970 - mean_squared_error: 13.6970 - rmse: 3.7009 - mean_absolute_error: 2.9569 - val_loss: 10.4058 - val_mean_squared_error: 10.4058 - val_rmse: 3.2258 - val_mean_absolute_error: 2.850

Epoch 80/1000
1/1 [==============================] - ETA: 0s - loss: 13.6676 - mean_squared_error: 13.6676 - rmse: 3.6970 - mean_absolute_error: 2.9375
Epoch 00080: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 162ms/step - loss: 13.6676 - mean_squared_error: 13.6676 - rmse: 3.6970 - mean_absolute_error: 2.9375 - val_loss: 10.2524 - val_mean_squared_error: 10.2524 - val_rmse: 3.2019 - val_mean_absolute_error: 2.8308 - lr: 0.0025
Epoch 81/1000
1/1 [==============================] - ETA: 0s - loss: 13.6662 - mean_squared_error: 13.6662 - rmse: 3.6968 - mean_absolute_error: 2.9372
Epoch 00081: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 166ms/step - loss: 13.6662 - mean_squared_error: 13.6662 - rmse: 3.6968 - mean_absolute_error: 2.9372 - val_loss: 10.2514 - val_mean_squared_error: 10.2514 - val_rmse: 3.2018 - val_mean_absolute_error: 2.8307 - lr: 0.0025
Epoch 82/1000
1/1 [==============================] - ETA: 0s - los

Epoch 98/1000
1/1 [==============================] - ETA: 0s - loss: 13.6498 - mean_squared_error: 13.6498 - rmse: 3.6946 - mean_absolute_error: 2.9393
Epoch 00098: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 229ms/step - loss: 13.6498 - mean_squared_error: 13.6498 - rmse: 3.6946 - mean_absolute_error: 2.9393 - val_loss: 10.2868 - val_mean_squared_error: 10.2868 - val_rmse: 3.2073 - val_mean_absolute_error: 2.8361 - lr: 0.0012
Epoch 99/1000
1/1 [==============================] - ETA: 0s - loss: 13.6489 - mean_squared_error: 13.6489 - rmse: 3.6944 - mean_absolute_error: 2.9395
Epoch 00099: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 170ms/step - loss: 13.6489 - mean_squared_error: 13.6489 - rmse: 3.6944 - mean_absolute_error: 2.9395 - val_loss: 10.2891 - val_mean_squared_error: 10.2891 - val_rmse: 3.2077 - val_mean_absolute_error: 2.8365 - lr: 0.0012
Epoch 100/1000
1/1 [==============================] - ETA: 0s - lo

1/1 [==============================] - ETA: 0s - loss: 13.6390 - mean_squared_error: 13.6390 - rmse: 3.6931 - mean_absolute_error: 2.9398
Epoch 00115: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 237ms/step - loss: 13.6390 - mean_squared_error: 13.6390 - rmse: 3.6931 - mean_absolute_error: 2.9398 - val_loss: 10.2975 - val_mean_squared_error: 10.2975 - val_rmse: 3.2090 - val_mean_absolute_error: 2.8379 - lr: 6.2500e-04
Epoch 116/1000
1/1 [==============================] - ETA: 0s - loss: 13.6384 - mean_squared_error: 13.6384 - rmse: 3.6930 - mean_absolute_error: 2.9397
Epoch 00116: val_loss did not improve from 9.96635
1/1 [==============================] - 0s 166ms/step - loss: 13.6384 - mean_squared_error: 13.6384 - rmse: 3.6930 - mean_absolute_error: 2.9397 - val_loss: 10.2973 - val_mean_squared_error: 10.2973 - val_rmse: 3.2089 - val_mean_absolute_error: 2.8379 - lr: 6.2500e-04
Epoch 117/1000
1/1 [==============================] - ETA: 0s - loss: 1

In [90]:
df_lstm1_2 = (df_lstm14.merge(df_lstm15, how='outer')).merge(df_lstm16, how='outer')

### lstm2

#### single-cross-site

In [91]:
df_lstm21, history_lstm21 = single_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 0, 3, 4, X, y)
df_lstm22, history_lstm22 = single_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 3, 0, 4, X, y)
df_lstm23, history_lstm23 = single_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 4, 0, 3, X, y)

Model: "model_43"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_44 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm_12 (LSTM)              (None, 100, 100)          69200     
                                                                 
 lstm_13 (LSTM)              (None, 100)               80400     
                                                                 
 dense_95 (Dense)            (None, 1)                 101       
                                                                 
Total params: 149,701
Trainable params: 149,701
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
4/4 [==============================] - ETA: 0s - loss: 55.0601 - mean_squared_error: 55.0601 - rmse: 7.4202 - mean_absolute_error: 5.9624  
Epoch 00001: val_loss improved 

4/4 [==============================] - ETA: 0s - loss: 12.2461 - mean_squared_error: 12.2461 - rmse: 3.4994 - mean_absolute_error: 2.8260
Epoch 00016: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 268ms/step - loss: 12.2461 - mean_squared_error: 12.2461 - rmse: 3.4994 - mean_absolute_error: 2.8260 - val_loss: 12.8290 - val_mean_squared_error: 12.8290 - val_rmse: 3.5818 - val_mean_absolute_error: 2.8517 - lr: 0.0100
Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 12.2339 - mean_squared_error: 12.2339 - rmse: 3.4977 - mean_absolute_error: 2.8232
Epoch 00017: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 271ms/step - loss: 12.2339 - mean_squared_error: 12.2339 - rmse: 3.4977 - mean_absolute_error: 2.8232 - val_loss: 12.7346 - val_mean_squared_error: 12.7346 - val_rmse: 3.5686 - val_mean_absolute_error: 2.8596 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 12.2727 -

Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 12.2198 - mean_squared_error: 12.2198 - rmse: 3.4957 - mean_absolute_error: 2.8475
Epoch 00034: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 273ms/step - loss: 12.2198 - mean_squared_error: 12.2198 - rmse: 3.4957 - mean_absolute_error: 2.8475 - val_loss: 12.6900 - val_mean_squared_error: 12.6900 - val_rmse: 3.5623 - val_mean_absolute_error: 2.8657 - lr: 0.0050
Epoch 35/1000
4/4 [==============================] - ETA: 0s - loss: 12.2215 - mean_squared_error: 12.2215 - rmse: 3.4959 - mean_absolute_error: 2.8449
Epoch 00035: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 266ms/step - loss: 12.2215 - mean_squared_error: 12.2215 - rmse: 3.4959 - mean_absolute_error: 2.8449 - val_loss: 12.7068 - val_mean_squared_error: 12.7068 - val_rmse: 3.5647 - val_mean_absolute_error: 2.8628 - lr: 0.0050
Epoch 36/1000
4/4 [==============================] - ETA: 0s - l

Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 12.2191 - mean_squared_error: 12.2191 - rmse: 3.4956 - mean_absolute_error: 2.8466
Epoch 00052: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 261ms/step - loss: 12.2191 - mean_squared_error: 12.2191 - rmse: 3.4956 - mean_absolute_error: 2.8466 - val_loss: 12.6934 - val_mean_squared_error: 12.6934 - val_rmse: 3.5628 - val_mean_absolute_error: 2.8651 - lr: 0.0025
Epoch 53/1000
4/4 [==============================] - ETA: 0s - loss: 12.2377 - mean_squared_error: 12.2377 - rmse: 3.4982 - mean_absolute_error: 2.8518
Epoch 00053: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 262ms/step - loss: 12.2377 - mean_squared_error: 12.2377 - rmse: 3.4982 - mean_absolute_error: 2.8518 - val_loss: 12.6783 - val_mean_squared_error: 12.6783 - val_rmse: 3.5607 - val_mean_absolute_error: 2.8680 - lr: 0.0025
Epoch 54/1000
4/4 [==============================] - ETA: 0s - l

Epoch 70/1000
4/4 [==============================] - ETA: 0s - loss: 12.2191 - mean_squared_error: 12.2191 - rmse: 3.4956 - mean_absolute_error: 2.8451
Epoch 00070: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 260ms/step - loss: 12.2191 - mean_squared_error: 12.2191 - rmse: 3.4956 - mean_absolute_error: 2.8451 - val_loss: 12.7007 - val_mean_squared_error: 12.7007 - val_rmse: 3.5638 - val_mean_absolute_error: 2.8637 - lr: 0.0012
Epoch 71/1000
4/4 [==============================] - ETA: 0s - loss: 12.2194 - mean_squared_error: 12.2194 - rmse: 3.4956 - mean_absolute_error: 2.8456
Epoch 00071: val_loss did not improve from 12.58447
4/4 [==============================] - 1s 254ms/step - loss: 12.2194 - mean_squared_error: 12.2194 - rmse: 3.4956 - mean_absolute_error: 2.8456 - val_loss: 12.6994 - val_mean_squared_error: 12.6994 - val_rmse: 3.5636 - val_mean_absolute_error: 2.8639 - lr: 0.0012
Epoch 72/1000
4/4 [==============================] - ETA: 0s - l

...

Epoch 27/1000
2/2 [==============================] - ETA: 0s - loss: 13.7103 - mean_squared_error: 13.7103 - rmse: 3.7027 - mean_absolute_error: 3.1029
Epoch 00027: val_loss did not improve from 11.91620

Epoch 00027: ReduceLROnPlateau reducing learning rate to 0.004999999888241291.
2/2 [==============================] - 0s 149ms/step - loss: 13.7103 - mean_squared_error: 13.7103 - rmse: 3.7027 - mean_absolute_error: 3.1029 - val_loss: 12.1011 - val_mean_squared_error: 12.1011 - val_rmse: 3.4787 - val_mean_absolute_error: 3.0310 - lr: 0.0100
Epoch 28/1000
2/2 [==============================] - ETA: 0s - loss: 13.7340 - mean_squared_error: 13.7340 - rmse: 3.7059 - mean_absolute_error: 3.1207
Epoch 00028: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 147ms/step - loss: 13.7340 - mean_squared_error: 13.7340 - rmse: 3.7059 - mean_absolute_error: 3.1207 - val_loss: 12.0957 - val_mean_squared_error: 12.0957 - val_rmse: 3.4779 - val_mean_absolute_error: 3.03

Epoch 45/1000
2/2 [==============================] - ETA: 0s - loss: 13.7650 - mean_squared_error: 13.7650 - rmse: 3.7101 - mean_absolute_error: 3.1367
Epoch 00045: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 131ms/step - loss: 13.7650 - mean_squared_error: 13.7650 - rmse: 3.7101 - mean_absolute_error: 3.1367 - val_loss: 12.0834 - val_mean_squared_error: 12.0834 - val_rmse: 3.4761 - val_mean_absolute_error: 3.0284 - lr: 0.0050
Epoch 46/1000
2/2 [==============================] - ETA: 0s - loss: 13.7970 - mean_squared_error: 13.7970 - rmse: 3.7144 - mean_absolute_error: 3.1252
Epoch 00046: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 139ms/step - loss: 13.7970 - mean_squared_error: 13.7970 - rmse: 3.7144 - mean_absolute_error: 3.1252 - val_loss: 12.1596 - val_mean_squared_error: 12.1596 - val_rmse: 3.4871 - val_mean_absolute_error: 3.0387 - lr: 0.0050
Epoch 47/1000
2/2 [==============================] - ETA: 0s - l

Epoch 63/1000
2/2 [==============================] - ETA: 0s - loss: 13.7065 - mean_squared_error: 13.7065 - rmse: 3.7022 - mean_absolute_error: 3.0930
Epoch 00063: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 122ms/step - loss: 13.7065 - mean_squared_error: 13.7065 - rmse: 3.7022 - mean_absolute_error: 3.0930 - val_loss: 12.2641 - val_mean_squared_error: 12.2641 - val_rmse: 3.5020 - val_mean_absolute_error: 3.0504 - lr: 0.0025
Epoch 64/1000
2/2 [==============================] - ETA: 0s - loss: 13.7058 - mean_squared_error: 13.7058 - rmse: 3.7021 - mean_absolute_error: 3.0910
Epoch 00064: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 140ms/step - loss: 13.7058 - mean_squared_error: 13.7058 - rmse: 3.7021 - mean_absolute_error: 3.0910 - val_loss: 12.2910 - val_mean_squared_error: 12.2910 - val_rmse: 3.5059 - val_mean_absolute_error: 3.0532 - lr: 0.0025
Epoch 65/1000
2/2 [==============================] - ETA: 0s - l

Epoch 81/1000
2/2 [==============================] - ETA: 0s - loss: 13.7156 - mean_squared_error: 13.7156 - rmse: 3.7035 - mean_absolute_error: 3.0717
Epoch 00081: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 137ms/step - loss: 13.7156 - mean_squared_error: 13.7156 - rmse: 3.7035 - mean_absolute_error: 3.0717 - val_loss: 12.4270 - val_mean_squared_error: 12.4270 - val_rmse: 3.5252 - val_mean_absolute_error: 3.0659 - lr: 0.0012
Epoch 82/1000
2/2 [==============================] - ETA: 0s - loss: 13.7178 - mean_squared_error: 13.7178 - rmse: 3.7038 - mean_absolute_error: 3.0700
Epoch 00082: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 121ms/step - loss: 13.7178 - mean_squared_error: 13.7178 - rmse: 3.7038 - mean_absolute_error: 3.0700 - val_loss: 12.4288 - val_mean_squared_error: 12.4288 - val_rmse: 3.5255 - val_mean_absolute_error: 3.0661 - lr: 0.0012
Epoch 83/1000
2/2 [==============================] - ETA: 0s - l

2/2 [==============================] - ETA: 0s - loss: 13.7041 - mean_squared_error: 13.7041 - rmse: 3.7019 - mean_absolute_error: 3.0996
Epoch 00098: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 121ms/step - loss: 13.7041 - mean_squared_error: 13.7041 - rmse: 3.7019 - mean_absolute_error: 3.0996 - val_loss: 12.2315 - val_mean_squared_error: 12.2315 - val_rmse: 3.4974 - val_mean_absolute_error: 3.0470 - lr: 6.2500e-04
Epoch 99/1000
2/2 [==============================] - ETA: 0s - loss: 13.7018 - mean_squared_error: 13.7018 - rmse: 3.7016 - mean_absolute_error: 3.0956
Epoch 00099: val_loss did not improve from 11.91620
2/2 [==============================] - 0s 119ms/step - loss: 13.7018 - mean_squared_error: 13.7018 - rmse: 3.7016 - mean_absolute_error: 3.0956 - val_loss: 12.2588 - val_mean_squared_error: 12.2588 - val_rmse: 3.5013 - val_mean_absolute_error: 3.0499 - lr: 6.2500e-04
Epoch 100/1000
2/2 [==============================] - ETA: 0s - loss: 

In [92]:
df_lstm2_1 = (df_lstm21.merge(df_lstm22, how='outer')).merge(df_lstm23, how='outer')

#### double-cross-site

In [93]:
df_lstm24, history_lstm24 = double_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 0, 3, 4, X, y)
df_lstm25, history_lstm25 = double_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 0, 4, 3, X, y)
df_lstm26, history_lstm26 = double_cross_site(lstm2, 'lstm2', '/tmp/lstm2.m5', 0.01, 3, 4, 0, X, y)

Model: "model_46"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_47 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 lstm_18 (LSTM)              (None, 100, 100)          69200     
                                                                 
 lstm_19 (LSTM)              (None, 100)               80400     
                                                                 
 dense_98 (Dense)            (None, 1)                 101       
                                                                 
Total params: 149,701
Trainable params: 149,701
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
1/1 [==============================] - ETA: 0s - loss: 145.1672 - mean_squared_error: 145.1672 - rmse: 12.0485 - mean_absolute_error: 11.2533
Epoch 00001: val_loss improve

1/1 [==============================] - ETA: 0s - loss: 18.8779 - mean_squared_error: 18.8779 - rmse: 4.3449 - mean_absolute_error: 3.3713
Epoch 00016: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 131ms/step - loss: 18.8779 - mean_squared_error: 18.8779 - rmse: 4.3449 - mean_absolute_error: 3.3713 - val_loss: 15.4650 - val_mean_squared_error: 15.4650 - val_rmse: 3.9326 - val_mean_absolute_error: 3.3679 - lr: 0.0100
Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 19.1350 - mean_squared_error: 19.1350 - rmse: 4.3744 - mean_absolute_error: 3.3623
Epoch 00017: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 123ms/step - loss: 19.1350 - mean_squared_error: 19.1350 - rmse: 4.3744 - mean_absolute_error: 3.3623 - val_loss: 15.3827 - val_mean_squared_error: 15.3827 - val_rmse: 3.9221 - val_mean_absolute_error: 3.3585 - lr: 0.0100
Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 19.3120 -

Epoch 34/1000
1/1 [==============================] - ETA: 0s - loss: 18.5797 - mean_squared_error: 18.5797 - rmse: 4.3104 - mean_absolute_error: 3.5549
Epoch 00034: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 129ms/step - loss: 18.5797 - mean_squared_error: 18.5797 - rmse: 4.3104 - mean_absolute_error: 3.5549 - val_loss: 17.6991 - val_mean_squared_error: 17.6991 - val_rmse: 4.2070 - val_mean_absolute_error: 3.4921 - lr: 0.0050
Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 18.5787 - mean_squared_error: 18.5787 - rmse: 4.3103 - mean_absolute_error: 3.5544
Epoch 00035: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 147ms/step - loss: 18.5787 - mean_squared_error: 18.5787 - rmse: 4.3103 - mean_absolute_error: 3.5544 - val_loss: 17.6584 - val_mean_squared_error: 17.6584 - val_rmse: 4.2022 - val_mean_absolute_error: 3.4886 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - l

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 18.4946 - mean_squared_error: 18.4946 - rmse: 4.3005 - mean_absolute_error: 3.4380
Epoch 00052: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 140ms/step - loss: 18.4946 - mean_squared_error: 18.4946 - rmse: 4.3005 - mean_absolute_error: 3.4380 - val_loss: 16.6170 - val_mean_squared_error: 16.6170 - val_rmse: 4.0764 - val_mean_absolute_error: 3.4328 - lr: 0.0025
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 18.4942 - mean_squared_error: 18.4942 - rmse: 4.3005 - mean_absolute_error: 3.4382
Epoch 00053: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 139ms/step - loss: 18.4942 - mean_squared_error: 18.4942 - rmse: 4.3005 - mean_absolute_error: 3.4382 - val_loss: 16.6258 - val_mean_squared_error: 16.6258 - val_rmse: 4.0775 - val_mean_absolute_error: 3.4332 - lr: 0.0025
Epoch 54/1000
1/1 [==============================] - ETA: 0s - l

Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 18.4860 - mean_squared_error: 18.4860 - rmse: 4.2995 - mean_absolute_error: 3.4570
Epoch 00070: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 125ms/step - loss: 18.4860 - mean_squared_error: 18.4860 - rmse: 4.2995 - mean_absolute_error: 3.4570 - val_loss: 16.8846 - val_mean_squared_error: 16.8846 - val_rmse: 4.1091 - val_mean_absolute_error: 3.4428 - lr: 0.0012
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 18.4860 - mean_squared_error: 18.4860 - rmse: 4.2995 - mean_absolute_error: 3.4574
Epoch 00071: val_loss did not improve from 15.30678
1/1 [==============================] - 0s 121ms/step - loss: 18.4860 - mean_squared_error: 18.4860 - rmse: 4.2995 - mean_absolute_error: 3.4574 - val_loss: 16.8876 - val_mean_squared_error: 16.8876 - val_rmse: 4.1095 - val_mean_absolute_error: 3.4429 - lr: 0.0012
Epoch 72/1000
1/1 [==============================] - ETA: 0s - l

...

Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 14.3322 - mean_squared_error: 14.3322 - rmse: 3.7858 - mean_absolute_error: 3.0847
Epoch 00053: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 262ms/step - loss: 14.3322 - mean_squared_error: 14.3322 - rmse: 3.7858 - mean_absolute_error: 3.0847 - val_loss: 16.1322 - val_mean_squared_error: 16.1322 - val_rmse: 4.0165 - val_mean_absolute_error: 3.2761 - lr: 0.0050
Epoch 54/1000
1/1 [==============================] - ETA: 0s - loss: 14.3301 - mean_squared_error: 14.3301 - rmse: 3.7855 - mean_absolute_error: 3.0860
Epoch 00054: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 269ms/step - loss: 14.3301 - mean_squared_error: 14.3301 - rmse: 3.7855 - mean_absolute_error: 3.0860 - val_loss: 16.1308 - val_mean_squared_error: 16.1308 - val_rmse: 4.0163 - val_mean_absolute_error: 3.2774 - lr: 0.0050
Epoch 55/1000
1/1 [==============================] - ETA: 0s - l

Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 14.3155 - mean_squared_error: 14.3155 - rmse: 3.7836 - mean_absolute_error: 3.1200
Epoch 00071: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 284ms/step - loss: 14.3155 - mean_squared_error: 14.3155 - rmse: 3.7836 - mean_absolute_error: 3.1200 - val_loss: 16.1431 - val_mean_squared_error: 16.1431 - val_rmse: 4.0178 - val_mean_absolute_error: 3.2935 - lr: 0.0025
Epoch 72/1000
1/1 [==============================] - ETA: 0s - loss: 14.3149 - mean_squared_error: 14.3149 - rmse: 3.7835 - mean_absolute_error: 3.1189
Epoch 00072: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 305ms/step - loss: 14.3149 - mean_squared_error: 14.3149 - rmse: 3.7835 - mean_absolute_error: 3.1189 - val_loss: 16.1415 - val_mean_squared_error: 16.1415 - val_rmse: 4.0176 - val_mean_absolute_error: 3.2929 - lr: 0.0025
Epoch 73/1000
1/1 [==============================] - ETA: 0s - l

Epoch 89/1000
1/1 [==============================] - ETA: 0s - loss: 14.3132 - mean_squared_error: 14.3132 - rmse: 3.7833 - mean_absolute_error: 3.1059
Epoch 00089: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 340ms/step - loss: 14.3132 - mean_squared_error: 14.3132 - rmse: 3.7833 - mean_absolute_error: 3.1059 - val_loss: 16.1311 - val_mean_squared_error: 16.1311 - val_rmse: 4.0164 - val_mean_absolute_error: 3.2868 - lr: 0.0012
Epoch 90/1000
1/1 [==============================] - ETA: 0s - loss: 14.3131 - mean_squared_error: 14.3131 - rmse: 3.7833 - mean_absolute_error: 3.1061
Epoch 00090: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 294ms/step - loss: 14.3131 - mean_squared_error: 14.3131 - rmse: 3.7833 - mean_absolute_error: 3.1061 - val_loss: 16.1313 - val_mean_squared_error: 16.1313 - val_rmse: 4.0164 - val_mean_absolute_error: 3.2869 - lr: 0.0012
Epoch 91/1000
1/1 [==============================] - ETA: 0s - l

Epoch 107/1000
1/1 [==============================] - ETA: 0s - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1107
Epoch 00107: val_loss did not improve from 16.12868

Epoch 00107: ReduceLROnPlateau reducing learning rate to 0.0006249999860301614.
1/1 [==============================] - 0s 278ms/step - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1107 - val_loss: 16.1345 - val_mean_squared_error: 16.1345 - val_rmse: 4.0168 - val_mean_absolute_error: 3.2893 - lr: 0.0012
Epoch 108/1000
1/1 [==============================] - ETA: 0s - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1109
Epoch 00108: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 349ms/step - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1109 - val_loss: 16.1345 - val_mean_squared_error: 16.1345 - val_rmse: 4.0168 - val_mean_absolute_error: 3

1/1 [==============================] - ETA: 0s - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1108
Epoch 00124: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 304ms/step - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1108 - val_loss: 16.1344 - val_mean_squared_error: 16.1344 - val_rmse: 4.0168 - val_mean_absolute_error: 3.2892 - lr: 6.2500e-04
Epoch 125/1000
1/1 [==============================] - ETA: 0s - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1108
Epoch 00125: val_loss did not improve from 16.12868
1/1 [==============================] - 0s 311ms/step - loss: 14.3126 - mean_squared_error: 14.3126 - rmse: 3.7832 - mean_absolute_error: 3.1108 - val_loss: 16.1343 - val_mean_squared_error: 16.1343 - val_rmse: 4.0168 - val_mean_absolute_error: 3.2892 - lr: 6.2500e-04
Epoch 126/1000
1/1 [==============================] - ETA: 0s - loss:

In [94]:
df_lstm2_2 = (df_lstm24.merge(df_lstm25, how='outer')).merge(df_lstm26, how='outer')

### blstm1

In [95]:
df_blstm11, history_blstm11 = single_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 0, 3, 4, X, y)
df_blstm12, history_blstm12 = single_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 3, 0, 4, X, y)
df_blstm13, history_blstm13 = single_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 4, 0, 3, X, y)

Model: "model_49"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_50 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 bidirectional (Bidirectiona  (None, 200)              138400    
 l)                                                              
                                                                 
 dense_101 (Dense)           (None, 1)                 201       
                                                                 
Total params: 138,601
Trainable params: 138,601
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
4/4 [==============================] - ETA: 0s - loss: 47.5712 - mean_squared_error: 47.5712 - rmse: 6.8972 - mean_absolute_error: 5.4813  
Epoch 00001: val_loss improved from inf to 14.55018, saving model to /tmp/blstm1.m5
4/4 [========

4/4 [==============================] - ETA: 0s - loss: 12.5224 - mean_squared_error: 12.5224 - rmse: 3.5387 - mean_absolute_error: 2.8722
Epoch 00016: val_loss did not improve from 11.92190
4/4 [==============================] - 1s 198ms/step - loss: 12.5224 - mean_squared_error: 12.5224 - rmse: 3.5387 - mean_absolute_error: 2.8722 - val_loss: 11.9260 - val_mean_squared_error: 11.9260 - val_rmse: 3.4534 - val_mean_absolute_error: 2.8519 - lr: 0.0100
Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 12.4857 - mean_squared_error: 12.4857 - rmse: 3.5335 - mean_absolute_error: 2.8457
Epoch 00017: val_loss did not improve from 11.92190
4/4 [==============================] - 1s 192ms/step - loss: 12.4857 - mean_squared_error: 12.4857 - rmse: 3.5335 - mean_absolute_error: 2.8457 - val_loss: 11.9916 - val_mean_squared_error: 11.9916 - val_rmse: 3.4629 - val_mean_absolute_error: 2.8326 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 12.4928 -

Epoch 33/1000
4/4 [==============================] - ETA: 0s - loss: 11.1433 - mean_squared_error: 11.1433 - rmse: 3.3382 - mean_absolute_error: 2.6827
Epoch 00033: val_loss improved from 10.54838 to 10.14582, saving model to /tmp/blstm1.m5
4/4 [==============================] - 1s 205ms/step - loss: 11.1433 - mean_squared_error: 11.1433 - rmse: 3.3382 - mean_absolute_error: 2.6827 - val_loss: 10.1458 - val_mean_squared_error: 10.1458 - val_rmse: 3.1853 - val_mean_absolute_error: 2.6453 - lr: 0.0100
Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 10.8176 - mean_squared_error: 10.8176 - rmse: 3.2890 - mean_absolute_error: 2.6973
Epoch 00034: val_loss did not improve from 10.14582
4/4 [==============================] - 1s 203ms/step - loss: 10.8176 - mean_squared_error: 10.8176 - rmse: 3.2890 - mean_absolute_error: 2.6973 - val_loss: 11.6606 - val_mean_squared_error: 11.6606 - val_rmse: 3.4148 - val_mean_absolute_error: 2.6227 - lr: 0.0100
Epoch 35/1000
4/4 [========

Epoch 50/1000
4/4 [==============================] - ETA: 0s - loss: 8.5855 - mean_squared_error: 8.5855 - rmse: 2.9301 - mean_absolute_error: 2.3457
Epoch 00050: val_loss did not improve from 6.68655
4/4 [==============================] - 1s 197ms/step - loss: 8.5855 - mean_squared_error: 8.5855 - rmse: 2.9301 - mean_absolute_error: 2.3457 - val_loss: 6.8613 - val_mean_squared_error: 6.8613 - val_rmse: 2.6194 - val_mean_absolute_error: 2.0300 - lr: 0.0100
Epoch 51/1000
4/4 [==============================] - ETA: 0s - loss: 7.9676 - mean_squared_error: 7.9676 - rmse: 2.8227 - mean_absolute_error: 2.3284
Epoch 00051: val_loss did not improve from 6.68655
4/4 [==============================] - 1s 204ms/step - loss: 7.9676 - mean_squared_error: 7.9676 - rmse: 2.8227 - mean_absolute_error: 2.3284 - val_loss: 7.4315 - val_mean_squared_error: 7.4315 - val_rmse: 2.7261 - val_mean_absolute_error: 2.0289 - lr: 0.0100
Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 7.0993 - 

Epoch 68/1000
4/4 [==============================] - ETA: 0s - loss: 6.8632 - mean_squared_error: 6.8632 - rmse: 2.6198 - mean_absolute_error: 2.0388
Epoch 00068: val_loss did not improve from 5.92878
4/4 [==============================] - 1s 193ms/step - loss: 6.8632 - mean_squared_error: 6.8632 - rmse: 2.6198 - mean_absolute_error: 2.0388 - val_loss: 6.6792 - val_mean_squared_error: 6.6792 - val_rmse: 2.5844 - val_mean_absolute_error: 2.0946 - lr: 0.0100
Epoch 69/1000
4/4 [==============================] - ETA: 0s - loss: 7.9244 - mean_squared_error: 7.9244 - rmse: 2.8150 - mean_absolute_error: 2.2175
Epoch 00069: val_loss did not improve from 5.92878
4/4 [==============================] - 1s 195ms/step - loss: 7.9244 - mean_squared_error: 7.9244 - rmse: 2.8150 - mean_absolute_error: 2.2175 - val_loss: 6.3567 - val_mean_squared_error: 6.3567 - val_rmse: 2.5213 - val_mean_absolute_error: 1.9035 - lr: 0.0100
Epoch 70/1000
4/4 [==============================] - ETA: 0s - loss: 7.1895 - 

...

Epoch 200/1000
2/2 [==============================] - ETA: 0s - loss: 8.0741 - mean_squared_error: 8.0741 - rmse: 2.8415 - mean_absolute_error: 2.2729
Epoch 00200: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 91ms/step - loss: 8.0741 - mean_squared_error: 8.0741 - rmse: 2.8415 - mean_absolute_error: 2.2729 - val_loss: 8.9529 - val_mean_squared_error: 8.9529 - val_rmse: 2.9921 - val_mean_absolute_error: 2.3791 - lr: 0.0025
Epoch 201/1000
2/2 [==============================] - ETA: 0s - loss: 7.8429 - mean_squared_error: 7.8429 - rmse: 2.8005 - mean_absolute_error: 2.2401
Epoch 00201: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 93ms/step - loss: 7.8429 - mean_squared_error: 7.8429 - rmse: 2.8005 - mean_absolute_error: 2.2401 - val_loss: 8.6883 - val_mean_squared_error: 8.6883 - val_rmse: 2.9476 - val_mean_absolute_error: 2.3335 - lr: 0.0025
Epoch 202/1000
2/2 [==============================] - ETA: 0s - loss: 7.5895 -

Epoch 218/1000
2/2 [==============================] - ETA: 0s - loss: 6.4920 - mean_squared_error: 6.4920 - rmse: 2.5479 - mean_absolute_error: 1.9754
Epoch 00218: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 105ms/step - loss: 6.4920 - mean_squared_error: 6.4920 - rmse: 2.5479 - mean_absolute_error: 1.9754 - val_loss: 8.7909 - val_mean_squared_error: 8.7909 - val_rmse: 2.9649 - val_mean_absolute_error: 2.2990 - lr: 0.0012
Epoch 219/1000
2/2 [==============================] - ETA: 0s - loss: 6.9327 - mean_squared_error: 6.9327 - rmse: 2.6330 - mean_absolute_error: 2.1290
Epoch 00219: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 91ms/step - loss: 6.9327 - mean_squared_error: 6.9327 - rmse: 2.6330 - mean_absolute_error: 2.1290 - val_loss: 8.9084 - val_mean_squared_error: 8.9084 - val_rmse: 2.9847 - val_mean_absolute_error: 2.2997 - lr: 0.0012
Epoch 220/1000
2/2 [==============================] - ETA: 0s - loss: 7.0369 

Epoch 236/1000
2/2 [==============================] - ETA: 0s - loss: 6.3655 - mean_squared_error: 6.3655 - rmse: 2.5230 - mean_absolute_error: 1.9964
Epoch 00236: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 94ms/step - loss: 6.3655 - mean_squared_error: 6.3655 - rmse: 2.5230 - mean_absolute_error: 1.9964 - val_loss: 7.5175 - val_mean_squared_error: 7.5175 - val_rmse: 2.7418 - val_mean_absolute_error: 2.1580 - lr: 6.2500e-04
Epoch 237/1000
2/2 [==============================] - ETA: 0s - loss: 6.2964 - mean_squared_error: 6.2964 - rmse: 2.5093 - mean_absolute_error: 1.9691
Epoch 00237: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 94ms/step - loss: 6.2964 - mean_squared_error: 6.2964 - rmse: 2.5093 - mean_absolute_error: 1.9691 - val_loss: 6.9466 - val_mean_squared_error: 6.9466 - val_rmse: 2.6356 - val_mean_absolute_error: 2.0823 - lr: 6.2500e-04
Epoch 238/1000
2/2 [==============================] - ETA: 0s - loss: 

Epoch 254/1000
2/2 [==============================] - ETA: 0s - loss: 6.2279 - mean_squared_error: 6.2279 - rmse: 2.4956 - mean_absolute_error: 1.9631
Epoch 00254: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 94ms/step - loss: 6.2279 - mean_squared_error: 6.2279 - rmse: 2.4956 - mean_absolute_error: 1.9631 - val_loss: 7.5884 - val_mean_squared_error: 7.5884 - val_rmse: 2.7547 - val_mean_absolute_error: 2.1638 - lr: 3.1250e-04
Epoch 255/1000
2/2 [==============================] - ETA: 0s - loss: 6.2127 - mean_squared_error: 6.2127 - rmse: 2.4925 - mean_absolute_error: 1.9616
Epoch 00255: val_loss did not improve from 5.78456
2/2 [==============================] - 0s 92ms/step - loss: 6.2127 - mean_squared_error: 6.2127 - rmse: 2.4925 - mean_absolute_error: 1.9616 - val_loss: 7.3083 - val_mean_squared_error: 7.3083 - val_rmse: 2.7034 - val_mean_absolute_error: 2.1309 - lr: 3.1250e-04
Epoch 256/1000
2/2 [==============================] - ETA: 0s - loss: 

5/5 [==============================] - 0s 15ms/step - loss: 21.3036 - mean_squared_error: 21.3036 - rmse: 4.6156 - mean_absolute_error: 3.4434


In [102]:
df_blstm1_1 = (df_blstm11.merge(df_blstm12, how='outer')).merge(df_blstm13, how='outer')

In [97]:
df_blstm14, history_blstm14 = double_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 0, 3, 4, X, y)
df_blstm15, history_blstm15 = double_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 0, 4, 3, X, y)
df_blstm16, history_blstm16 = double_cross_site(blstm1, 'blstm1', '/tmp/blstm1.m5', 0.01, 3, 4, 0, X, y)

Model: "model_52"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_53 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 bidirectional_3 (Bidirectio  (None, 200)              138400    
 nal)                                                            
                                                                 
 dense_104 (Dense)           (None, 1)                 201       
                                                                 
Total params: 138,601
Trainable params: 138,601
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
1/1 [==============================] - ETA: 0s - loss: 134.2448 - mean_squared_error: 134.2448 - rmse: 11.5864 - mean_absolute_error: 10.9868
Epoch 00001: val_loss improved from inf to 49.96326, saving model to /tmp/blstm1.m5
1/1 [======

Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 13.0779 - mean_squared_error: 13.0779 - rmse: 3.6163 - mean_absolute_error: 2.9414
Epoch 00017: val_loss improved from 16.22427 to 16.21765, saving model to /tmp/blstm1.m5
1/1 [==============================] - 0s 111ms/step - loss: 13.0779 - mean_squared_error: 13.0779 - rmse: 3.6163 - mean_absolute_error: 2.9414 - val_loss: 16.2176 - val_mean_squared_error: 16.2176 - val_rmse: 4.0271 - val_mean_absolute_error: 2.8236 - lr: 0.0100
Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 12.9960 - mean_squared_error: 12.9960 - rmse: 3.6050 - mean_absolute_error: 2.9727
Epoch 00018: val_loss improved from 16.21765 to 16.17862, saving model to /tmp/blstm1.m5
1/1 [==============================] - 0s 109ms/step - loss: 12.9960 - mean_squared_error: 12.9960 - rmse: 3.6050 - mean_absolute_error: 2.9727 - val_loss: 16.1786 - val_mean_squared_error: 16.1786 - val_rmse: 4.0223 - val_mean_absolute_error: 2.8905 - l

1/1 [==============================] - ETA: 0s - loss: 12.6750 - mean_squared_error: 12.6750 - rmse: 3.5602 - mean_absolute_error: 2.8937
Epoch 00034: val_loss did not improve from 16.17796
1/1 [==============================] - 0s 89ms/step - loss: 12.6750 - mean_squared_error: 12.6750 - rmse: 3.5602 - mean_absolute_error: 2.8937 - val_loss: 16.2381 - val_mean_squared_error: 16.2381 - val_rmse: 4.0297 - val_mean_absolute_error: 2.7749 - lr: 0.0100
Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 12.6111 - mean_squared_error: 12.6111 - rmse: 3.5512 - mean_absolute_error: 2.9011
Epoch 00035: val_loss did not improve from 16.17796
1/1 [==============================] - 0s 91ms/step - loss: 12.6111 - mean_squared_error: 12.6111 - rmse: 3.5512 - mean_absolute_error: 2.9011 - val_loss: 16.2023 - val_mean_squared_error: 16.2023 - val_rmse: 4.0252 - val_mean_absolute_error: 2.7973 - lr: 0.0100
Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 12.5468 - m

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 11.5334 - mean_squared_error: 11.5334 - rmse: 3.3961 - mean_absolute_error: 2.7989
Epoch 00052: val_loss did not improve from 16.16609
1/1 [==============================] - 0s 87ms/step - loss: 11.5334 - mean_squared_error: 11.5334 - rmse: 3.3961 - mean_absolute_error: 2.7989 - val_loss: 16.2977 - val_mean_squared_error: 16.2977 - val_rmse: 4.0370 - val_mean_absolute_error: 2.8613 - lr: 0.0100
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 11.4568 - mean_squared_error: 11.4568 - rmse: 3.3848 - mean_absolute_error: 2.7984
Epoch 00053: val_loss did not improve from 16.16609
1/1 [==============================] - 0s 88ms/step - loss: 11.4568 - mean_squared_error: 11.4568 - rmse: 3.3848 - mean_absolute_error: 2.7984 - val_loss: 16.3130 - val_mean_squared_error: 16.3130 - val_rmse: 4.0389 - val_mean_absolute_error: 2.8764 - lr: 0.0100
Epoch 54/1000
1/1 [==============================] - ETA: 0s - los

1/1 [==============================] - 0s 112ms/step - loss: 10.2397 - mean_squared_error: 10.2397 - rmse: 3.2000 - mean_absolute_error: 2.6120 - val_loss: 16.0291 - val_mean_squared_error: 16.0291 - val_rmse: 4.0036 - val_mean_absolute_error: 2.8543 - lr: 0.0100
Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 10.1328 - mean_squared_error: 10.1328 - rmse: 3.1832 - mean_absolute_error: 2.5652
Epoch 00070: val_loss did not improve from 16.02914
1/1 [==============================] - 0s 92ms/step - loss: 10.1328 - mean_squared_error: 10.1328 - rmse: 3.1832 - mean_absolute_error: 2.5652 - val_loss: 16.0320 - val_mean_squared_error: 16.0320 - val_rmse: 4.0040 - val_mean_absolute_error: 2.7997 - lr: 0.0100
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 10.1057 - mean_squared_error: 10.1057 - rmse: 3.1789 - mean_absolute_error: 2.5259
Epoch 00071: val_loss did not improve from 16.02914
1/1 [==============================] - 0s 85ms/step - loss: 10.10

...

Epoch 164/1000
1/1 [==============================] - ETA: 0s - loss: 7.8927 - mean_squared_error: 7.8927 - rmse: 2.8094 - mean_absolute_error: 2.2948
Epoch 00164: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 204ms/step - loss: 7.8927 - mean_squared_error: 7.8927 - rmse: 2.8094 - mean_absolute_error: 2.2948 - val_loss: 7.5092 - val_mean_squared_error: 7.5092 - val_rmse: 2.7403 - val_mean_absolute_error: 2.2587 - lr: 0.0050
Epoch 165/1000
1/1 [==============================] - ETA: 0s - loss: 8.1111 - mean_squared_error: 8.1111 - rmse: 2.8480 - mean_absolute_error: 2.3407
Epoch 00165: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 204ms/step - loss: 8.1111 - mean_squared_error: 8.1111 - rmse: 2.8480 - mean_absolute_error: 2.3407 - val_loss: 6.8562 - val_mean_squared_error: 6.8562 - val_rmse: 2.6184 - val_mean_absolute_error: 2.1818 - lr: 0.0050
Epoch 166/1000
1/1 [==============================] - ETA: 0s - loss: 7.4407

Epoch 182/1000
1/1 [==============================] - ETA: 0s - loss: 6.2362 - mean_squared_error: 6.2362 - rmse: 2.4972 - mean_absolute_error: 1.9440
Epoch 00182: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 199ms/step - loss: 6.2362 - mean_squared_error: 6.2362 - rmse: 2.4972 - mean_absolute_error: 1.9440 - val_loss: 6.4139 - val_mean_squared_error: 6.4139 - val_rmse: 2.5326 - val_mean_absolute_error: 2.0991 - lr: 0.0025
Epoch 183/1000
1/1 [==============================] - ETA: 0s - loss: 6.1457 - mean_squared_error: 6.1457 - rmse: 2.4790 - mean_absolute_error: 1.9404
Epoch 00183: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 193ms/step - loss: 6.1457 - mean_squared_error: 6.1457 - rmse: 2.4790 - mean_absolute_error: 1.9404 - val_loss: 6.5943 - val_mean_squared_error: 6.5943 - val_rmse: 2.5679 - val_mean_absolute_error: 2.1448 - lr: 0.0025
Epoch 184/1000
1/1 [==============================] - ETA: 0s - loss: 6.0696

Epoch 200/1000
1/1 [==============================] - ETA: 0s - loss: 5.6399 - mean_squared_error: 5.6399 - rmse: 2.3749 - mean_absolute_error: 1.8948
Epoch 00200: val_loss did not improve from 5.67811

Epoch 00200: ReduceLROnPlateau reducing learning rate to 0.0012499999720603228.
1/1 [==============================] - 0s 202ms/step - loss: 5.6399 - mean_squared_error: 5.6399 - rmse: 2.3749 - mean_absolute_error: 1.8948 - val_loss: 6.6338 - val_mean_squared_error: 6.6338 - val_rmse: 2.5756 - val_mean_absolute_error: 2.1053 - lr: 0.0025
Epoch 201/1000
1/1 [==============================] - ETA: 0s - loss: 5.6143 - mean_squared_error: 5.6143 - rmse: 2.3695 - mean_absolute_error: 1.8832
Epoch 00201: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 199ms/step - loss: 5.6143 - mean_squared_error: 5.6143 - rmse: 2.3695 - mean_absolute_error: 1.8832 - val_loss: 6.6064 - val_mean_squared_error: 6.6064 - val_rmse: 2.5703 - val_mean_absolute_error: 2.0956 - lr: 0.

Epoch 218/1000
1/1 [==============================] - ETA: 0s - loss: 5.4126 - mean_squared_error: 5.4126 - rmse: 2.3265 - mean_absolute_error: 1.8428
Epoch 00218: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 194ms/step - loss: 5.4126 - mean_squared_error: 5.4126 - rmse: 2.3265 - mean_absolute_error: 1.8428 - val_loss: 6.7406 - val_mean_squared_error: 6.7406 - val_rmse: 2.5963 - val_mean_absolute_error: 2.1218 - lr: 0.0012
Epoch 219/1000
1/1 [==============================] - ETA: 0s - loss: 5.4005 - mean_squared_error: 5.4005 - rmse: 2.3239 - mean_absolute_error: 1.8412
Epoch 00219: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 191ms/step - loss: 5.4005 - mean_squared_error: 5.4005 - rmse: 2.3239 - mean_absolute_error: 1.8412 - val_loss: 6.7654 - val_mean_squared_error: 6.7654 - val_rmse: 2.6010 - val_mean_absolute_error: 2.1248 - lr: 0.0012
Epoch 220/1000
1/1 [==============================] - ETA: 0s - loss: 5.3876

Epoch 236/1000
1/1 [==============================] - ETA: 0s - loss: 5.2842 - mean_squared_error: 5.2842 - rmse: 2.2987 - mean_absolute_error: 1.8192
Epoch 00236: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 207ms/step - loss: 5.2842 - mean_squared_error: 5.2842 - rmse: 2.2987 - mean_absolute_error: 1.8192 - val_loss: 6.8068 - val_mean_squared_error: 6.8068 - val_rmse: 2.6090 - val_mean_absolute_error: 2.1280 - lr: 6.2500e-04
Epoch 237/1000
1/1 [==============================] - ETA: 0s - loss: 5.2778 - mean_squared_error: 5.2778 - rmse: 2.2973 - mean_absolute_error: 1.8172
Epoch 00237: val_loss did not improve from 5.67811
1/1 [==============================] - 0s 195ms/step - loss: 5.2778 - mean_squared_error: 5.2778 - rmse: 2.2973 - mean_absolute_error: 1.8172 - val_loss: 6.8044 - val_mean_squared_error: 6.8044 - val_rmse: 2.6085 - val_mean_absolute_error: 2.1267 - lr: 6.2500e-04
Epoch 238/1000
1/1 [==============================] - ETA: 0s - loss

In [98]:
df_blstm1_2 = (df_blstm14.merge(df_blstm15, how='outer')).merge(df_blstm16, how='outer')

### blstm2

In [99]:
df_blstm21, history_blstm21 = single_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 0, 3, 4, X, y)
df_blstm22, history_blstm22 = single_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 3, 0, 4, X, y)
df_blstm23, history_blstm23 = single_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 4, 0, 3, X, y)

Model: "model_55"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_56 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 bidirectional_6 (Bidirectio  (None, 100, 200)         138400    
 nal)                                                            
                                                                 
 bidirectional_7 (Bidirectio  (None, 200)              240800    
 nal)                                                            
                                                                 
 dense_107 (Dense)           (None, 1)                 201       
                                                                 
Total params: 379,401
Trainable params: 379,401
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
4/4 [==============================] - 

4/4 [==============================] - ETA: 0s - loss: 13.4516 - mean_squared_error: 13.4516 - rmse: 3.6676 - mean_absolute_error: 3.0368
Epoch 00016: val_loss did not improve from 8.68419
4/4 [==============================] - 2s 489ms/step - loss: 13.4516 - mean_squared_error: 13.4516 - rmse: 3.6676 - mean_absolute_error: 3.0368 - val_loss: 8.8589 - val_mean_squared_error: 8.8589 - val_rmse: 2.9764 - val_mean_absolute_error: 2.3731 - lr: 0.0100
Epoch 17/1000
4/4 [==============================] - ETA: 0s - loss: 13.4708 - mean_squared_error: 13.4708 - rmse: 3.6703 - mean_absolute_error: 3.0288
Epoch 00017: val_loss did not improve from 8.68419
4/4 [==============================] - 2s 486ms/step - loss: 13.4708 - mean_squared_error: 13.4708 - rmse: 3.6703 - mean_absolute_error: 3.0288 - val_loss: 8.8861 - val_mean_squared_error: 8.8861 - val_rmse: 2.9810 - val_mean_absolute_error: 2.3826 - lr: 0.0100
Epoch 18/1000
4/4 [==============================] - ETA: 0s - loss: 13.4810 - mean_

4/4 [==============================] - ETA: 0s - loss: 12.9898 - mean_squared_error: 12.9898 - rmse: 3.6041 - mean_absolute_error: 2.9780
Epoch 00033: val_loss did not improve from 8.47908
4/4 [==============================] - 2s 487ms/step - loss: 12.9898 - mean_squared_error: 12.9898 - rmse: 3.6041 - mean_absolute_error: 2.9780 - val_loss: 8.7791 - val_mean_squared_error: 8.7791 - val_rmse: 2.9630 - val_mean_absolute_error: 2.4021 - lr: 0.0050
Epoch 34/1000
4/4 [==============================] - ETA: 0s - loss: 12.9188 - mean_squared_error: 12.9188 - rmse: 3.5943 - mean_absolute_error: 2.9852
Epoch 00034: val_loss improved from 8.47908 to 8.37345, saving model to /tmp/blstm2.m5
4/4 [==============================] - 2s 499ms/step - loss: 12.9188 - mean_squared_error: 12.9188 - rmse: 3.5943 - mean_absolute_error: 2.9852 - val_loss: 8.3735 - val_mean_squared_error: 8.3735 - val_rmse: 2.8937 - val_mean_absolute_error: 2.3095 - lr: 0.0050
Epoch 35/1000
4/4 [=============================

Epoch 50/1000
4/4 [==============================] - ETA: 0s - loss: 14.0662 - mean_squared_error: 14.0662 - rmse: 3.7505 - mean_absolute_error: 2.8414
Epoch 00050: val_loss did not improve from 5.46309
4/4 [==============================] - 2s 482ms/step - loss: 14.0662 - mean_squared_error: 14.0662 - rmse: 3.7505 - mean_absolute_error: 2.8414 - val_loss: 7.2509 - val_mean_squared_error: 7.2509 - val_rmse: 2.6928 - val_mean_absolute_error: 2.1852 - lr: 0.0050
Epoch 51/1000
4/4 [==============================] - ETA: 0s - loss: 11.7866 - mean_squared_error: 11.7866 - rmse: 3.4332 - mean_absolute_error: 2.9073
Epoch 00051: val_loss did not improve from 5.46309
4/4 [==============================] - 2s 496ms/step - loss: 11.7866 - mean_squared_error: 11.7866 - rmse: 3.4332 - mean_absolute_error: 2.9073 - val_loss: 8.1526 - val_mean_squared_error: 8.1526 - val_rmse: 2.8553 - val_mean_absolute_error: 2.3907 - lr: 0.0050
Epoch 52/1000
4/4 [==============================] - ETA: 0s - loss: 1

Epoch 68/1000
4/4 [==============================] - ETA: 0s - loss: 7.1579 - mean_squared_error: 7.1579 - rmse: 2.6754 - mean_absolute_error: 2.1109
Epoch 00068: val_loss improved from 5.30710 to 5.25456, saving model to /tmp/blstm2.m5
4/4 [==============================] - 2s 496ms/step - loss: 7.1579 - mean_squared_error: 7.1579 - rmse: 2.6754 - mean_absolute_error: 2.1109 - val_loss: 5.2546 - val_mean_squared_error: 5.2546 - val_rmse: 2.2923 - val_mean_absolute_error: 1.8687 - lr: 0.0050
Epoch 69/1000
4/4 [==============================] - ETA: 0s - loss: 6.9771 - mean_squared_error: 6.9771 - rmse: 2.6414 - mean_absolute_error: 2.0552
Epoch 00069: val_loss did not improve from 5.25456
4/4 [==============================] - 2s 481ms/step - loss: 6.9771 - mean_squared_error: 6.9771 - rmse: 2.6414 - mean_absolute_error: 2.0552 - val_loss: 5.5125 - val_mean_squared_error: 5.5125 - val_rmse: 2.3479 - val_mean_absolute_error: 1.9257 - lr: 0.0050
Epoch 70/1000
4/4 [=======================

...

Epoch 29/1000
2/2 [==============================] - ETA: 0s - loss: 13.2153 - mean_squared_error: 13.2153 - rmse: 3.6353 - mean_absolute_error: 3.0196
Epoch 00029: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 181ms/step - loss: 13.2153 - mean_squared_error: 13.2153 - rmse: 3.6353 - mean_absolute_error: 3.0196 - val_loss: 17.7345 - val_mean_squared_error: 17.7345 - val_rmse: 4.2112 - val_mean_absolute_error: 3.5415 - lr: 0.0050
Epoch 30/1000
2/2 [==============================] - ETA: 0s - loss: 13.1796 - mean_squared_error: 13.1796 - rmse: 3.6304 - mean_absolute_error: 2.9950
Epoch 00030: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 182ms/step - loss: 13.1796 - mean_squared_error: 13.1796 - rmse: 3.6304 - mean_absolute_error: 2.9950 - val_loss: 18.0920 - val_mean_squared_error: 18.0920 - val_rmse: 4.2535 - val_mean_absolute_error: 3.5577 - lr: 0.0050
Epoch 31/1000
2/2 [==============================] - ETA: 0s - l

Epoch 47/1000
2/2 [==============================] - ETA: 0s - loss: 13.1623 - mean_squared_error: 13.1623 - rmse: 3.6280 - mean_absolute_error: 2.9937
Epoch 00047: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 169ms/step - loss: 13.1623 - mean_squared_error: 13.1623 - rmse: 3.6280 - mean_absolute_error: 2.9937 - val_loss: 17.3176 - val_mean_squared_error: 17.3176 - val_rmse: 4.1614 - val_mean_absolute_error: 3.5195 - lr: 0.0050
Epoch 48/1000
2/2 [==============================] - ETA: 0s - loss: 13.2435 - mean_squared_error: 13.2435 - rmse: 3.6392 - mean_absolute_error: 3.0371
Epoch 00048: val_loss did not improve from 16.62710

Epoch 00048: ReduceLROnPlateau reducing learning rate to 0.0024999999441206455.
2/2 [==============================] - 1s 172ms/step - loss: 13.2435 - mean_squared_error: 13.2435 - rmse: 3.6392 - mean_absolute_error: 3.0371 - val_loss: 17.0759 - val_mean_squared_error: 17.0759 - val_rmse: 4.1323 - val_mean_absolute_error: 3.5

Epoch 65/1000
2/2 [==============================] - ETA: 0s - loss: 13.1555 - mean_squared_error: 13.1555 - rmse: 3.6270 - mean_absolute_error: 2.9806
Epoch 00065: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 181ms/step - loss: 13.1555 - mean_squared_error: 13.1555 - rmse: 3.6270 - mean_absolute_error: 2.9806 - val_loss: 17.6635 - val_mean_squared_error: 17.6635 - val_rmse: 4.2028 - val_mean_absolute_error: 3.5361 - lr: 0.0025
Epoch 66/1000
2/2 [==============================] - ETA: 0s - loss: 13.1434 - mean_squared_error: 13.1434 - rmse: 3.6254 - mean_absolute_error: 2.9955
Epoch 00066: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 177ms/step - loss: 13.1434 - mean_squared_error: 13.1434 - rmse: 3.6254 - mean_absolute_error: 2.9955 - val_loss: 17.4340 - val_mean_squared_error: 17.4340 - val_rmse: 4.1754 - val_mean_absolute_error: 3.5246 - lr: 0.0025
Epoch 67/1000
2/2 [==============================] - ETA: 0s - l

Epoch 83/1000
2/2 [==============================] - ETA: 0s - loss: 13.1238 - mean_squared_error: 13.1238 - rmse: 3.6227 - mean_absolute_error: 2.9689
Epoch 00083: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 181ms/step - loss: 13.1238 - mean_squared_error: 13.1238 - rmse: 3.6227 - mean_absolute_error: 2.9689 - val_loss: 17.9391 - val_mean_squared_error: 17.9391 - val_rmse: 4.2355 - val_mean_absolute_error: 3.5457 - lr: 0.0012
Epoch 84/1000
2/2 [==============================] - ETA: 0s - loss: 13.1154 - mean_squared_error: 13.1154 - rmse: 3.6215 - mean_absolute_error: 2.9705
Epoch 00084: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 177ms/step - loss: 13.1154 - mean_squared_error: 13.1154 - rmse: 3.6215 - mean_absolute_error: 2.9705 - val_loss: 17.8960 - val_mean_squared_error: 17.8960 - val_rmse: 4.2304 - val_mean_absolute_error: 3.5432 - lr: 0.0012
Epoch 85/1000
2/2 [==============================] - ETA: 0s - l

2/2 [==============================] - ETA: 0s - loss: 12.9693 - mean_squared_error: 12.9693 - rmse: 3.6013 - mean_absolute_error: 2.9755
Epoch 00100: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 180ms/step - loss: 12.9693 - mean_squared_error: 12.9693 - rmse: 3.6013 - mean_absolute_error: 2.9755 - val_loss: 17.5533 - val_mean_squared_error: 17.5533 - val_rmse: 4.1897 - val_mean_absolute_error: 3.5213 - lr: 6.2500e-04
Epoch 101/1000
2/2 [==============================] - ETA: 0s - loss: 12.9554 - mean_squared_error: 12.9554 - rmse: 3.5994 - mean_absolute_error: 2.9709
Epoch 00101: val_loss did not improve from 16.62710
2/2 [==============================] - 1s 172ms/step - loss: 12.9554 - mean_squared_error: 12.9554 - rmse: 3.5994 - mean_absolute_error: 2.9709 - val_loss: 17.5956 - val_mean_squared_error: 17.5956 - val_rmse: 4.1947 - val_mean_absolute_error: 3.5237 - lr: 6.2500e-04
Epoch 102/1000
2/2 [==============================] - ETA: 0s - loss:

In [103]:
df_blstm2_1 = (df_blstm21.merge(df_blstm22, how='outer')).merge(df_blstm23, how='outer')

In [101]:
df_blstm24, history_blstm24 = double_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 0, 3, 4, X, y)
df_blstm25, history_blstm25 = double_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 0, 4, 3, X, y)
df_blstm26, history_blstm26 = double_cross_site(blstm2, 'blstm2', '/tmp/blstm2.m5', 0.01, 3, 4, 0, X, y)

Model: "model_58"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_59 (InputLayer)       [(None, 100, 72)]         0         
                                                                 
 bidirectional_12 (Bidirecti  (None, 100, 200)         138400    
 onal)                                                           
                                                                 
 bidirectional_13 (Bidirecti  (None, 200)              240800    
 onal)                                                           
                                                                 
 dense_110 (Dense)           (None, 1)                 201       
                                                                 
Total params: 379,401
Trainable params: 379,401
Non-trainable params: 0
_________________________________________________________________
Epoch 1/1000
1/1 [==============================] - 

1/1 [==============================] - ETA: 0s - loss: 9.9566 - mean_squared_error: 9.9566 - rmse: 3.1554 - mean_absolute_error: 2.4249
Epoch 00016: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 171ms/step - loss: 9.9566 - mean_squared_error: 9.9566 - rmse: 3.1554 - mean_absolute_error: 2.4249 - val_loss: 21.4262 - val_mean_squared_error: 21.4262 - val_rmse: 4.6288 - val_mean_absolute_error: 3.5877 - lr: 0.0100
Epoch 17/1000
1/1 [==============================] - ETA: 0s - loss: 9.9949 - mean_squared_error: 9.9949 - rmse: 3.1615 - mean_absolute_error: 2.4465
Epoch 00017: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 162ms/step - loss: 9.9949 - mean_squared_error: 9.9949 - rmse: 3.1615 - mean_absolute_error: 2.4465 - val_loss: 21.2765 - val_mean_squared_error: 21.2765 - val_rmse: 4.6126 - val_mean_absolute_error: 3.5695 - lr: 0.0100
Epoch 18/1000
1/1 [==============================] - ETA: 0s - loss: 10.0089 - mean_sq

Epoch 34/1000
1/1 [==============================] - ETA: 0s - loss: 9.9068 - mean_squared_error: 9.9068 - rmse: 3.1475 - mean_absolute_error: 2.3894
Epoch 00034: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 164ms/step - loss: 9.9068 - mean_squared_error: 9.9068 - rmse: 3.1475 - mean_absolute_error: 2.3894 - val_loss: 23.0075 - val_mean_squared_error: 23.0075 - val_rmse: 4.7966 - val_mean_absolute_error: 3.7724 - lr: 0.0050
Epoch 35/1000
1/1 [==============================] - ETA: 0s - loss: 9.9099 - mean_squared_error: 9.9099 - rmse: 3.1480 - mean_absolute_error: 2.3920
Epoch 00035: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 169ms/step - loss: 9.9099 - mean_squared_error: 9.9099 - rmse: 3.1480 - mean_absolute_error: 2.3920 - val_loss: 22.8750 - val_mean_squared_error: 22.8750 - val_rmse: 4.7828 - val_mean_absolute_error: 3.7574 - lr: 0.0050
Epoch 36/1000
1/1 [==============================] - ETA: 0s - loss: 9.9

Epoch 52/1000
1/1 [==============================] - ETA: 0s - loss: 9.9019 - mean_squared_error: 9.9019 - rmse: 3.1467 - mean_absolute_error: 2.3840
Epoch 00052: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 169ms/step - loss: 9.9019 - mean_squared_error: 9.9019 - rmse: 3.1467 - mean_absolute_error: 2.3840 - val_loss: 23.7488 - val_mean_squared_error: 23.7488 - val_rmse: 4.8733 - val_mean_absolute_error: 3.8557 - lr: 0.0025
Epoch 53/1000
1/1 [==============================] - ETA: 0s - loss: 9.9013 - mean_squared_error: 9.9013 - rmse: 3.1466 - mean_absolute_error: 2.3842
Epoch 00053: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 158ms/step - loss: 9.9013 - mean_squared_error: 9.9013 - rmse: 3.1466 - mean_absolute_error: 2.3842 - val_loss: 23.6997 - val_mean_squared_error: 23.6997 - val_rmse: 4.8682 - val_mean_absolute_error: 3.8504 - lr: 0.0025
Epoch 54/1000
1/1 [==============================] - ETA: 0s - loss: 9.9

Epoch 70/1000
1/1 [==============================] - ETA: 0s - loss: 9.8965 - mean_squared_error: 9.8965 - rmse: 3.1459 - mean_absolute_error: 2.3848
Epoch 00070: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 202ms/step - loss: 9.8965 - mean_squared_error: 9.8965 - rmse: 3.1459 - mean_absolute_error: 2.3848 - val_loss: 23.4771 - val_mean_squared_error: 23.4771 - val_rmse: 4.8453 - val_mean_absolute_error: 3.8263 - lr: 0.0012
Epoch 71/1000
1/1 [==============================] - ETA: 0s - loss: 9.8963 - mean_squared_error: 9.8963 - rmse: 3.1458 - mean_absolute_error: 2.3846
Epoch 00071: val_loss did not improve from 13.37222
1/1 [==============================] - 0s 166ms/step - loss: 9.8963 - mean_squared_error: 9.8963 - rmse: 3.1458 - mean_absolute_error: 2.3846 - val_loss: 23.4943 - val_mean_squared_error: 23.4943 - val_rmse: 4.8471 - val_mean_absolute_error: 3.8282 - lr: 0.0012
Epoch 72/1000
1/1 [==============================] - ETA: 0s - loss: 9.8

...

Epoch 195/1000
1/1 [==============================] - ETA: 0s - loss: 5.5998 - mean_squared_error: 5.5998 - rmse: 2.3664 - mean_absolute_error: 1.8635
Epoch 00195: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 427ms/step - loss: 5.5998 - mean_squared_error: 5.5998 - rmse: 2.3664 - mean_absolute_error: 1.8635 - val_loss: 9.0739 - val_mean_squared_error: 9.0739 - val_rmse: 3.0123 - val_mean_absolute_error: 2.3857 - lr: 0.0100
Epoch 196/1000
1/1 [==============================] - ETA: 0s - loss: 6.5181 - mean_squared_error: 6.5181 - rmse: 2.5531 - mean_absolute_error: 1.9594
Epoch 00196: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 432ms/step - loss: 6.5181 - mean_squared_error: 6.5181 - rmse: 2.5531 - mean_absolute_error: 1.9594 - val_loss: 11.1002 - val_mean_squared_error: 11.1002 - val_rmse: 3.3317 - val_mean_absolute_error: 2.6575 - lr: 0.0100
Epoch 197/1000
1/1 [==============================] - ETA: 0s - loss: 5.07

Epoch 213/1000
1/1 [==============================] - ETA: 0s - loss: 4.1382 - mean_squared_error: 4.1382 - rmse: 2.0342 - mean_absolute_error: 1.6211
Epoch 00213: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 451ms/step - loss: 4.1382 - mean_squared_error: 4.1382 - rmse: 2.0342 - mean_absolute_error: 1.6211 - val_loss: 9.6077 - val_mean_squared_error: 9.6077 - val_rmse: 3.0996 - val_mean_absolute_error: 2.5009 - lr: 0.0050
Epoch 214/1000
1/1 [==============================] - ETA: 0s - loss: 4.4089 - mean_squared_error: 4.4089 - rmse: 2.0997 - mean_absolute_error: 1.6747
Epoch 00214: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 434ms/step - loss: 4.4089 - mean_squared_error: 4.4089 - rmse: 2.0997 - mean_absolute_error: 1.6747 - val_loss: 9.2149 - val_mean_squared_error: 9.2149 - val_rmse: 3.0356 - val_mean_absolute_error: 2.4324 - lr: 0.0050
Epoch 215/1000
1/1 [==============================] - ETA: 0s - loss: 4.2294

Epoch 231/1000
1/1 [==============================] - ETA: 0s - loss: 3.9086 - mean_squared_error: 3.9086 - rmse: 1.9770 - mean_absolute_error: 1.5423
Epoch 00231: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 436ms/step - loss: 3.9086 - mean_squared_error: 3.9086 - rmse: 1.9770 - mean_absolute_error: 1.5423 - val_loss: 8.5288 - val_mean_squared_error: 8.5288 - val_rmse: 2.9204 - val_mean_absolute_error: 2.3113 - lr: 0.0025
Epoch 232/1000
1/1 [==============================] - ETA: 0s - loss: 3.9147 - mean_squared_error: 3.9147 - rmse: 1.9786 - mean_absolute_error: 1.5502
Epoch 00232: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 420ms/step - loss: 3.9147 - mean_squared_error: 3.9147 - rmse: 1.9786 - mean_absolute_error: 1.5502 - val_loss: 8.4941 - val_mean_squared_error: 8.4941 - val_rmse: 2.9145 - val_mean_absolute_error: 2.3058 - lr: 0.0025
Epoch 233/1000
1/1 [==============================] - ETA: 0s - loss: 3.9101

Epoch 249/1000
1/1 [==============================] - ETA: 0s - loss: 3.7584 - mean_squared_error: 3.7584 - rmse: 1.9387 - mean_absolute_error: 1.5160
Epoch 00249: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 436ms/step - loss: 3.7584 - mean_squared_error: 3.7584 - rmse: 1.9387 - mean_absolute_error: 1.5160 - val_loss: 8.6091 - val_mean_squared_error: 8.6091 - val_rmse: 2.9341 - val_mean_absolute_error: 2.3060 - lr: 0.0012
Epoch 250/1000
1/1 [==============================] - ETA: 0s - loss: 3.7535 - mean_squared_error: 3.7535 - rmse: 1.9374 - mean_absolute_error: 1.5158
Epoch 00250: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 431ms/step - loss: 3.7535 - mean_squared_error: 3.7535 - rmse: 1.9374 - mean_absolute_error: 1.5158 - val_loss: 8.5790 - val_mean_squared_error: 8.5790 - val_rmse: 2.9290 - val_mean_absolute_error: 2.3014 - lr: 0.0012
Epoch 251/1000
1/1 [==============================] - ETA: 0s - loss: 3.7492

Epoch 267/1000
1/1 [==============================] - ETA: 0s - loss: 3.6801 - mean_squared_error: 3.6801 - rmse: 1.9184 - mean_absolute_error: 1.5037
Epoch 00267: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 430ms/step - loss: 3.6801 - mean_squared_error: 3.6801 - rmse: 1.9184 - mean_absolute_error: 1.5037 - val_loss: 8.5829 - val_mean_squared_error: 8.5829 - val_rmse: 2.9297 - val_mean_absolute_error: 2.2868 - lr: 6.2500e-04
Epoch 268/1000
1/1 [==============================] - ETA: 0s - loss: 3.6779 - mean_squared_error: 3.6779 - rmse: 1.9178 - mean_absolute_error: 1.5034
Epoch 00268: val_loss did not improve from 7.92880
1/1 [==============================] - 0s 441ms/step - loss: 3.6779 - mean_squared_error: 3.6779 - rmse: 1.9178 - mean_absolute_error: 1.5034 - val_loss: 8.5821 - val_mean_squared_error: 8.5821 - val_rmse: 2.9295 - val_mean_absolute_error: 2.2861 - lr: 6.2500e-04
Epoch 269/1000
1/1 [==============================] - ETA: 0s - loss

In [104]:
df_blstm2_2 = (df_blstm24.merge(df_blstm25, how='outer')).merge(df_blstm26, how='outer')

### lstm_fcn

In [71]:
df_fcn1, history_fcn1 = single_cross_site(lstm_fcn, 'lstm_fcn', '/tmp/fcn.m5', 0.01, 0, 3, 4, X, y)
df_fcn2, history_fcn2 = single_cross_site(lstm_fcn, 'lstm_fcn', '/tmp/fcn.m5', 0.01, 3, 0, 4, X, y)
df_fcn3, history_fcn3 = single_cross_site(lstm_fcn, 'lstm_fcn', '/tmp/fcn.m5', 0.01, 4, 0, 3, X, y)

Model: "model_34"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_35 (InputLayer)          [(None, 100, 72)]    0           []                               
                                                                                                  
 conv1d_100 (Conv1D)            (None, 100, 128)     73856       ['input_35[0][0]']               
                                                                                                  
 batch_normalization_45 (BatchN  (None, 100, 128)    512         ['conv1d_100[0][0]']             
 ormalization)                                                                                    
                                                                                                  
 activation_45 (Activation)     (None, 100, 128)     0           ['batch_normalization_45[0

Epoch 9/1000
4/4 [==============================] - ETA: 0s - loss: 5.1027 - mean_squared_error: 5.1027 - rmse: 2.2589 - mean_absolute_error: 1.8049
Epoch 00009: val_loss did not improve from 40609.30859
4/4 [==============================] - 1s 244ms/step - loss: 5.1027 - mean_squared_error: 5.1027 - rmse: 2.2589 - mean_absolute_error: 1.8049 - val_loss: 49036.9531 - val_mean_squared_error: 49036.9531 - val_rmse: 221.4429 - val_mean_absolute_error: 219.8163 - lr: 0.0100
Epoch 10/1000
4/4 [==============================] - ETA: 0s - loss: 5.4342 - mean_squared_error: 5.4342 - rmse: 2.3311 - mean_absolute_error: 1.8447
Epoch 00010: val_loss improved from 40609.30859 to 31212.90430, saving model to /tmp/fcn.m5
4/4 [==============================] - 1s 250ms/step - loss: 5.4342 - mean_squared_error: 5.4342 - rmse: 2.3311 - mean_absolute_error: 1.8447 - val_loss: 31212.9043 - val_mean_squared_error: 31212.9043 - val_rmse: 176.6717 - val_mean_absolute_error: 175.5993 - lr: 0.0100
Epoch 11/1

Epoch 26/1000
4/4 [==============================] - ETA: 0s - loss: 1.7410 - mean_squared_error: 1.7410 - rmse: 1.3195 - mean_absolute_error: 1.0519
Epoch 00026: val_loss did not improve from 678.75598
4/4 [==============================] - 1s 228ms/step - loss: 1.7410 - mean_squared_error: 1.7410 - rmse: 1.3195 - mean_absolute_error: 1.0519 - val_loss: 1186.7461 - val_mean_squared_error: 1186.7461 - val_rmse: 34.4492 - val_mean_absolute_error: 33.8942 - lr: 0.0100
Epoch 27/1000
4/4 [==============================] - ETA: 0s - loss: 1.6216 - mean_squared_error: 1.6216 - rmse: 1.2734 - mean_absolute_error: 1.0006
Epoch 00027: val_loss did not improve from 678.75598
4/4 [==============================] - 1s 234ms/step - loss: 1.6216 - mean_squared_error: 1.6216 - rmse: 1.2734 - mean_absolute_error: 1.0006 - val_loss: 764.7416 - val_mean_squared_error: 764.7416 - val_rmse: 27.6540 - val_mean_absolute_error: 27.2050 - lr: 0.0100
Epoch 28/1000
4/4 [==============================] - ETA: 0s

Epoch 61/1000
4/4 [==============================] - ETA: 0s - loss: 0.5493 - mean_squared_error: 0.5493 - rmse: 0.7411 - mean_absolute_error: 0.5774
Epoch 00061: val_loss did not improve from 10.75844
4/4 [==============================] - 1s 227ms/step - loss: 0.5493 - mean_squared_error: 0.5493 - rmse: 0.7411 - mean_absolute_error: 0.5774 - val_loss: 20.4526 - val_mean_squared_error: 20.4526 - val_rmse: 4.5225 - val_mean_absolute_error: 3.8450 - lr: 0.0100
Epoch 62/1000
4/4 [==============================] - ETA: 0s - loss: 0.4166 - mean_squared_error: 0.4166 - rmse: 0.6454 - mean_absolute_error: 0.4595
Epoch 00062: val_loss did not improve from 10.75844
4/4 [==============================] - 1s 233ms/step - loss: 0.4166 - mean_squared_error: 0.4166 - rmse: 0.6454 - mean_absolute_error: 0.4595 - val_loss: 10.8686 - val_mean_squared_error: 10.8686 - val_rmse: 3.2968 - val_mean_absolute_error: 2.5567 - lr: 0.0100
Epoch 63/1000
4/4 [==============================] - ETA: 0s - loss: 0.5

Epoch 79/1000
4/4 [==============================] - ETA: 0s - loss: 0.4064 - mean_squared_error: 0.4064 - rmse: 0.6375 - mean_absolute_error: 0.4772
Epoch 00079: val_loss did not improve from 8.60592
4/4 [==============================] - 1s 229ms/step - loss: 0.4064 - mean_squared_error: 0.4064 - rmse: 0.6375 - mean_absolute_error: 0.4772 - val_loss: 9.3515 - val_mean_squared_error: 9.3515 - val_rmse: 3.0580 - val_mean_absolute_error: 2.3511 - lr: 0.0100
Epoch 80/1000
4/4 [==============================] - ETA: 0s - loss: 0.3572 - mean_squared_error: 0.3572 - rmse: 0.5976 - mean_absolute_error: 0.4744
Epoch 00080: val_loss did not improve from 8.60592
4/4 [==============================] - 1s 228ms/step - loss: 0.3572 - mean_squared_error: 0.3572 - rmse: 0.5976 - mean_absolute_error: 0.4744 - val_loss: 12.3860 - val_mean_squared_error: 12.3860 - val_rmse: 3.5194 - val_mean_absolute_error: 2.6999 - lr: 0.0100
Epoch 81/1000
4/4 [==============================] - ETA: 0s - loss: 0.3064 

...

Epoch 285/1000
2/2 [==============================] - ETA: 0s - loss: 0.5563 - mean_squared_error: 0.5563 - rmse: 0.7459 - mean_absolute_error: 0.5614
Epoch 00285: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 109ms/step - loss: 0.5563 - mean_squared_error: 0.5563 - rmse: 0.7459 - mean_absolute_error: 0.5614 - val_loss: 5.1747 - val_mean_squared_error: 5.1747 - val_rmse: 2.2748 - val_mean_absolute_error: 1.8030 - lr: 3.9062e-05
Epoch 286/1000
2/2 [==============================] - ETA: 0s - loss: 0.9429 - mean_squared_error: 0.9429 - rmse: 0.9710 - mean_absolute_error: 0.7336
Epoch 00286: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 107ms/step - loss: 0.9429 - mean_squared_error: 0.9429 - rmse: 0.9710 - mean_absolute_error: 0.7336 - val_loss: 5.2298 - val_mean_squared_error: 5.2298 - val_rmse: 2.2869 - val_mean_absolute_error: 1.8285 - lr: 3.9062e-05
Epoch 287/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 303/1000
2/2 [==============================] - ETA: 0s - loss: 0.4946 - mean_squared_error: 0.4946 - rmse: 0.7033 - mean_absolute_error: 0.5482
Epoch 00303: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 106ms/step - loss: 0.4946 - mean_squared_error: 0.4946 - rmse: 0.7033 - mean_absolute_error: 0.5482 - val_loss: 5.4019 - val_mean_squared_error: 5.4019 - val_rmse: 2.3242 - val_mean_absolute_error: 1.8994 - lr: 1.9531e-05
Epoch 304/1000
2/2 [==============================] - ETA: 0s - loss: 0.4739 - mean_squared_error: 0.4739 - rmse: 0.6884 - mean_absolute_error: 0.5524
Epoch 00304: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 109ms/step - loss: 0.4739 - mean_squared_error: 0.4739 - rmse: 0.6884 - mean_absolute_error: 0.5524 - val_loss: 5.3678 - val_mean_squared_error: 5.3678 - val_rmse: 2.3169 - val_mean_absolute_error: 1.8890 - lr: 1.9531e-05
Epoch 305/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 321/1000
2/2 [==============================] - ETA: 0s - loss: 0.4967 - mean_squared_error: 0.4967 - rmse: 0.7048 - mean_absolute_error: 0.5724
Epoch 00321: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 112ms/step - loss: 0.4967 - mean_squared_error: 0.4967 - rmse: 0.7048 - mean_absolute_error: 0.5724 - val_loss: 5.2093 - val_mean_squared_error: 5.2093 - val_rmse: 2.2824 - val_mean_absolute_error: 1.8065 - lr: 9.7656e-06
Epoch 322/1000
2/2 [==============================] - ETA: 0s - loss: 0.5266 - mean_squared_error: 0.5266 - rmse: 0.7257 - mean_absolute_error: 0.5790
Epoch 00322: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 104ms/step - loss: 0.5266 - mean_squared_error: 0.5266 - rmse: 0.7257 - mean_absolute_error: 0.5790 - val_loss: 5.2118 - val_mean_squared_error: 5.2118 - val_rmse: 2.2829 - val_mean_absolute_error: 1.8072 - lr: 9.7656e-06
Epoch 323/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 339/1000
2/2 [==============================] - ETA: 0s - loss: 0.5134 - mean_squared_error: 0.5134 - rmse: 0.7165 - mean_absolute_error: 0.5617
Epoch 00339: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 103ms/step - loss: 0.5134 - mean_squared_error: 0.5134 - rmse: 0.7165 - mean_absolute_error: 0.5617 - val_loss: 5.1394 - val_mean_squared_error: 5.1394 - val_rmse: 2.2670 - val_mean_absolute_error: 1.7953 - lr: 4.8828e-06
Epoch 340/1000
2/2 [==============================] - ETA: 0s - loss: 0.6522 - mean_squared_error: 0.6522 - rmse: 0.8076 - mean_absolute_error: 0.6288
Epoch 00340: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 108ms/step - loss: 0.6522 - mean_squared_error: 0.6522 - rmse: 0.8076 - mean_absolute_error: 0.6288 - val_loss: 5.1321 - val_mean_squared_error: 5.1321 - val_rmse: 2.2654 - val_mean_absolute_error: 1.7909 - lr: 4.8828e-06
Epoch 341/1000
2/2 [==============================] - ETA: 0s - loss

Epoch 357/1000
2/2 [==============================] - ETA: 0s - loss: 0.5830 - mean_squared_error: 0.5830 - rmse: 0.7636 - mean_absolute_error: 0.6115
Epoch 00357: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 102ms/step - loss: 0.5830 - mean_squared_error: 0.5830 - rmse: 0.7636 - mean_absolute_error: 0.6115 - val_loss: 5.1086 - val_mean_squared_error: 5.1086 - val_rmse: 2.2602 - val_mean_absolute_error: 1.7796 - lr: 2.4414e-06
Epoch 358/1000
2/2 [==============================] - ETA: 0s - loss: 0.7787 - mean_squared_error: 0.7787 - rmse: 0.8824 - mean_absolute_error: 0.6552
Epoch 00358: val_loss did not improve from 4.89283
2/2 [==============================] - 0s 106ms/step - loss: 0.7787 - mean_squared_error: 0.7787 - rmse: 0.8824 - mean_absolute_error: 0.6552 - val_loss: 5.1102 - val_mean_squared_error: 5.1102 - val_rmse: 2.2606 - val_mean_absolute_error: 1.7798 - lr: 2.4414e-06
Epoch 359/1000
2/2 [==============================] - ETA: 0s - loss

In [72]:
df_fcn = (df_fcn1.merge(df_fcn2, how='outer')).merge(df_fcn3, how='outer')

In [157]:
def to_arr(dict):
    lists = dict.items()
    x,y = zip(*lists)
    arr = np.array(y)
    return arr

In [171]:
to_arr(results_1_3)[0,:]          

array([11.16009808,  3.34067321,  2.61717224])

In [75]:
df_lenet


Model  Train_site  Test_site Metric      Value
0   cnn_lenet           0          0    MSE  13.840021
1   cnn_lenet           0          0   RMSE   3.720218
2   cnn_lenet           0          0    MAE   2.866733
3   cnn_lenet           0          0   coef   0.312581
4   cnn_lenet           0          3    MSE  15.715021
5   cnn_lenet           0          3   RMSE   3.964218
6   cnn_lenet           0          3    MAE   2.945293
7   cnn_lenet           0          3   coef   0.245997
8   cnn_lenet           0          4    MSE  15.704589
9   cnn_lenet           0          4   RMSE   3.962902
10  cnn_lenet           0          4    MAE   3.019663
11  cnn_lenet           0          4   coef   0.112425
12  cnn_lenet           3          3    MSE  13.166924
13  cnn_lenet           3          3   RMSE   3.628626
14  cnn_lenet           3          3    MAE   2.773962
15  cnn_lenet           3          3   coef   0.085063
16  cnn_lenet           3          0    MSE  11.322652
17  cnn_lenet           3          0   RMSE   3.364915
18  cnn_lenet           3          0    MAE   2.822765
19  cnn_lenet           3          0   coef   0.238810
20  cnn_lenet           3          4    MSE  11.169086
21  cnn_lenet           3          4   RMSE   3.342018
22  cnn_lenet           3          4    MAE   2.859704
23  cnn_lenet           3          4   coef   0.346945
24  cnn_lenet           4          4    MSE  12.285432
25  cnn_lenet           4          4   RMSE   3.505058
26  cnn_lenet           4          4    MAE   2.955604
27  cnn_lenet           4          4   coef   0.395645
28  cnn_lenet           4          0    MSE  12.876002
29  cnn_lenet           4          0   RMSE   3.588315
30  cnn_lenet           4          0    MAE   3.063138
31  cnn_lenet           4          0   coef   0.195917
32  cnn_lenet           4          3    MSE  11.253750
33  cnn_lenet           4          3   RMSE   3.354661
34  cnn_lenet           4          3    MAE   2.876251
35  cnn_lenet           4          3   coef   0.341190